In [1]:
from rdflib import Graph
from tqdm import tqdm
from datasets import load_from_disk

import pandas as pd
import re

In [2]:
prefix = '''@prefix xsd: <http://www.w3.org/2001/XMLSchema#> .
@prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> .
@prefix rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> .
@prefix dbo: <http://dbpedia.org/ontology/> .
@prefix dct: <http://purl.org/dc/terms/> .
@prefix owl: <http://www.w3.org/2002/07/owl#> .
@prefix wd: <https://www.wikidata.org/wiki/> .
@prefix lexid-s: <https://w3id.org/lex-id/schema/> .
@prefix lexid: <https://w3id.org/lex-id/data/> .

'''

In [3]:
from rdflib import Graph, Namespace, URIRef
from rdflib.namespace import XSD, RDFS, RDF, OWL
from rdflib.exceptions import ParserError


def is_valid_triples(triple_str):
    ttl = prefix
    ttl += triple_str
    
#     print(ttl)
    
    g = Graph()
    DBO = Namespace("http://dbpedia.org/ontology/")
    DCT = Namespace("http://purl.org/dc/terms/")
    WD = Namespace("https://www.wikidata.org/wiki/")
    LEXID_S = Namespace("https://w3id.org/lex-id/schema/")
    LEXID = Namespace("https://w3id.org/lex-id/data/")

    g.bind("xsd", XSD)
    g.bind("rdfs", RDFS)
    g.bind("rdf", RDF)
    g.bind("dbo", DBO)
    g.bind("dct", DCT)
    g.bind("owl", OWL)
    g.bind("wd", WD)
    g.bind("lexid-s", LEXID_S)
    g.bind("lexid", LEXID)
    
    try:
        g.parse(data=ttl, format="turtle")
        return True
    except:
        return False

In [4]:
from rdflib import Graph, Namespace, URIRef
from rdflib.namespace import XSD, RDFS, RDF, OWL
from rdflib.exceptions import ParserError


def is_valid_ttl(triple_str):
    g = Graph()
    DBO = Namespace("http://dbpedia.org/ontology/")
    DCT = Namespace("http://purl.org/dc/terms/")
    WD = Namespace("https://www.wikidata.org/wiki/")
    LEXID_S = Namespace("https://w3id.org/lex-id/schema/")
    LEXID = Namespace("https://w3id.org/lex-id/data/")

    g.bind("xsd", XSD)
    g.bind("rdfs", RDFS)
    g.bind("rdf", RDF)
    g.bind("dbo", DBO)
    g.bind("dct", DCT)
    g.bind("owl", OWL)
    g.bind("wd", WD)
    g.bind("lexid-s", LEXID_S)
    g.bind("lexid", LEXID)
    
    try:
        g.parse(data=triple_str, format="turtle")
#         for subj, pred, obj in g:
#             print(f"Subject: {subj}, Predicate: {pred}, Object: {obj}")
        return True
    except:
        return False

In [34]:
is_valid_ttl(cc_gemma.at[0, '1'])

True

In [5]:
def evaluate_ttl(ttl_pred, ttl_gold):
    g_pred = Graph()
    g_pred.parse(data=ttl_pred, format="turtle")

    g_gold = Graph()
    g_gold.parse(data=ttl_gold, format="turtle")

    g_pred_total = len(g_pred)
    g_gold_total = len(g_gold)

    tp = len(set(g_pred).intersection(set(g_gold)))

    fp = g_pred_total - tp
    fn = g_gold_total - tp
    
    if tp + fp == 0:
        p = 0
    else:
        p = tp / (tp + fp)
        
    if tp + fn == 0:
        r = 0
    else:
        r = tp / (tp + fn)
    
    if p + r == 0:
        f1 = 0
    else:
        f1 = (2 * p * r)/ (p + r)
    
    return tp, fp, fn, p, r, f1

In [34]:
from rdflib import Graph, Namespace, Literal

def literals_case_insensitive_equal(lit1, lit2):
    return str(lit1).lower() == str(lit2).lower()

def triple_case_insensitive_equal(triple1, triple2):
    return (
        triple1[0] == triple2[0] and
        triple1[1] == triple2[1] and
        (
            (isinstance(triple1[2], Literal) and isinstance(triple2[2], Literal) and literals_case_insensitive_equal(triple1[2], triple2[2])) or
            (not isinstance(triple1[2], Literal) and not isinstance(triple2[2], Literal) and triple1[2] == triple2[2])
        )
    )

def evaluate_ttl_case_insensitive(ttl_pred, ttl_gold):
    g_pred = Graph()
    g_pred.parse(data=ttl_pred, format="turtle")

    g_gold = Graph()
    g_gold.parse(data=ttl_gold, format="turtle")

    g_pred_total = len(g_pred)
    g_gold_total = len(g_gold)

    tp = 0
    for triple in g_pred:
        if any(triple_case_insensitive_equal(triple, gold_triple) for gold_triple in g_gold):
            tp += 1

    fp = g_pred_total - tp
    fn = g_gold_total - tp

    if tp + fp == 0:
        p = 0
    else:
        p = round(tp / (tp + fp), 3)
        
    if tp + fn == 0:
        r = 0
    else:
        r = round(tp / (tp + fn), 3)
    
    if p + r == 0:
        f1 = 0
    else:
        f1 = round((2 * p * r) / (p + r), 3)
    
    return tp, fp, fn, p, r, f1

# Closing

In [44]:
results = pd.DataFrame()
results = pd.DataFrame(columns=['regulatory'
                                , 'cfg_p_1'
                                , 'cfg_r_1'
                                , 'cfg_f1_1'
                                , 'cfg_p_2'
                                , 'cfg_r_2'
                                , 'cfg_f1_2'
                                , 'cfcl_p_1'
                                , 'cfl_r_1'
                                , 'cfl_f1_1'
                                , 'cfl_p_2'
                                , 'cfl_r_2'
                                , 'cfl_f1_2'
                                , 'cfp_p_1'
                                , 'cfp_r_1'
                                , 'cfp_f1_1'
                                , 'cfp_p_2'
                                , 'cfp_r_2'
                                , 'cfp_f1_2'
                               ])

In [27]:
def test_1(name, df, dataset, shot, output):
    print('tes')
    
    cnt = 0
    tp_s = 0
    fp_s = 0
    fn_s = 0
    tp_i = 0
    fp_i = 0
    fn_i = 0
    
    for i in range(len(df)):
        reg = df.at[i, 'regulatory']
        ttl_pred = df.at[i, f'ttl_{shot}']
        ttl_test = prefix + dataset[i]['triples']
        
        tp, fp, fn, p, r, f1 = evaluate_ttl(ttl_pred, ttl_test)
        tp_s += tp
        fp_s += fp
        fn_s += fn
        
        results.at[i, 'regulatory'] = reg
        results.at[i, f'{name}_p_{shot}'] = p
        results.at[i, f'{name}_r_{shot}'] = r
        results.at[i, f'{name}_f1_{shot}'] = f1
        
        print(cnt, reg)
        print(f'Case Sensitive   : P: {p} || R: {r} || F1: {f1}')     
        
        tp, fp, fn, p, r, f1 = evaluate_ttl_case_insensitive(ttl_pred, ttl_test)
        tp_i += tp
        fp_i += fp
        fn_i += fn
        
        print(f'Case Insensitive : P: {p} || R: {r} || F1: {f1}') 
        
        cnt += 1
        
        if cnt % 100 == 0:
            results.to_csv(output)
            
    results.to_csv(output)
        
    p_s = tp_s / (tp_s + fp_s)
    r_s = tp_s / (tp_s + fn_s)
    f1_s = (2 * p_s * r_s)/ (p_s + r_s)
    
    p_i = tp_i / (tp_i + fp_i)
    r_i = tp_i / (tp_i + fn_i)
    f1_i = (2 * p_i * r_i)/ (p_i + r_i)
    
    print()
    print('####################################################')
    print()
    print(f'{name} {shot} Shot')

    print()
    print('Case Sensitive')
    print(f'Precision: {p_s}')    
    print(f'Recall: {r_s}')              
    print(f'F1 Score: {f1_s}') 
    
    print()
    print('Case Insensitive')
    print(f'Precision: {p_i}')    
    print(f'Recall: {r_i}')              
    print(f'F1 Score: {f1_i}') 

In [43]:
test_closing_name = "dataset-surface-info/new-closing/new-closing-1"
test_closing = load_from_disk(test_closing_name)
len(test_closing)

2640

In [47]:
cf_gemma = pd.read_csv('results/new/CF_gemma_post.csv')
cf_llama = pd.read_csv('results/new/CF_llama_post.csv')
cf_phi = pd.read_csv('results/new/CF_phi_post.csv')

In [48]:
test_1('cfg', cf_gemma, test_closing, '1', 'results/metrics_cf.csv')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.5263157894736842 || R: 0.625 || F1: 0.5714285714285714
Case Insensitive : P: 0.526 || R: 0.625 || F1: 0.571
1 Permen_KP_2013_5
Case Sensitive   : P: 0.5263157894736842 || R: 0.7692307692307693 || F1: 0.625
Case Insensitive : P: 0.526 || R: 0.769 || F1: 0.625
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.3157894736842105 || R: 0.6666666666666666 || F1: 0.42857142857142855
Case Insensitive : P: 0.316 || R: 0.667 || F1: 0.429
3 Permen_Par_2015_14
Case Sensitive   : P: 0.6842105263157895 || R: 1.0 || F1: 0.8125000000000001
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
4 Perpres_2019_67
Case Sensitive   : P: 0.6842105263157895 || R: 0.6842105263157895 || F1: 0.6842105263157895
Case Insensitive : P: 0.684 || R: 0.684 || F1: 0.684
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.05263157894736842 || R: 0.07692307692307693 || F1: 0.0625
Case Insensitive : P: 0.053 || R: 0.077 || F1: 0.063
6 Perkab_Tabalong_2010_09
Case Sensitive   : 

74 Permen_PR_2009_03
Case Sensitive   : P: 0.3684210526315789 || R: 1.0 || F1: 0.5384615384615384
Case Insensitive : P: 0.368 || R: 1.0 || F1: 0.538
75 Peraturan_Polri_2012_4
Case Sensitive   : P: 0.5789473684210527 || R: 0.9166666666666666 || F1: 0.7096774193548387
Case Insensitive : P: 0.579 || R: 0.917 || F1: 0.71
76 Permen_Perin_2012_11
Case Sensitive   : P: 0.5789473684210527 || R: 0.9166666666666666 || F1: 0.7096774193548387
Case Insensitive : P: 0.579 || R: 0.917 || F1: 0.71
77 Perkab_Sleman_2012_9
Case Sensitive   : P: 1.0 || R: 1.0 || F1: 1.0
Case Insensitive : P: 1.0 || R: 1.0 || F1: 1.0
78 PP_1990_59
Case Sensitive   : P: 0.3157894736842105 || R: 1.0 || F1: 0.4799999999999999
Case Insensitive : P: 0.316 || R: 1.0 || F1: 0.48
79 Permen_Agama_2016_21
Case Sensitive   : P: 0.6842105263157895 || R: 0.6842105263157895 || F1: 0.6842105263157895
Case Insensitive : P: 0.684 || R: 0.684 || F1: 0.684
80 Permen_PANRB_2018_15
Case Sensitive   : P: 0.3684210526315789 || R: 0.368421052631

155 PP_2016_10
Case Sensitive   : P: 0.631578947368421 || R: 0.8 || F1: 0.7058823529411765
Case Insensitive : P: 0.632 || R: 0.8 || F1: 0.706
156 UU_1954_66
Case Sensitive   : P: 0.041666666666666664 || R: 1.0 || F1: 0.07999999999999999
Case Insensitive : P: 0.042 || R: 1.0 || F1: 0.081
157 Permen_Pora_2017_12
Case Sensitive   : P: 0.6842105263157895 || R: 0.6842105263157895 || F1: 0.6842105263157895
Case Insensitive : P: 0.684 || R: 0.684 || F1: 0.684
158 Permen_Keu_2010_243
Case Sensitive   : P: 0.5789473684210527 || R: 0.9166666666666666 || F1: 0.7096774193548387
Case Insensitive : P: 0.579 || R: 0.917 || F1: 0.71
159 Perkab_Indramayu_1998_16
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
160 Perprov_Gorontalo_2007_02
Case Sensitive   : P: 0.3684210526315789 || R: 0.4117647058823529 || F1: 0.3888888888888889
Case Insensitive : P: 0.368 || R: 0.412 || F1: 0.389
161 Permen_Han_2014_83
Case Sensitive   : P: 0.6842105263157895 || R: 1.0 || F1: 

231 Perkab_Kotabaru_2012_13
Case Sensitive   : P: 0.5263157894736842 || R: 0.7692307692307693 || F1: 0.625
Case Insensitive : P: 0.526 || R: 0.769 || F1: 0.625
232 UU_2008_50
Case Sensitive   : P: 0.05263157894736842 || R: 1.0 || F1: 0.1
Case Insensitive : P: 0.053 || R: 1.0 || F1: 0.101
233 Peraturan_PPATK_2011_14
Case Sensitive   : P: 0.42105263157894735 || R: 0.8 || F1: 0.5517241379310345
Case Insensitive : P: 0.474 || R: 0.9 || F1: 0.621
234 Permen_LHK_2019_56
Case Sensitive   : P: 0.9230769230769231 || R: 0.75 || F1: 0.8275862068965517
Case Insensitive : P: 1.0 || R: 0.812 || F1: 0.896
235 Permen_PR_2011_09
Case Sensitive   : P: 0.6842105263157895 || R: 1.0 || F1: 0.8125000000000001
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
236 Permen_Dagri_2013_67
Case Sensitive   : P: 0.6842105263157895 || R: 1.0 || F1: 0.8125000000000001
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
237 Perprov_Kalbar_2001_7
Case Sensitive   : P: 0.2631578947368421 || R: 0.45454545454545453 || F1:

327 Perpres_2012_69
Case Sensitive   : P: 0.631578947368421 || R: 1.0 || F1: 0.7741935483870968
Case Insensitive : P: 0.632 || R: 1.0 || F1: 0.775
328 Permen_Humham_2013_3
Case Sensitive   : P: 0.7333333333333333 || R: 1.0 || F1: 0.846153846153846
Case Insensitive : P: 0.733 || R: 1.0 || F1: 0.846
329 Permen_Parekraf_2014_22
Case Sensitive   : P: 0.5789473684210527 || R: 0.8461538461538461 || F1: 0.6875
Case Insensitive : P: 0.579 || R: 0.846 || F1: 0.687
330 Permen_ESDM_2014_10
Case Sensitive   : P: 0.6842105263157895 || R: 1.0 || F1: 0.8125000000000001
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
331 UU_1957_29
Case Sensitive   : P: 0.06666666666666667 || R: 1.0 || F1: 0.125
Case Insensitive : P: 0.067 || R: 1.0 || F1: 0.126
332 Perkab_Bantul_1994_12
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
333 Peraturan_Polri_2010_20
Case Sensitive   : P: 0.6 || R: 0.9230769230769231 || F1: 0.7272727272727274
Case Insensitive : P: 0.6 || R: 0.92

...

2351 PP_2018_32
Case Sensitive   : P: 0.3157894736842105 || R: 0.6666666666666666 || F1: 0.42857142857142855
Case Insensitive : P: 0.316 || R: 0.667 || F1: 0.429
2352 UU_2002_27
Case Sensitive   : P: 0.05263157894736842 || R: 1.0 || F1: 0.1
Case Insensitive : P: 0.053 || R: 1.0 || F1: 0.101
2353 Permen_PUPR_2015_01
Case Sensitive   : P: 0.3684210526315789 || R: 0.5384615384615384 || F1: 0.4375
Case Insensitive : P: 0.368 || R: 0.538 || F1: 0.437
2354 PP_2019_28
Case Sensitive   : P: 0.47368421052631576 || R: 0.75 || F1: 0.5806451612903226
Case Insensitive : P: 0.474 || R: 0.75 || F1: 0.581
2355 Perkot_Depok_2003_10
Case Sensitive   : P: 0.8947368421052632 || R: 0.8947368421052632 || F1: 0.8947368421052632
Case Insensitive : P: 0.895 || R: 0.895 || F1: 0.895
2356 Permen_Hub_2013_16
Case Sensitive   : P: 0.47368421052631576 || R: 0.6923076923076923 || F1: 0.5625
Case Insensitive : P: 0.474 || R: 0.692 || F1: 0.563
2357 Perpres_2009_42
Case Sensitive   : P: 0.09090909090909091 || R: 1.0 |

2421 Permen_Keu_2014_100
Case Sensitive   : P: 0.1111111111111111 || R: 0.6666666666666666 || F1: 0.1904761904761905
Case Insensitive : P: 0.111 || R: 0.667 || F1: 0.19
2422 Perkot_Tasikmalaya_2004_16
Case Sensitive   : P: 0.05263157894736842 || R: 0.25 || F1: 0.08695652173913043
Case Insensitive : P: 0.053 || R: 0.25 || F1: 0.087
2423 Perkot_Binjai_2001_26
Case Sensitive   : P: 0.07692307692307693 || R: 1.0 || F1: 0.14285714285714288
Case Insensitive : P: 0.077 || R: 1.0 || F1: 0.143
2424 PP_1986_23
Case Sensitive   : P: 0.631578947368421 || R: 0.8 || F1: 0.7058823529411765
Case Insensitive : P: 0.632 || R: 0.8 || F1: 0.706
2425 Perkot_Depok_2008_11
Case Sensitive   : P: 0.3684210526315789 || R: 0.4375 || F1: 0.39999999999999997
Case Insensitive : P: 0.368 || R: 0.438 || F1: 0.4
2426 Permen_Hub_2014_20
Case Sensitive   : P: 0.5263157894736842 || R: 1.0 || F1: 0.6896551724137931
Case Insensitive : P: 0.526 || R: 1.0 || F1: 0.689
2427 Perkab_Pacitan_2010_6
Case Sensitive   : P: 0.0 || R

2492 Permen_Keu_2011_238
Case Sensitive   : P: 0.3157894736842105 || R: 1.0 || F1: 0.4799999999999999
Case Insensitive : P: 0.316 || R: 1.0 || F1: 0.48
2493 Perkab_Kulon_Progo_2006_3
Case Sensitive   : P: 0.8333333333333334 || R: 0.23809523809523808 || F1: 0.37037037037037035
Case Insensitive : P: 0.833 || R: 0.238 || F1: 0.37
2494 Perkot_Samarinda_2008_18
Case Sensitive   : P: 0.10526315789473684 || R: 1.0 || F1: 0.1904761904761905
Case Insensitive : P: 0.105 || R: 1.0 || F1: 0.19
2495 UU_1974_4
Case Sensitive   : P: 0.06666666666666667 || R: 1.0 || F1: 0.125
Case Insensitive : P: 0.067 || R: 1.0 || F1: 0.126
2496 Peraturan_BPKP_2017_6
Case Sensitive   : P: 0.47368421052631576 || R: 0.5 || F1: 0.4864864864864865
Case Insensitive : P: 0.474 || R: 0.5 || F1: 0.487
2497 Permen_Perin_2019_35
Case Sensitive   : P: 0.47368421052631576 || R: 0.5 || F1: 0.4864864864864865
Case Insensitive : P: 0.474 || R: 0.5 || F1: 0.487
2498 PP_2007_35
Case Sensitive   : P: 0.5555555555555556 || R: 0.833333

2548 Permen_Hub_2016_2
Case Sensitive   : P: 0.631578947368421 || R: 0.6666666666666666 || F1: 0.6486486486486486
Case Insensitive : P: 0.632 || R: 0.667 || F1: 0.649
2549 Permen_PPPA_2015_9
Case Sensitive   : P: 0.05263157894736842 || R: 1.0 || F1: 0.1
Case Insensitive : P: 0.053 || R: 1.0 || F1: 0.101
2550 PP_2005_15
Case Sensitive   : P: 0.5789473684210527 || R: 0.6875 || F1: 0.6285714285714286
Case Insensitive : P: 0.579 || R: 0.688 || F1: 0.629
2551 Perkab_Serdang_Bedagai_2012_14
Case Sensitive   : P: 0.42105263157894735 || R: 1.0 || F1: 0.5925925925925926
Case Insensitive : P: 0.421 || R: 1.0 || F1: 0.593
2552 PP_2003_34
Case Sensitive   : P: 0.16666666666666666 || R: 0.5 || F1: 0.25
Case Insensitive : P: 0.167 || R: 0.5 || F1: 0.25
2553 Permen_Hub_2015_134
Case Sensitive   : P: 0.3157894736842105 || R: 0.6666666666666666 || F1: 0.42857142857142855
Case Insensitive : P: 0.316 || R: 0.667 || F1: 0.429
2554 Permen_Ristekdikti_2016_55
Case Sensitive   : P: 0.5263157894736842 || R: 0

2600 PP_2015_69
Case Sensitive   : P: 0.3157894736842105 || R: 1.0 || F1: 0.4799999999999999
Case Insensitive : P: 0.316 || R: 1.0 || F1: 0.48
2601 Permen_LH_2012_20
Case Sensitive   : P: 0.6842105263157895 || R: 1.0 || F1: 0.8125000000000001
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
2602 UU_1954_76
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2603 Perkab_Magelang_2010_12
Case Sensitive   : P: 0.3157894736842105 || R: 0.6 || F1: 0.41379310344827586
Case Insensitive : P: 0.316 || R: 0.6 || F1: 0.414
2604 Perpres_2016_68
Case Sensitive   : P: 0.3157894736842105 || R: 0.6666666666666666 || F1: 0.42857142857142855
Case Insensitive : P: 0.316 || R: 0.667 || F1: 0.429
2605 Permen_Agama_2015_41
Case Sensitive   : P: 0.6842105263157895 || R: 1.0 || F1: 0.8125000000000001
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
2606 Peraturan_BKN_2012_16
Case Sensitive   : P: 0.631578947368421 || R: 0.9230769230769231 || F1: 0.7499999999999999
Cas

In [50]:
test_1('cfg', cf_gemma, test_closing, '2', 'results/metrics_cf.csv')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.5263157894736842 || R: 0.625 || F1: 0.5714285714285714
Case Insensitive : P: 0.526 || R: 0.625 || F1: 0.571
1 Permen_KP_2013_5
Case Sensitive   : P: 0.5263157894736842 || R: 0.7692307692307693 || F1: 0.625
Case Insensitive : P: 0.526 || R: 0.769 || F1: 0.625
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.3157894736842105 || R: 0.6666666666666666 || F1: 0.42857142857142855
Case Insensitive : P: 0.316 || R: 0.667 || F1: 0.429
3 Permen_Par_2015_14
Case Sensitive   : P: 0.6842105263157895 || R: 1.0 || F1: 0.8125000000000001
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
4 Perpres_2019_67
Case Sensitive   : P: 0.6842105263157895 || R: 0.6842105263157895 || F1: 0.6842105263157895
Case Insensitive : P: 0.684 || R: 0.684 || F1: 0.684
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.05263157894736842 || R: 0.07692307692307693 || F1: 0.0625
Case Insensitive : P: 0.053 || R: 0.077 || F1: 0.063
6 Perkab_Tabalong_2010_09
Case Sensitive   : 

71 Perprov_Sulteng_2005_02
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
72 Perkab_Kotabaru_2014_11
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
73 Perpres_2008_41
Case Sensitive   : P: 0.5789473684210527 || R: 0.9166666666666666 || F1: 0.7096774193548387
Case Insensitive : P: 0.579 || R: 0.917 || F1: 0.71
74 Permen_PR_2009_03
Case Sensitive   : P: 0.3684210526315789 || R: 1.0 || F1: 0.5384615384615384
Case Insensitive : P: 0.368 || R: 1.0 || F1: 0.538
75 Peraturan_Polri_2012_4
Case Sensitive   : P: 0.5789473684210527 || R: 0.9166666666666666 || F1: 0.7096774193548387
Case Insensitive : P: 0.579 || R: 0.917 || F1: 0.71
76 Permen_Perin_2012_11
Case Sensitive   : P: 0.5789473684210527 || R: 0.9166666666666666 || F1: 0.7096774193548387
Case Insensitive : P: 0.579 || R: 0.917 || F1: 0.71
77 Perkab_Sleman_2012_9
Case Sensitive   : P: 1.0 || R: 1.0 || F1: 1.0
Case Insensitive : P: 1.0 || R: 1.0 || F1: 1.

126 Permen_Tan_2012_53
Case Sensitive   : P: 0.631578947368421 || R: 0.9230769230769231 || F1: 0.7499999999999999
Case Insensitive : P: 0.632 || R: 0.923 || F1: 0.75
127 Perpres_2010_2
Case Sensitive   : P: 0.47368421052631576 || R: 1.0 || F1: 0.6428571428571429
Case Insensitive : P: 0.474 || R: 1.0 || F1: 0.643
128 Permen_Dikbud_2012_58
Case Sensitive   : P: 0.47619047619047616 || R: 0.8333333333333334 || F1: 0.6060606060606061
Case Insensitive : P: 0.571 || R: 1.0 || F1: 0.727
129 Peraturan_Basarnas_2017_17
Case Sensitive   : P: 0.10526315789473684 || R: 0.10526315789473684 || F1: 0.10526315789473684
Case Insensitive : P: 0.105 || R: 0.105 || F1: 0.105
130 Permen_ATRBPN_2018_16
Case Sensitive   : P: 0.3684210526315789 || R: 0.3684210526315789 || F1: 0.3684210526315789
Case Insensitive : P: 0.368 || R: 0.368 || F1: 0.368
131 Permen_Perin_2018_9
Case Sensitive   : P: 0.6842105263157895 || R: 0.6842105263157895 || F1: 0.6842105263157895
Case Insensitive : P: 0.684 || R: 0.684 || F1: 0.6

180 Peraturan_BNP2TKI_2017_11
Case Sensitive   : P: 0.6842105263157895 || R: 0.6842105263157895 || F1: 0.6842105263157895
Case Insensitive : P: 0.684 || R: 0.684 || F1: 0.684
181 Permen_Tan_2010_45
Case Sensitive   : P: 0.6842105263157895 || R: 1.0 || F1: 0.8125000000000001
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
182 Permen_Dikbud_2013_87
Case Sensitive   : P: 0.631578947368421 || R: 0.9230769230769231 || F1: 0.7499999999999999
Case Insensitive : P: 0.632 || R: 0.923 || F1: 0.75
183 Permen_Perin_2015_48
Case Sensitive   : P: 0.6842105263157895 || R: 1.0 || F1: 0.8125000000000001
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
184 Perprov_Sulteng_2002_06
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
185 PP_1990_46
Case Sensitive   : P: 0.3157894736842105 || R: 1.0 || F1: 0.4799999999999999
Case Insensitive : P: 0.316 || R: 1.0 || F1: 0.48
186 Permen_Ristekdikti_2016_57
Case Sensitive   : P: 0.5263157894736842 || R: 0.769230769230

236 Permen_Dagri_2013_67
Case Sensitive   : P: 0.6842105263157895 || R: 1.0 || F1: 0.8125000000000001
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
237 Perprov_Kalbar_2001_7
Case Sensitive   : P: 0.2631578947368421 || R: 0.45454545454545453 || F1: 0.3333333333333333
Case Insensitive : P: 0.263 || R: 0.455 || F1: 0.333
238 Permen_Tan_2015_53
Case Sensitive   : P: 0.5263157894736842 || R: 1.0 || F1: 0.6896551724137931
Case Insensitive : P: 0.526 || R: 1.0 || F1: 0.689
239 Permen_Keu_2015_78
Case Sensitive   : P: 0.3157894736842105 || R: 1.0 || F1: 0.4799999999999999
Case Insensitive : P: 0.316 || R: 1.0 || F1: 0.48
240 PP_1963_44
Case Sensitive   : P: 0.125 || R: 0.2222222222222222 || F1: 0.16
Case Insensitive : P: 0.125 || R: 0.222 || F1: 0.16
241 Permen_Keu_2009_173
Case Sensitive   : P: 0.2631578947368421 || R: 0.8333333333333334 || F1: 0.39999999999999997
Case Insensitive : P: 0.263 || R: 0.833 || F1: 0.4
242 PP_2005_71
Case Sensitive   : P: 0.3684210526315789 || R: 0.3888888888

...

2212 PP_1998_47
Case Sensitive   : P: 0.3157894736842105 || R: 1.0 || F1: 0.4799999999999999
Case Insensitive : P: 0.316 || R: 1.0 || F1: 0.48
2213 UU_1954_58
Case Sensitive   : P: 0.05555555555555555 || R: 1.0 || F1: 0.10526315789473684
Case Insensitive : P: 0.056 || R: 1.0 || F1: 0.106
2214 Permen_Kes_2016_72
Case Sensitive   : P: 0.631578947368421 || R: 0.75 || F1: 0.6857142857142857
Case Insensitive : P: 0.632 || R: 0.75 || F1: 0.686
2215 Perprov_Gorontalo_2005_07
Case Sensitive   : P: 0.3684210526315789 || R: 0.4117647058823529 || F1: 0.3888888888888889
Case Insensitive : P: 0.368 || R: 0.412 || F1: 0.389
2216 Perkab_Bantul_2002_9
Case Sensitive   : P: 0.05263157894736842 || R: 1.0 || F1: 0.1
Case Insensitive : P: 0.053 || R: 1.0 || F1: 0.101
2217 Peraturan_Basarnas_2016_5
Case Sensitive   : P: 0.5263157894736842 || R: 0.625 || F1: 0.5714285714285714
Case Insensitive : P: 0.526 || R: 0.625 || F1: 0.571
2218 Permen_Hut_2014_1
Case Sensitive   : P: 0.6842105263157895 || R: 1.0 || F1

2329 UU_2003_7
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2330 PP_1981_17
Case Sensitive   : P: 0.4 || R: 0.4 || F1: 0.4000000000000001
Case Insensitive : P: 0.4 || R: 0.4 || F1: 0.4
2331 Permen_Keu_2014_252
Case Sensitive   : P: 0.47368421052631576 || R: 0.75 || F1: 0.5806451612903226
Case Insensitive : P: 0.474 || R: 0.75 || F1: 0.581
2332 Permen_Hub_2016_144
Case Sensitive   : P: 0.42105263157894735 || R: 0.6666666666666666 || F1: 0.5161290322580646
Case Insensitive : P: 0.421 || R: 0.667 || F1: 0.516
2333 Permen_Parekraf_2013_07
Case Sensitive   : P: 0.6842105263157895 || R: 1.0 || F1: 0.8125000000000001
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
2334 Peraturan_Polri_2013_2
Case Sensitive   : P: 0.631578947368421 || R: 0.9230769230769231 || F1: 0.7499999999999999
Case Insensitive : P: 0.632 || R: 0.923 || F1: 0.75
2335 Peraturan_KY_2016_4
Case Sensitive   : P: 0.5263157894736842 || R: 0.5263157894736842 || F1: 0.526315789473684

2400 Permen_ESDM_2013_19
Case Sensitive   : P: 0.6842105263157895 || R: 1.0 || F1: 0.8125000000000001
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
2401 Peraturan_LKPP_2019_14
Case Sensitive   : P: 0.5263157894736842 || R: 0.5263157894736842 || F1: 0.5263157894736842
Case Insensitive : P: 0.526 || R: 0.526 || F1: 0.526
2402 Permen_Hub_2017_87
Case Sensitive   : P: 0.3157894736842105 || R: 0.4 || F1: 0.35294117647058826
Case Insensitive : P: 0.316 || R: 0.4 || F1: 0.353
2403 Peraturan_Batan_2016_4
Case Sensitive   : P: 0.5263157894736842 || R: 0.7692307692307693 || F1: 0.625
Case Insensitive : P: 0.526 || R: 0.769 || F1: 0.625
2404 PP_1957_13
Case Sensitive   : P: 0.1111111111111111 || R: 0.3333333333333333 || F1: 0.16666666666666666
Case Insensitive : P: 0.111 || R: 0.333 || F1: 0.167
2405 Peraturan_BPJSTK_2018_1
Case Sensitive   : P: 0 || R: 0.0 || F1: 0
Case Insensitive : P: 0 || R: 0.0 || F1: 0
2406 Peraturan_LIPI_2017_1
Case Sensitive   : P: 0.42105263157894735 || R: 0.5333333

2547 Permen_Kes_2014_72
Case Sensitive   : P: 0.6842105263157895 || R: 1.0 || F1: 0.8125000000000001
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
2548 Permen_Hub_2016_2
Case Sensitive   : P: 0.631578947368421 || R: 0.6666666666666666 || F1: 0.6486486486486486
Case Insensitive : P: 0.632 || R: 0.667 || F1: 0.649
2549 Permen_PPPA_2015_9
Case Sensitive   : P: 0.05263157894736842 || R: 1.0 || F1: 0.1
Case Insensitive : P: 0.053 || R: 1.0 || F1: 0.101
2550 PP_2005_15
Case Sensitive   : P: 0.5789473684210527 || R: 0.6875 || F1: 0.6285714285714286
Case Insensitive : P: 0.579 || R: 0.688 || F1: 0.629
2551 Perkab_Serdang_Bedagai_2012_14
Case Sensitive   : P: 0.42105263157894735 || R: 1.0 || F1: 0.5925925925925926
Case Insensitive : P: 0.421 || R: 1.0 || F1: 0.593
2552 PP_2003_34
Case Sensitive   : P: 0.16666666666666666 || R: 0.5 || F1: 0.25
Case Insensitive : P: 0.167 || R: 0.5 || F1: 0.25
2553 Permen_Hub_2015_134
Case Sensitive   : P: 0.3157894736842105 || R: 0.6666666666666666 || F1: 0

2602 UU_1954_76
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2603 Perkab_Magelang_2010_12
Case Sensitive   : P: 0.3157894736842105 || R: 0.6 || F1: 0.41379310344827586
Case Insensitive : P: 0.316 || R: 0.6 || F1: 0.414
2604 Perpres_2016_68
Case Sensitive   : P: 0.3157894736842105 || R: 0.6666666666666666 || F1: 0.42857142857142855
Case Insensitive : P: 0.316 || R: 0.667 || F1: 0.429
2605 Permen_Agama_2015_41
Case Sensitive   : P: 0.6842105263157895 || R: 1.0 || F1: 0.8125000000000001
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
2606 Peraturan_BKN_2012_16
Case Sensitive   : P: 0.631578947368421 || R: 0.9230769230769231 || F1: 0.7499999999999999
Case Insensitive : P: 0.632 || R: 0.923 || F1: 0.75
2607 Permen_Kes_2016_56
Case Sensitive   : P: 0.631578947368421 || R: 0.75 || F1: 0.6857142857142857
Case Insensitive : P: 0.632 || R: 0.75 || F1: 0.686
2608 Perkab_Indramayu_2005_1
Case Sensitive   : P: 0.3333333333333333 || R: 0.3125 || F1: 0.

In [51]:
test_1('cfl', cf_llama, test_closing, '1', 'results/metrics_cf.csv')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.47368421052631576 || R: 0.5625 || F1: 0.5142857142857142
Case Insensitive : P: 0.474 || R: 0.562 || F1: 0.514
1 Permen_KP_2013_5
Case Sensitive   : P: 0.631578947368421 || R: 0.9230769230769231 || F1: 0.7499999999999999
Case Insensitive : P: 0.632 || R: 0.923 || F1: 0.75
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.2631578947368421 || R: 0.5555555555555556 || F1: 0.35714285714285715
Case Insensitive : P: 0.263 || R: 0.556 || F1: 0.357
3 Permen_Par_2015_14
Case Sensitive   : P: 0.631578947368421 || R: 0.9230769230769231 || F1: 0.7499999999999999
Case Insensitive : P: 0.632 || R: 0.923 || F1: 0.75
4 Perpres_2019_67
Case Sensitive   : P: 0.6842105263157895 || R: 0.6842105263157895 || F1: 0.6842105263157895
Case Insensitive : P: 0.684 || R: 0.684 || F1: 0.684
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.2631578947368421 || R: 0.38461538461538464 || F1: 0.3125
Case Insensitive : P: 0.263 || R: 0.385 || F1: 0.313
6 Perkab_Tabalong_

100 PP_2013_55
Case Sensitive   : P: 0.631578947368421 || R: 1.0 || F1: 0.7741935483870968
Case Insensitive : P: 0.632 || R: 1.0 || F1: 0.775
101 Permen_LHK_2019_21
Case Sensitive   : P: 0.47368421052631576 || R: 0.6923076923076923 || F1: 0.5625
Case Insensitive : P: 0.474 || R: 0.692 || F1: 0.563
102 Perpres_2018_45
Case Sensitive   : P: 0.7894736842105263 || R: 0.8333333333333334 || F1: 0.8108108108108109
Case Insensitive : P: 0.789 || R: 0.833 || F1: 0.81
103 UU_2008_9
Case Sensitive   : P: 0.05263157894736842 || R: 1.0 || F1: 0.1
Case Insensitive : P: 0.053 || R: 1.0 || F1: 0.101
104 UU_1954_63
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
105 Permen_Tan_2014_36
Case Sensitive   : P: 0.47368421052631576 || R: 0.9 || F1: 0.6206896551724138
Case Insensitive : P: 0.474 || R: 0.9 || F1: 0.621
106 Permen_Keu_2017_37
Case Sensitive   : P: 0.3157894736842105 || R: 0.5 || F1: 0.3870967741935484
Case Insensitive : P: 0.316 || R: 0.5 || F1: 0.387
1

200 Permen_Keu_2009_234
Case Sensitive   : P: 0.3157894736842105 || R: 1.0 || F1: 0.4799999999999999
Case Insensitive : P: 0.316 || R: 1.0 || F1: 0.48
201 PP_2009_78
Case Sensitive   : P: 0.3157894736842105 || R: 0.6666666666666666 || F1: 0.42857142857142855
Case Insensitive : P: 0.316 || R: 0.667 || F1: 0.429
202 Peraturan_BPOM_2019_30
Case Sensitive   : P: 0.4117647058823529 || R: 0.3684210526315789 || F1: 0.3888888888888889
Case Insensitive : P: 0.412 || R: 0.368 || F1: 0.389
203 Permen_Pora_2019_3
Case Sensitive   : P: 0.6842105263157895 || R: 0.6842105263157895 || F1: 0.6842105263157895
Case Insensitive : P: 0.684 || R: 0.684 || F1: 0.684
204 Perprov_Papua_2013_14
Case Sensitive   : P: 0.5263157894736842 || R: 0.7692307692307693 || F1: 0.625
Case Insensitive : P: 0.526 || R: 0.769 || F1: 0.625
205 Permen_PANRB_2013_32
Case Sensitive   : P: 0.631578947368421 || R: 0.9230769230769231 || F1: 0.7499999999999999
Case Insensitive : P: 0.632 || R: 0.923 || F1: 0.75
206 Permen_Dagri_2017_

257 Permen_Keu_2016_148
Case Sensitive   : P: 0.10526315789473684 || R: 0.2222222222222222 || F1: 0.14285714285714285
Case Insensitive : P: 0.105 || R: 0.222 || F1: 0.143
258 Perkot_Semarang_2004_14
Case Sensitive   : P: 0.631578947368421 || R: 0.8 || F1: 0.7058823529411765
Case Insensitive : P: 0.632 || R: 0.8 || F1: 0.706
259 Perprov_Jabar_2013_1
Case Sensitive   : P: 0.5789473684210527 || R: 0.5789473684210527 || F1: 0.5789473684210527
Case Insensitive : P: 0.579 || R: 0.579 || F1: 0.579
260 Permen_ESDM_2018_4
Case Sensitive   : P: 0.5263157894736842 || R: 0.5263157894736842 || F1: 0.5263157894736842
Case Insensitive : P: 0.526 || R: 0.526 || F1: 0.526
261 PP_1985_32
Case Sensitive   : P: 0.3157894736842105 || R: 0.6666666666666666 || F1: 0.42857142857142855
Case Insensitive : P: 0.316 || R: 0.667 || F1: 0.429
262 Permen_Keu_2015_247
Case Sensitive   : P: 0.10526315789473684 || R: 0.3333333333333333 || F1: 0.16
Case Insensitive : P: 0.105 || R: 0.333 || F1: 0.16
263 Permen_Hut_2014_

400 Perkab_Bandung_2005_7
Case Sensitive   : P: 0.35294117647058826 || R: 0.6666666666666666 || F1: 0.46153846153846156
Case Insensitive : P: 0.353 || R: 0.667 || F1: 0.462
401 Peraturan_BPS_2016_73
Case Sensitive   : P: 0.35294117647058826 || R: 0.3333333333333333 || F1: 0.34285714285714286
Case Insensitive : P: 0.353 || R: 0.333 || F1: 0.343
402 UU_2013_5
Case Sensitive   : P: 0.05263157894736842 || R: 1.0 || F1: 0.1
Case Insensitive : P: 0.053 || R: 1.0 || F1: 0.101
403 Peraturan_Bekraf_2016_1
Case Sensitive   : P: 0.47058823529411764 || R: 0.47058823529411764 || F1: 0.47058823529411764
Case Insensitive : P: 0.471 || R: 0.471 || F1: 0.471
404 Permen_ESDM_2014_28
Case Sensitive   : P: 0.631578947368421 || R: 0.9230769230769231 || F1: 0.7499999999999999
Case Insensitive : P: 0.632 || R: 0.923 || F1: 0.75
405 Permen_Naker_2015_5
Case Sensitive   : P: 0.5263157894736842 || R: 1.0 || F1: 0.6896551724137931
Case Insensitive : P: 0.526 || R: 1.0 || F1: 0.689
406 Permen_Bappenas_2016_6
Case

...

2389 Perkab_Sleman_2001_15
Case Sensitive   : P: 0.7894736842105263 || R: 0.8333333333333334 || F1: 0.8108108108108109
Case Insensitive : P: 0.789 || R: 0.833 || F1: 0.81
2390 Peraturan_BNN_2017_2
Case Sensitive   : P: 0.5263157894736842 || R: 0.5263157894736842 || F1: 0.5263157894736842
Case Insensitive : P: 0.526 || R: 0.526 || F1: 0.526
2391 UU_1957_53
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2392 Peraturan_BNPB_2010_15
Case Sensitive   : P: 0.42105263157894735 || R: 0.8888888888888888 || F1: 0.5714285714285714
Case Insensitive : P: 0.421 || R: 0.889 || F1: 0.571
2393 Permen_Han_2014_56
Case Sensitive   : P: 0.631578947368421 || R: 0.9230769230769231 || F1: 0.7499999999999999
Case Insensitive : P: 0.632 || R: 0.923 || F1: 0.75
2394 Peraturan_BPOM_2017_12
Case Sensitive   : P: 0 || R: 0.0 || F1: 0
Case Insensitive : P: 0 || R: 0.0 || F1: 0
2395 Permen_ESDM_2014_25
Case Sensitive   : P: 0.47368421052631576 || R: 0.6923076923076923 || F1

2444 Perprov_Kep_Riau_2011_8
Case Sensitive   : P: 0.3684210526315789 || R: 0.7 || F1: 0.48275862068965514
Case Insensitive : P: 0.368 || R: 0.7 || F1: 0.482
2445 Permen_Kes_2011_2356
Case Sensitive   : P: 0.42105263157894735 || R: 0.8888888888888888 || F1: 0.5714285714285714
Case Insensitive : P: 0.421 || R: 0.889 || F1: 0.571
2446 Permen_Keu_2013_179
Case Sensitive   : P: 0.42105263157894735 || R: 0.8888888888888888 || F1: 0.5714285714285714
Case Insensitive : P: 0.421 || R: 0.889 || F1: 0.571
2447 PP_2015_62
Case Sensitive   : P: 0.3157894736842105 || R: 1.0 || F1: 0.4799999999999999
Case Insensitive : P: 0.316 || R: 1.0 || F1: 0.48
2448 Permen_Keu_2009_180
Case Sensitive   : P: 0.47368421052631576 || R: 0.9 || F1: 0.6206896551724138
Case Insensitive : P: 0.474 || R: 0.9 || F1: 0.621
2449 Peraturan_BPH_Migas_2013_10
Case Sensitive   : P: 0.2631578947368421 || R: 0.5555555555555556 || F1: 0.35714285714285715
Case Insensitive : P: 0.263 || R: 0.556 || F1: 0.357
2450 Permen_Dikbud_2018

2500 Permen_ESDM_2014_36
Case Sensitive   : P: 0.631578947368421 || R: 0.9230769230769231 || F1: 0.7499999999999999
Case Insensitive : P: 0.632 || R: 0.923 || F1: 0.75
2501 Peraturan_Polri_2015_18
Case Sensitive   : P: 0.5263157894736842 || R: 0.5263157894736842 || F1: 0.5263157894736842
Case Insensitive : P: 0.526 || R: 0.526 || F1: 0.526
2502 Perkot_Pangkalpinang_2006_12
Case Sensitive   : P: 0.2631578947368421 || R: 0.5555555555555556 || F1: 0.35714285714285715
Case Insensitive : P: 0.263 || R: 0.556 || F1: 0.357
2503 Permen_LH_2011_3
Case Sensitive   : P: 0.6842105263157895 || R: 1.0 || F1: 0.8125000000000001
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
2504 Perprov_Kalbar_2004_1
Case Sensitive   : P: 0.2777777777777778 || R: 0.38461538461538464 || F1: 0.3225806451612903
Case Insensitive : P: 0.278 || R: 0.385 || F1: 0.323
2505 Perkab_Garut_2008_17
Case Sensitive   : P: 0.05263157894736842 || R: 1.0 || F1: 0.1
Case Insensitive : P: 0.053 || R: 1.0 || F1: 0.101
2506 Permen_Hum

2552 PP_2003_34
Case Sensitive   : P: 0.2631578947368421 || R: 0.8333333333333334 || F1: 0.39999999999999997
Case Insensitive : P: 0.263 || R: 0.833 || F1: 0.4
2553 Permen_Hub_2015_134
Case Sensitive   : P: 0.2631578947368421 || R: 0.5555555555555556 || F1: 0.35714285714285715
Case Insensitive : P: 0.263 || R: 0.556 || F1: 0.357
2554 Permen_Ristekdikti_2016_55
Case Sensitive   : P: 0.6842105263157895 || R: 0.8125 || F1: 0.742857142857143
Case Insensitive : P: 0.684 || R: 0.812 || F1: 0.743
2555 Peraturan_OJK_2019_13
Case Sensitive   : P: 0.5263157894736842 || R: 0.625 || F1: 0.5714285714285714
Case Insensitive : P: 0.526 || R: 0.625 || F1: 0.571
2556 Permen_Kes_2013_75
Case Sensitive   : P: 0.631578947368421 || R: 0.9230769230769231 || F1: 0.7499999999999999
Case Insensitive : P: 0.632 || R: 0.923 || F1: 0.75
2557 Permen_Dagri_2012_16
Case Sensitive   : P: 0.5789473684210527 || R: 0.8461538461538461 || F1: 0.6875
Case Insensitive : P: 0.579 || R: 0.846 || F1: 0.687
2558 Perkot_Bogor_20

2607 Permen_Kes_2016_56
Case Sensitive   : P: 0.3157894736842105 || R: 0.375 || F1: 0.34285714285714286
Case Insensitive : P: 0.316 || R: 0.375 || F1: 0.343
2608 Perkab_Indramayu_2005_1
Case Sensitive   : P: 0 || R: 0.0 || F1: 0
Case Insensitive : P: 0 || R: 0.0 || F1: 0
2609 Permen_PANRB_2018_25
Case Sensitive   : P: 0.6842105263157895 || R: 0.6842105263157895 || F1: 0.6842105263157895
Case Insensitive : P: 0.684 || R: 0.684 || F1: 0.684
2610 Permen_Humham_2018_04
Case Sensitive   : P: 0.2777777777777778 || R: 0.4166666666666667 || F1: 0.33333333333333337
Case Insensitive : P: 0.278 || R: 0.417 || F1: 0.334
2611 Permen_Humham_2019_8
Case Sensitive   : P: 0.5263157894736842 || R: 0.5263157894736842 || F1: 0.5263157894736842
Case Insensitive : P: 0.526 || R: 0.526 || F1: 0.526
2612 Peraturan_Basarnas_2017_3
Case Sensitive   : P: 0.3157894736842105 || R: 0.3333333333333333 || F1: 0.3243243243243243
Case Insensitive : P: 0.316 || R: 0.333 || F1: 0.324
2613 Permenko_Polhukam_2018_2
Case Se

In [52]:
test_1('cfl', cf_llama, test_closing, '2', 'results/metrics_cf.csv')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.47368421052631576 || R: 0.5625 || F1: 0.5142857142857142
Case Insensitive : P: 0.474 || R: 0.562 || F1: 0.514
1 Permen_KP_2013_5
Case Sensitive   : P: 0.631578947368421 || R: 0.9230769230769231 || F1: 0.7499999999999999
Case Insensitive : P: 0.632 || R: 0.923 || F1: 0.75
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.2631578947368421 || R: 0.5555555555555556 || F1: 0.35714285714285715
Case Insensitive : P: 0.263 || R: 0.556 || F1: 0.357
3 Permen_Par_2015_14
Case Sensitive   : P: 0.631578947368421 || R: 0.9230769230769231 || F1: 0.7499999999999999
Case Insensitive : P: 0.632 || R: 0.923 || F1: 0.75
4 Perpres_2019_67
Case Sensitive   : P: 0.6842105263157895 || R: 0.6842105263157895 || F1: 0.6842105263157895
Case Insensitive : P: 0.684 || R: 0.684 || F1: 0.684
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.2631578947368421 || R: 0.38461538461538464 || F1: 0.3125
Case Insensitive : P: 0.263 || R: 0.385 || F1: 0.313
6 Perkab_Tabalong_

65 Perprov_Jateng_2001_10
Case Sensitive   : P: 0.42105263157894735 || R: 0.6666666666666666 || F1: 0.5161290322580646
Case Insensitive : P: 0.421 || R: 0.667 || F1: 0.516
66 PP_2008_70
Case Sensitive   : P: 0.6842105263157895 || R: 1.0 || F1: 0.8125000000000001
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
67 Permen_Dikbud_2012_7
Case Sensitive   : P: 0.5263157894736842 || R: 0.9090909090909091 || F1: 0.6666666666666666
Case Insensitive : P: 0.526 || R: 0.909 || F1: 0.666
68 Perpres_2013_103
Case Sensitive   : P: 0.42105263157894735 || R: 0.8888888888888888 || F1: 0.5714285714285714
Case Insensitive : P: 0.421 || R: 0.889 || F1: 0.571
69 PP_2018_49
Case Sensitive   : P: 0.47368421052631576 || R: 0.75 || F1: 0.5806451612903226
Case Insensitive : P: 0.474 || R: 0.75 || F1: 0.581
70 Peraturan_Bappebti_2017_4
Case Sensitive   : P: 0.7647058823529411 || R: 0.6842105263157895 || F1: 0.7222222222222222
Case Insensitive : P: 0.765 || R: 0.684 || F1: 0.722
71 Perprov_Sulteng_2005_02
Case 

120 Perkab_Sleman_2012_1
Case Sensitive   : P: 0.5789473684210527 || R: 0.6111111111111112 || F1: 0.5945945945945946
Case Insensitive : P: 0.579 || R: 0.611 || F1: 0.595
121 Permen_Dagri_2017_111
Case Sensitive   : P: 0.3157894736842105 || R: 0.5 || F1: 0.3870967741935484
Case Insensitive : P: 0.316 || R: 0.5 || F1: 0.387
122 Permen_ESDM_2013_17
Case Sensitive   : P: 0.6842105263157895 || R: 1.0 || F1: 0.8125000000000001
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
123 Perprov_Yogya_2001_8
Case Sensitive   : P: 0.10526315789473684 || R: 0.2222222222222222 || F1: 0.14285714285714285
Case Insensitive : P: 0.105 || R: 0.222 || F1: 0.143
124 Permen_Dikbud_2014_115
Case Sensitive   : P: 0.631578947368421 || R: 0.9230769230769231 || F1: 0.7499999999999999
Case Insensitive : P: 0.632 || R: 0.923 || F1: 0.75
125 Peraturan_BPKP_2016_23
Case Sensitive   : P: 0.5263157894736842 || R: 0.7692307692307693 || F1: 0.625
Case Insensitive : P: 0.526 || R: 0.769 || F1: 0.625
126 Permen_Tan_2012_53


182 Permen_Dikbud_2013_87
Case Sensitive   : P: 0.631578947368421 || R: 0.9230769230769231 || F1: 0.7499999999999999
Case Insensitive : P: 0.632 || R: 0.923 || F1: 0.75
183 Permen_Perin_2015_48
Case Sensitive   : P: 0.6842105263157895 || R: 1.0 || F1: 0.8125000000000001
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
184 Perprov_Sulteng_2002_06
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
185 PP_1990_46
Case Sensitive   : P: 0.3157894736842105 || R: 1.0 || F1: 0.4799999999999999
Case Insensitive : P: 0.316 || R: 1.0 || F1: 0.48
186 Permen_Ristekdikti_2016_57
Case Sensitive   : P: 0.5263157894736842 || R: 0.7692307692307693 || F1: 0.625
Case Insensitive : P: 0.526 || R: 0.769 || F1: 0.625
187 Permen_Bappenas_2017_14
Case Sensitive   : P: 0.5789473684210527 || R: 0.5789473684210527 || F1: 0.5789473684210527
Case Insensitive : P: 0.579 || R: 0.579 || F1: 0.579
188 PP_2013_94
Case Sensitive   : P: 0.47368421052631576 || R: 1.0 || F1: 0.642857

253 UU_1971_7
Case Sensitive   : P: 0.05263157894736842 || R: 1.0 || F1: 0.1
Case Insensitive : P: 0.053 || R: 1.0 || F1: 0.101
254 Permen_Kes_2017_32
Case Sensitive   : P: 0.47368421052631576 || R: 0.6 || F1: 0.5294117647058824
Case Insensitive : P: 0.474 || R: 0.6 || F1: 0.53
255 Permen_Keu_2012_34
Case Sensitive   : P: 0.631578947368421 || R: 0.9230769230769231 || F1: 0.7499999999999999
Case Insensitive : P: 0.632 || R: 0.923 || F1: 0.75
256 UU_2002_25
Case Sensitive   : P: 0.06666666666666667 || R: 1.0 || F1: 0.125
Case Insensitive : P: 0.067 || R: 1.0 || F1: 0.126
257 Permen_Keu_2016_148
Case Sensitive   : P: 0.10526315789473684 || R: 0.2222222222222222 || F1: 0.14285714285714285
Case Insensitive : P: 0.105 || R: 0.222 || F1: 0.143
258 Perkot_Semarang_2004_14
Case Sensitive   : P: 0.631578947368421 || R: 0.8 || F1: 0.7058823529411765
Case Insensitive : P: 0.632 || R: 0.8 || F1: 0.706
259 Perprov_Jabar_2013_1
Case Sensitive   : P: 0.5789473684210527 || R: 0.5789473684210527 || F1: 

...

2248 UU_2002_24
Case Sensitive   : P: 0.05263157894736842 || R: 1.0 || F1: 0.1
Case Insensitive : P: 0.053 || R: 1.0 || F1: 0.101
2249 Perkab_Jayapura_2006_4
Case Sensitive   : P: 0.47368421052631576 || R: 0.5 || F1: 0.4864864864864865
Case Insensitive : P: 0.474 || R: 0.5 || F1: 0.487
2250 Perkab_Aceh_Tamiang_2011_9
Case Sensitive   : P: 0.05263157894736842 || R: 1.0 || F1: 0.1
Case Insensitive : P: 0.053 || R: 1.0 || F1: 0.101
2251 PP_1970_39
Case Sensitive   : P: 0.15789473684210525 || R: 0.5 || F1: 0.23999999999999996
Case Insensitive : P: 0.158 || R: 0.5 || F1: 0.24
2252 Permen_KP_2013_15
Case Sensitive   : P: 0.6842105263157895 || R: 1.0 || F1: 0.8125000000000001
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
2253 Permen_KP_2016_37
Case Sensitive   : P: 0.8421052631578947 || R: 0.8421052631578947 || F1: 0.8421052631578947
Case Insensitive : P: 0.842 || R: 0.842 || F1: 0.842
2254 Perkab_Boyolali_2011_7
Case Sensitive   : P: 0.5294117647058824 || R: 0.47368421052631576 || F1: 0

2332 Permen_Hub_2016_144
Case Sensitive   : P: 0.2631578947368421 || R: 0.4166666666666667 || F1: 0.3225806451612903
Case Insensitive : P: 0.263 || R: 0.417 || F1: 0.323
2333 Permen_Parekraf_2013_07
Case Sensitive   : P: 0.631578947368421 || R: 0.9230769230769231 || F1: 0.7499999999999999
Case Insensitive : P: 0.632 || R: 0.923 || F1: 0.75
2334 Peraturan_Polri_2013_2
Case Sensitive   : P: 0.6842105263157895 || R: 1.0 || F1: 0.8125000000000001
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
2335 Peraturan_KY_2016_4
Case Sensitive   : P: 0.3684210526315789 || R: 0.3684210526315789 || F1: 0.3684210526315789
Case Insensitive : P: 0.368 || R: 0.368 || F1: 0.368
2336 Permen_Dag_2016_85
Case Sensitive   : P: 0.2631578947368421 || R: 0.2631578947368421 || F1: 0.2631578947368421
Case Insensitive : P: 0.263 || R: 0.263 || F1: 0.263
2337 Perkab_Purwakarta_2012_6
Case Sensitive   : P: 0.06666666666666667 || R: 0.08333333333333333 || F1: 0.07407407407407407
Case Insensitive : P: 0.067 || R: 0.08

2437 Perkot_Bandung_2000_04
Case Sensitive   : P: 0.05263157894736842 || R: 1.0 || F1: 0.1
Case Insensitive : P: 0.053 || R: 1.0 || F1: 0.101
2438 Permen_PR_2012_39
Case Sensitive   : P: 0.6842105263157895 || R: 1.0 || F1: 0.8125000000000001
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
2439 Perpres_2014_75
Case Sensitive   : P: 0.47368421052631576 || R: 1.0 || F1: 0.6428571428571429
Case Insensitive : P: 0.474 || R: 1.0 || F1: 0.643
2440 Perpres_2017_28
Case Sensitive   : P: 0.42105263157894735 || R: 0.6666666666666666 || F1: 0.5161290322580646
Case Insensitive : P: 0.421 || R: 0.667 || F1: 0.516
2441 Permen_Han_2014_64
Case Sensitive   : P: 0.47368421052631576 || R: 0.9 || F1: 0.6206896551724138
Case Insensitive : P: 0.474 || R: 0.9 || F1: 0.621
2442 Perkab_Rokan_Hilir_2013_6
Case Sensitive   : P: 0.3684210526315789 || R: 0.5384615384615384 || F1: 0.4375
Case Insensitive : P: 0.368 || R: 0.538 || F1: 0.437
2443 Peraturan_Perpusnas_2018_3
Case Sensitive   : P: 0.47368421052631576

2524 Permen_Dag_2019_16
Case Sensitive   : P: 0.3684210526315789 || R: 0.7 || F1: 0.48275862068965514
Case Insensitive : P: 0.368 || R: 0.7 || F1: 0.482
2525 Permen_Keu_2015_237
Case Sensitive   : P: 0.7894736842105263 || R: 0.7894736842105263 || F1: 0.7894736842105263
Case Insensitive : P: 0.789 || R: 0.789 || F1: 0.789
2526 Perprov_Riau_2013_17
Case Sensitive   : P: 0.5263157894736842 || R: 0.7692307692307693 || F1: 0.625
Case Insensitive : P: 0.526 || R: 0.769 || F1: 0.625
2527 Permen_PPPA_2010_10
Case Sensitive   : P: 0.21052631578947367 || R: 0.4444444444444444 || F1: 0.2857142857142857
Case Insensitive : P: 0.211 || R: 0.444 || F1: 0.286
2528 Peraturan_BSSN_2016_16
Case Sensitive   : P: 0.7894736842105263 || R: 0.9375 || F1: 0.8571428571428572
Case Insensitive : P: 0.789 || R: 0.938 || F1: 0.857
2529 Perkab_Musi_Rawas_2005_7
Case Sensitive   : P: 0.47368421052631576 || R: 0.6923076923076923 || F1: 0.5625
Case Insensitive : P: 0.474 || R: 0.692 || F1: 0.563
2530 Permen_KP_2016_28


Case Insensitive : P: 0.421 || R: 0.727 || F1: 0.533
2590 Perkab_Sleman_2001_8
Case Sensitive   : P: 0.5263157894736842 || R: 0.5555555555555556 || F1: 0.5405405405405405
Case Insensitive : P: 0.526 || R: 0.556 || F1: 0.541
2591 Peraturan_LAN_2015_42
Case Sensitive   : P: 0.5263157894736842 || R: 0.5263157894736842 || F1: 0.5263157894736842
Case Insensitive : P: 0.526 || R: 0.526 || F1: 0.526
2592 Peraturan_LAN_2016_5
Case Sensitive   : P: 0.3684210526315789 || R: 0.4375 || F1: 0.39999999999999997
Case Insensitive : P: 0.368 || R: 0.438 || F1: 0.4
2593 Permen_Dagri_2011_11
Case Sensitive   : P: 0.15789473684210525 || R: 0.5 || F1: 0.23999999999999996
Case Insensitive : P: 0.158 || R: 0.5 || F1: 0.24
2594 Perkab_Ponorogo_2011_4
Case Sensitive   : P: 0.5263157894736842 || R: 0.5555555555555556 || F1: 0.5405405405405405
Case Insensitive : P: 0.526 || R: 0.556 || F1: 0.541
2595 Permen_ESDM_2009_08
Case Sensitive   : P: 0.3684210526315789 || R: 0.5384615384615384 || F1: 0.4375
Case Insensit

In [53]:
test_1('cfp', cf_phi, test_closing, '1', 'results/metrics_cf.csv')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.7272727272727273 || R: 0.5 || F1: 0.5925925925925926
Case Insensitive : P: 0.727 || R: 0.5 || F1: 0.593
1 Permen_KP_2013_5
Case Sensitive   : P: 0.46153846153846156 || R: 0.46153846153846156 || F1: 0.46153846153846156
Case Insensitive : P: 0.538 || R: 0.538 || F1: 0.538
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.2222222222222222 || R: 0.2222222222222222 || F1: 0.2222222222222222
Case Insensitive : P: 0.222 || R: 0.222 || F1: 0.222
3 Permen_Par_2015_14
Case Sensitive   : P: 0.75 || R: 0.6923076923076923 || F1: 0.7199999999999999
Case Insensitive : P: 0.75 || R: 0.692 || F1: 0.72
4 Perpres_2019_67
Case Sensitive   : P: 0.5 || R: 0.3157894736842105 || F1: 0.3870967741935484
Case Insensitive : P: 0.5 || R: 0.316 || F1: 0.387
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.18181818181818182 || R: 0.15384615384615385 || F1: 0.16666666666666669
Case Insensitive : P: 0.182 || R: 0.154 || F1: 0.167
6 Perkab_Tabalong_2010_09
Case Sensit

58 Permen_Keu_2015_201
Case Sensitive   : P: 0.8181818181818182 || R: 0.5 || F1: 0.6206896551724137
Case Insensitive : P: 0.818 || R: 0.5 || F1: 0.621
59 Permen_Hub_2012_36
Case Sensitive   : P: 0.4 || R: 0.6153846153846154 || F1: 0.4848484848484849
Case Insensitive : P: 0.4 || R: 0.615 || F1: 0.485
60 Permen_Hut_2009_32
Case Sensitive   : P: 0.47058823529411764 || R: 0.8 || F1: 0.5925925925925927
Case Insensitive : P: 0.471 || R: 0.8 || F1: 0.593
61 Peraturan_KPU_2018_11
Case Sensitive   : P: 0.9166666666666666 || R: 0.6875 || F1: 0.7857142857142857
Case Insensitive : P: 0.917 || R: 0.688 || F1: 0.786
62 Permen_Tan_2017_49
Case Sensitive   : P: 0.29411764705882354 || R: 0.3125 || F1: 0.30303030303030304
Case Insensitive : P: 0.294 || R: 0.312 || F1: 0.303
63 Perkot_Sorong_2013_32
Case Sensitive   : P: 0.25 || R: 0.17647058823529413 || F1: 0.20689655172413793
Case Insensitive : P: 0.25 || R: 0.176 || F1: 0.207
64 Perkot_Bogor_2006_11
Case Sensitive   : P: 0.5 || R: 0.6 || F1: 0.5454545

126 Permen_Tan_2012_53
Case Sensitive   : P: 0.6470588235294118 || R: 0.8461538461538461 || F1: 0.7333333333333334
Case Insensitive : P: 0.647 || R: 0.846 || F1: 0.733
127 Perpres_2010_2
Case Sensitive   : P: 0.36363636363636365 || R: 0.4444444444444444 || F1: 0.39999999999999997
Case Insensitive : P: 0.364 || R: 0.444 || F1: 0.4
128 Permen_Dikbud_2012_58
Case Sensitive   : P: 0.38461538461538464 || R: 0.4166666666666667 || F1: 0.4
Case Insensitive : P: 0.462 || R: 0.5 || F1: 0.48
129 Peraturan_Basarnas_2017_17
Case Sensitive   : P: 0.6666666666666666 || R: 0.42105263157894735 || F1: 0.5161290322580646
Case Insensitive : P: 0.667 || R: 0.421 || F1: 0.516
130 Permen_ATRBPN_2018_16
Case Sensitive   : P: 0.5 || R: 0.3684210526315789 || F1: 0.4242424242424242
Case Insensitive : P: 0.5 || R: 0.368 || F1: 0.424
131 Permen_Perin_2018_9
Case Sensitive   : P: 0.8888888888888888 || R: 0.42105263157894735 || F1: 0.5714285714285714
Case Insensitive : P: 0.889 || R: 0.421 || F1: 0.571
132 UU_1953_1

193 Permen_Dag_2017_16
Case Sensitive   : P: 0.6363636363636364 || R: 0.4666666666666667 || F1: 0.5384615384615385
Case Insensitive : P: 0.636 || R: 0.467 || F1: 0.539
194 Permen_Dagri_2014_59
Case Sensitive   : P: 0.4444444444444444 || R: 0.7272727272727273 || F1: 0.5517241379310345
Case Insensitive : P: 0.444 || R: 0.727 || F1: 0.551
195 Permen_Humham_2017_12
Case Sensitive   : P: 0.5555555555555556 || R: 0.2631578947368421 || F1: 0.35714285714285715
Case Insensitive : P: 0.556 || R: 0.263 || F1: 0.357
196 Permen_Keu_2014_256
Case Sensitive   : P: 0.2777777777777778 || R: 0.8333333333333334 || F1: 0.4166666666666667
Case Insensitive : P: 0.278 || R: 0.833 || F1: 0.417
197 Permen_Par_2018_12
Case Sensitive   : P: 1.0 || R: 0.6842105263157895 || F1: 0.8125000000000001
Case Insensitive : P: 1.0 || R: 0.684 || F1: 0.812
198 Permen_Han_2014_03
Case Sensitive   : P: 0.25 || R: 0.3076923076923077 || F1: 0.27586206896551724
Case Insensitive : P: 0.25 || R: 0.308 || F1: 0.276
199 Peraturan_LA

260 Permen_ESDM_2018_4
Case Sensitive   : P: 0.8461538461538461 || R: 0.5789473684210527 || F1: 0.6875
Case Insensitive : P: 0.846 || R: 0.579 || F1: 0.687
261 PP_1985_32
Case Sensitive   : P: 0.16666666666666666 || R: 0.3333333333333333 || F1: 0.2222222222222222
Case Insensitive : P: 0.167 || R: 0.333 || F1: 0.222
262 Permen_Keu_2015_247
Case Sensitive   : P: 0.4 || R: 0.6666666666666666 || F1: 0.5
Case Insensitive : P: 0.4 || R: 0.667 || F1: 0.5
263 Permen_Hut_2014_89
Case Sensitive   : P: 0.35714285714285715 || R: 0.38461538461538464 || F1: 0.3703703703703704
Case Insensitive : P: 0.357 || R: 0.385 || F1: 0.37
264 Perkab_Sukabumi_2012_8
Case Sensitive   : P: 0.6363636363636364 || R: 0.5384615384615384 || F1: 0.5833333333333334
Case Insensitive : P: 0.636 || R: 0.538 || F1: 0.583
265 Permen_Agama_2012_39
Case Sensitive   : P: 0.4166666666666667 || R: 0.38461538461538464 || F1: 0.4
Case Insensitive : P: 0.417 || R: 0.385 || F1: 0.4
266 UU_1999_41
Case Sensitive   : P: 0.11111111111111

...

Case Insensitive : P: 0.056 || R: 1.0 || F1: 0.106
2041 PP_1998_18
Case Sensitive   : P: 0.3076923076923077 || R: 0.5714285714285714 || F1: 0.4
Case Insensitive : P: 0.308 || R: 0.571 || F1: 0.4
2042 Permen_Keu_2013_43
Case Sensitive   : P: 0.25 || R: 0.4444444444444444 || F1: 0.32
Case Insensitive : P: 0.312 || R: 0.556 || F1: 0.4
2043 Permen_Tan_2012_42
Case Sensitive   : P: 0.42857142857142855 || R: 0.5 || F1: 0.4615384615384615
Case Insensitive : P: 0.429 || R: 0.5 || F1: 0.462
2044 Permen_LHK_2017_61
Case Sensitive   : P: 0.6428571428571429 || R: 0.5625 || F1: 0.6000000000000001
Case Insensitive : P: 0.643 || R: 0.562 || F1: 0.6
2045 Permen_Dag_2018_38
Case Sensitive   : P: 0.7142857142857143 || R: 0.5555555555555556 || F1: 0.6250000000000001
Case Insensitive : P: 0.714 || R: 0.556 || F1: 0.625
2046 UU_2002_20
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2047 PP_1987_14
Case Sensitive   : P: 0.3076923076923077 || R: 0.4444444444444444 |

2200 Perkab_Banjar_2012_2
Case Sensitive   : P: 0.4166666666666667 || R: 0.3333333333333333 || F1: 0.3703703703703704
Case Insensitive : P: 0.417 || R: 0.333 || F1: 0.37
2201 Permen_Naker_2015_15
Case Sensitive   : P: 0.4117647058823529 || R: 0.7 || F1: 0.5185185185185185
Case Insensitive : P: 0.412 || R: 0.7 || F1: 0.519
2202 Peraturan_BWI_2012_1
Case Sensitive   : P: 0.3333333333333333 || R: 0.3333333333333333 || F1: 0.3333333333333333
Case Insensitive : P: 0.333 || R: 0.333 || F1: 0.333
2203 UU_1992_9
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2204 Permen_PPPA_2011_13
Case Sensitive   : P: 0.3076923076923077 || R: 0.3333333333333333 || F1: 0.32
Case Insensitive : P: 0.308 || R: 0.333 || F1: 0.32
2205 Permen_Dagri_2019_36
Case Sensitive   : P: 0.5 || R: 0.5833333333333334 || F1: 0.5384615384615384
Case Insensitive : P: 0.5 || R: 0.583 || F1: 0.538
2206 Peraturan_Polri_2017_8
Case Sensitive   : P: 0.8333333333333334 || R: 0.52631578947368

2300 Permen_Hub_2014_51
Case Sensitive   : P: 0.25 || R: 0.4 || F1: 0.3076923076923077
Case Insensitive : P: 0.25 || R: 0.4 || F1: 0.308
2301 Permen_Dagri_2017_90
Case Sensitive   : P: 0.8333333333333334 || R: 0.7894736842105263 || F1: 0.8108108108108109
Case Insensitive : P: 0.833 || R: 0.789 || F1: 0.81
2302 Perkab_Sukamara_2006_02
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2303 Peraturan_KPU_2018_20
Case Sensitive   : P: 0.9166666666666666 || R: 0.5789473684210527 || F1: 0.7096774193548387
Case Insensitive : P: 0.917 || R: 0.579 || F1: 0.71
2304 Permen_BUMN_2014_08
Case Sensitive   : P: 0 || R: 0.0 || F1: 0
Case Insensitive : P: 0 || R: 0.0 || F1: 0
2305 Permen_Dikbud_2016_35
Case Sensitive   : P: 0.6153846153846154 || R: 0.5333333333333333 || F1: 0.5714285714285715
Case Insensitive : P: 0.692 || R: 0.6 || F1: 0.643
2306 Permen_Han_2009_14
Case Sensitive   : P: 0.5384615384615384 || R: 0.5384615384615384 || F1: 0.5384615384615384
Case I

2444 Perprov_Kep_Riau_2011_8
Case Sensitive   : P: 0.45454545454545453 || R: 0.5 || F1: 0.47619047619047616
Case Insensitive : P: 0.455 || R: 0.5 || F1: 0.476
2445 Permen_Kes_2011_2356
Case Sensitive   : P: 0.18181818181818182 || R: 0.2222222222222222 || F1: 0.19999999999999998
Case Insensitive : P: 0.182 || R: 0.222 || F1: 0.2
2446 Permen_Keu_2013_179
Case Sensitive   : P: 0.2857142857142857 || R: 0.4444444444444444 || F1: 0.34782608695652173
Case Insensitive : P: 0.286 || R: 0.444 || F1: 0.348
2447 PP_2015_62
Case Sensitive   : P: 0.3157894736842105 || R: 1.0 || F1: 0.4799999999999999
Case Insensitive : P: 0.316 || R: 1.0 || F1: 0.48
2448 Permen_Keu_2009_180
Case Sensitive   : P: 0.4 || R: 0.4 || F1: 0.4000000000000001
Case Insensitive : P: 0.4 || R: 0.4 || F1: 0.4
2449 Peraturan_BPH_Migas_2013_10
Case Sensitive   : P: 0.36363636363636365 || R: 0.4444444444444444 || F1: 0.39999999999999997
Case Insensitive : P: 0.364 || R: 0.444 || F1: 0.4
2450 Permen_Dikbud_2018_28
Case Sensitive   

2561 Permen_Kopukm_2013_09
Case Sensitive   : P: 0.36363636363636365 || R: 0.3333333333333333 || F1: 0.34782608695652173
Case Insensitive : P: 0.364 || R: 0.333 || F1: 0.348
2562 Perkot_Samarinda_2006_09
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2563 Perkab_Rokan_Hilir_2014_6
Case Sensitive   : P: 0.18181818181818182 || R: 0.15384615384615385 || F1: 0.16666666666666669
Case Insensitive : P: 0.182 || R: 0.154 || F1: 0.167
2564 UU_2007_36
Case Sensitive   : P: 0.08333333333333333 || R: 1.0 || F1: 0.15384615384615385
Case Insensitive : P: 0.083 || R: 1.0 || F1: 0.153
2565 Permen_Keu_2015_229
Case Sensitive   : P: 0.8181818181818182 || R: 0.6 || F1: 0.6923076923076923
Case Insensitive : P: 0.818 || R: 0.6 || F1: 0.692
2566 Peraturan_BPH_Migas_2018_10
Case Sensitive   : P: 0.8181818181818182 || R: 0.5 || F1: 0.6206896551724137
Case Insensitive : P: 0.818 || R: 0.5 || F1: 0.621
2567 UU_1957_49
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case I

In [54]:
test_1('cfp', cf_phi, test_closing, '2', 'results/metrics_cf.csv')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.6 || R: 0.5625 || F1: 0.5806451612903225
Case Insensitive : P: 0.6 || R: 0.562 || F1: 0.58
1 Permen_KP_2013_5
Case Sensitive   : P: 0.5789473684210527 || R: 0.8461538461538461 || F1: 0.6875
Case Insensitive : P: 0.684 || R: 1.0 || F1: 0.812
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.375 || R: 0.6666666666666666 || F1: 0.4800000000000001
Case Insensitive : P: 0.375 || R: 0.667 || F1: 0.48
3 Permen_Par_2015_14
Case Sensitive   : P: 0.75 || R: 0.9230769230769231 || F1: 0.8275862068965517
Case Insensitive : P: 0.75 || R: 0.923 || F1: 0.828
4 Perpres_2019_67
Case Sensitive   : P: 0.6842105263157895 || R: 0.6842105263157895 || F1: 0.6842105263157895
Case Insensitive : P: 0.684 || R: 0.684 || F1: 0.684
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.05263157894736842 || R: 0.07692307692307693 || F1: 0.0625
Case Insensitive : P: 0.053 || R: 0.077 || F1: 0.063
6 Perkab_Tabalong_2010_09
Case Sensitive   : P: 0.8947368421052632 || R: 0.8

93 PP_1999_88
Case Sensitive   : P: 0.375 || R: 0.6666666666666666 || F1: 0.4800000000000001
Case Insensitive : P: 0.375 || R: 0.667 || F1: 0.48
94 UU_2007_38
Case Sensitive   : P: 0.0625 || R: 1.0 || F1: 0.11764705882352941
Case Insensitive : P: 0.062 || R: 1.0 || F1: 0.117
95 Permen_PANRB_2017_25
Case Sensitive   : P: 0.8 || R: 0.6666666666666666 || F1: 0.7272727272727272
Case Insensitive : P: 0.8 || R: 0.667 || F1: 0.727
96 Permen_Keu_2015_232
Case Sensitive   : P: 0.8461538461538461 || R: 0.5789473684210527 || F1: 0.6875
Case Insensitive : P: 0.846 || R: 0.579 || F1: 0.687
97 Permen_Dag_2017_82
Case Sensitive   : P: 0.6875 || R: 0.7333333333333333 || F1: 0.7096774193548386
Case Insensitive : P: 0.688 || R: 0.733 || F1: 0.71
98 Permen_Dagri_2018_92
Case Sensitive   : P: 0.6153846153846154 || R: 0.5333333333333333 || F1: 0.5714285714285715
Case Insensitive : P: 0.615 || R: 0.533 || F1: 0.571
99 Permen_Desa_2017_23
Case Sensitive   : P: 0.6875 || R: 0.7333333333333333 || F1: 0.7096774

Case Insensitive : P: 0.538 || R: 0.7 || F1: 0.608
234 Permen_LHK_2019_56
Case Sensitive   : P: 0.9230769230769231 || R: 0.75 || F1: 0.8275862068965517
Case Insensitive : P: 0.923 || R: 0.75 || F1: 0.828
235 Permen_PR_2011_09
Case Sensitive   : P: 0.4 || R: 0.46153846153846156 || F1: 0.42857142857142855
Case Insensitive : P: 0.4 || R: 0.462 || F1: 0.429
236 Permen_Dagri_2013_67
Case Sensitive   : P: 0.375 || R: 0.46153846153846156 || F1: 0.41379310344827586
Case Insensitive : P: 0.375 || R: 0.462 || F1: 0.414
237 Perprov_Kalbar_2001_7
Case Sensitive   : P: 0.38461538461538464 || R: 0.45454545454545453 || F1: 0.41666666666666663
Case Insensitive : P: 0.385 || R: 0.455 || F1: 0.417
238 Permen_Tan_2015_53
Case Sensitive   : P: 0.46153846153846156 || R: 0.6 || F1: 0.5217391304347826
Case Insensitive : P: 0.462 || R: 0.6 || F1: 0.522
239 Permen_Keu_2015_78
Case Sensitive   : P: 0.23076923076923078 || R: 0.5 || F1: 0.3157894736842105
Case Insensitive : P: 0.231 || R: 0.5 || F1: 0.316
240 PP_

300 Perprov_Jabar_2001_19
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
301 Perprov_Banten_2010_8
Case Sensitive   : P: 0.05263157894736842 || R: 1.0 || F1: 0.1
Case Insensitive : P: 0.053 || R: 1.0 || F1: 0.101
302 Permen_Kes_2013_89
Case Sensitive   : P: 0.42857142857142855 || R: 0.46153846153846156 || F1: 0.4444444444444445
Case Insensitive : P: 0.429 || R: 0.462 || F1: 0.445
303 Permen_Keu_2014_47
Case Sensitive   : P: 0.46153846153846156 || R: 0.6666666666666666 || F1: 0.5454545454545455
Case Insensitive : P: 0.462 || R: 0.667 || F1: 0.546
304 Permen_Keu_2009_86
Case Sensitive   : P: 0.38461538461538464 || R: 0.5555555555555556 || F1: 0.4545454545454546
Case Insensitive : P: 0.385 || R: 0.556 || F1: 0.455
305 Permen_Keu_2016_33
Case Sensitive   : P: 0.7692307692307693 || R: 0.6666666666666666 || F1: 0.7142857142857142
Case Insensitive : P: 0.769 || R: 0.667 || F1: 0.714
306 Peraturan_MA_2016_13
Case Sensitive   : P: 0.75 || R: 0.75 || F1

377 Permen_Nakertrans_2010_11
Case Sensitive   : P: 0.5 || R: 0.5384615384615384 || F1: 0.5185185185185186
Case Insensitive : P: 0.571 || R: 0.615 || F1: 0.592
378 Permen_Sos_2017_6
Case Sensitive   : P: 0.8461538461538461 || R: 0.6111111111111112 || F1: 0.7096774193548387
Case Insensitive : P: 0.846 || R: 0.611 || F1: 0.71
379 Permen_Tan_2017_26
Case Sensitive   : P: 0.5 || R: 0.4444444444444444 || F1: 0.47058823529411764
Case Insensitive : P: 0.5 || R: 0.444 || F1: 0.47
380 Permen_Ristekdikti_2016_67
Case Sensitive   : P: 0.6923076923076923 || R: 0.5625 || F1: 0.6206896551724138
Case Insensitive : P: 0.692 || R: 0.562 || F1: 0.62
381 Permen_Dikbud_2016_27
Case Sensitive   : P: 0.6 || R: 0.6 || F1: 0.6
Case Insensitive : P: 0.667 || R: 0.667 || F1: 0.667
382 Perprov_Sumbar_2012_16
Case Sensitive   : P: 0.15789473684210525 || R: 1.0 || F1: 0.2727272727272727
Case Insensitive : P: 0.158 || R: 1.0 || F1: 0.273
383 Perpres_2017_134
Case Sensitive   : P: 0.42105263157894735 || R: 0.5333333

...

Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7fc360f09000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", line 203, in parse_date
    raise ISO8601Error('Unrecognised ISO 8601 date format: %r' % datestring)
isodate.isoerror.ISO8601Error: Unrecognised ISO 8601 date format: ' '
Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7fc360f09000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", line 203, in 

2418 PP_1996_14
Case Sensitive   : P: 0.3684210526315789 || R: 1.0 || F1: 0.5384615384615384
Case Insensitive : P: 0.368 || R: 1.0 || F1: 0.538
2419 Peraturan_LKPP_2018_11
Case Sensitive   : P: 1.0 || R: 0.6842105263157895 || F1: 0.8125000000000001
Case Insensitive : P: 1.0 || R: 0.684 || F1: 0.812
2420 PP_1980_51
Case Sensitive   : P: 0.2777777777777778 || R: 0.3333333333333333 || F1: 0.303030303030303
Case Insensitive : P: 0.278 || R: 0.333 || F1: 0.303
2421 Permen_Keu_2014_100
Case Sensitive   : P: 0.15789473684210525 || R: 1.0 || F1: 0.2727272727272727
Case Insensitive : P: 0.158 || R: 1.0 || F1: 0.273
2422 Perkot_Tasikmalaya_2004_16
Case Sensitive   : P: 0.07692307692307693 || R: 0.25 || F1: 0.11764705882352941
Case Insensitive : P: 0.077 || R: 0.25 || F1: 0.118
2423 Perkot_Binjai_2001_26
Case Sensitive   : P: 0.09090909090909091 || R: 1.0 || F1: 0.16666666666666669
Case Insensitive : P: 0.091 || R: 1.0 || F1: 0.167
2424 PP_1986_23
Case Sensitive   : P: 0.5 || R: 0.6 || F1: 0.5454

2500 Permen_ESDM_2014_36
Case Sensitive   : P: 0.47368421052631576 || R: 0.6923076923076923 || F1: 0.5625
Case Insensitive : P: 0.526 || R: 0.769 || F1: 0.625
2501 Peraturan_Polri_2015_18
Case Sensitive   : P: 0.631578947368421 || R: 0.631578947368421 || F1: 0.631578947368421
Case Insensitive : P: 0.632 || R: 0.632 || F1: 0.632
2502 Perkot_Pangkalpinang_2006_12
Case Sensitive   : P: 0.4375 || R: 0.7777777777777778 || F1: 0.56
Case Insensitive : P: 0.438 || R: 0.778 || F1: 0.56
2503 Permen_LH_2011_3
Case Sensitive   : P: 0.5384615384615384 || R: 0.5384615384615384 || F1: 0.5384615384615384
Case Insensitive : P: 0.538 || R: 0.538 || F1: 0.538
2504 Perprov_Kalbar_2004_1
Case Sensitive   : P: 0.3076923076923077 || R: 0.3076923076923077 || F1: 0.3076923076923077
Case Insensitive : P: 0.308 || R: 0.308 || F1: 0.308
2505 Perkab_Garut_2008_17
Case Sensitive   : P: 0.05263157894736842 || R: 1.0 || F1: 0.1
Case Insensitive : P: 0.053 || R: 1.0 || F1: 0.101
2506 Permen_Humham_2016_60
Case Sensiti

Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7fc360f09000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/isodates.py", line 203, in parse_date
    raise ISO8601Error('Unrecognised ISO 8601 date format: %r' % datestring)
isodate.isoerror.ISO8601Error: Unrecognised ISO 8601 date format: '"GUBERNUR RIAU"^^xsd:string'
Failed to convert Literal lexical form to value. Datatype=http://www.w3.org/2001/XMLSchema#date, Converter=<function parse_date at 0x7fc360f09000>
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/rdflib/term.py", line 2119, in _castLexicalToPython
    return conv_func(lexical)  # type: ignore[arg-type]
  File "/usr/local/lib/python3.10/dist-packages/isodate/i

2562 Perkot_Samarinda_2006_09
Case Sensitive   : P: 0.3684210526315789 || R: 1.0 || F1: 0.5384615384615384
Case Insensitive : P: 0.368 || R: 1.0 || F1: 0.538
2563 Perkab_Rokan_Hilir_2014_6
Case Sensitive   : P: 0.4375 || R: 0.5384615384615384 || F1: 0.4827586206896552
Case Insensitive : P: 0.438 || R: 0.538 || F1: 0.483
2564 UU_2007_36
Case Sensitive   : P: 0.07692307692307693 || R: 1.0 || F1: 0.14285714285714288
Case Insensitive : P: 0.077 || R: 1.0 || F1: 0.143
2565 Permen_Keu_2015_229
Case Sensitive   : P: 0.7692307692307693 || R: 0.6666666666666666 || F1: 0.7142857142857142
Case Insensitive : P: 0.769 || R: 0.667 || F1: 0.714
2566 Peraturan_BPH_Migas_2018_10
Case Sensitive   : P: 0.7692307692307693 || R: 0.5555555555555556 || F1: 0.6451612903225806
Case Insensitive : P: 0.769 || R: 0.556 || F1: 0.645
2567 UU_1957_49
Case Sensitive   : P: 0.05263157894736842 || R: 1.0 || F1: 0.1
Case Insensitive : P: 0.053 || R: 1.0 || F1: 0.101
2568 Permen_Dagri_2011_41
Case Sensitive   : P: 0.3333

In [63]:
print(test_closing[3]['triples'])
print()
print(test_closing[3]['text'])

lexid:Position_Menteri_Pariwisata_Republik_Indonesia rdfs:label "Menteri Pariwisata Republik Indonesia"^^xsd:string .
lexid:Permen_Par_2015_14 lexid-s:hasPromulgationPlace lexid:Berita_Negara .
lexid:City_Jakarta rdfs:label "Jakarta"^^xsd:string .
lexid:Permen_Par_2015_14 lexid-s:hasEnactionLocation lexid:City_Jakarta .
lexid:Permen_Par_2015_14 lexid-s:hasPromulgationLocation lexid:City_Jakarta .
lexid:Person_Arief_Yahya rdf:type lexid-s:Person .
lexid:Permen_Par_2015_14 lexid-s:hasEnactionDate "2015-10-08"^^xsd:date .
lexid:Position_Menteri_Pariwisata_Republik_Indonesia rdf:type lexid-s:Position .
lexid:Person_Arief_Yahya rdfs:label "Arief Yahya"^^xsd:string .
lexid:Permen_Par_2015_14 lexid-s:hasEnactionOfficial lexid:Person_Arief_Yahya .
lexid:Permen_Par_2015_14 lexid-s:hasEnactionOffice lexid:Position_Menteri_Pariwisata_Republik_Indonesia .
lexid:Permen_Par_2015_14 lexid-s:hasPromulgationDate "2015-10-28"^^xsd:date .
lexid:City_Jakarta rdf:type lexid-s:City .

Pasal 4

Peraturan Men

In [50]:
print(cc_gemma.at[2627, 'ttl_1'])
print('######################')
print(test_closing[2627]['triples'])

@prefix xsd: <http://www.w3.org/2001/XMLSchema#> .
@prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> .
@prefix rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> .
@prefix dbo: <http://dbpedia.org/ontology/> .
@prefix dct: <http://purl.org/dc/terms/> .
@prefix owl: <http://www.w3.org/2002/07/owl#> .
@prefix wd: <https://www.wikidata.org/wiki/> .
@prefix lexid-s: <https://w3id.org/lex-id/schema/> .
@prefix lexid: <https://w3id.org/lex-id/data/> .

lexid:Peraturan_LAN_2016_3 lexid-s:hasPromulgationPlace lexid:Berita_Negara .
lexid:Peraturan_LAN_2016_3 lexid-s:hasEnactionDate "2016-01-12"^^xsd:date .
lexid:Peraturan_LAN_2016_3 lexid-s:hasEnactionLocation lexid:City_Jakarta .
lexid:City_Jakarta rdf:type lexid-s:City .
lexid:City_Jakarta rdfs:label "Jakarta"^^xsd:string .
lexid:Peraturan_LAN_2016_3 lexid-s:hasEnactionOfficial lexid:Person_Adi_Suryanto .
lexid:Person_Adi_Suryanto rdf:type lexid-s:Person .
lexid:Person_Adi_Suryanto rdfs:label "Adi Suryanto"^^xsd:string .
lexid:Peraturan_L

In [18]:
print(cc_gemma.at[15, '1'])

@prefix xsd: <http://www.w3.org/2001/XMLSchema#> .
@prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> .
@prefix rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> .
@prefix dbo: <http://dbpedia.org/ontology/> .
@prefix dct: <http://purl.org/dc/terms/> .
@prefix owl: <http://www.w3.org/2002/07/owl#> .
@prefix wd: <https://www.wikidata.org/wiki/> .
@prefix lexid-s: <https://w3id.org/lex-id/schema/> .
@prefix lexid: <https://w3id.org/lex-id/data/> .

lexid:PP_1986_37 lexid-s:hasPromulgationPlace lexid:Lembaran_Negara .
lexid:PP_1986_37 lexid-s:hasEnactionDate "1986-08-23"^^xsd:date .
lexid:PP_1986_37 lexid-s:hasEnactionLocation lexid:City_Jakarta .
lexid:City_Jakarta rdf:type lexid-s:City .
lexid:City_Jakarta rdfs:label "Jakarta"^^xsd:string .
lexid:PP_1986_37 lexid-s:hasEnactionOfficial lexid:Person_Soeharto .
lexid:Person_Soeharto rdf:type lexid-s:Person .
lexid:Person_Soeharto rdfs:label "Soeharto"^^xsd:string .
lexid:PP_1986_37 lexid-s:hasEnactionOffice lexid:Position_Presiden_Repu

In [82]:
def print_info(df, dataset, idx, kol):
    print(df.at[idx, kol])
    print()
    print(dataset[idx]['triples'])
    print()
    print(dataset[idx]['text'])

In [81]:
metrics = pd.read_csv('results/metrics_code.csv')
metrics

Unnamed: 0                  regulatory   ccg_p_1   ccg_r_1  ccg_f1_1  \
0              0  Permen_Ristekdikti_2017_20  0.526316  0.625000  0.571429   
1              1            Permen_KP_2013_5  0.526316  0.769231  0.625000   
2              2         Permen_Keu_2011_249  0.263158  0.555556  0.357143   
3              3          Permen_Par_2015_14  0.684211  1.000000  0.812500   
4              4             Perpres_2019_67  0.684211  0.684211  0.684211   
...          ...                         ...       ...       ...       ...   
2634        2634       Peraturan_BPS_2012_49  0.684211  1.000000  0.812500   
2635        2635        Permen_Dagri_2019_15  0.315789  0.666667  0.428571   
2636        2636                  UU_2002_10  0.052632  1.000000  0.100000   
2637        2637         Peraturan_MA_2017_4  0.315789  0.500000  0.387097   
2638        2638            Perpres_2014_108  0.473684  1.000000  0.642857   

       ccg_p_2   ccg_r_2  ccg_f1_2   ccl_p_1   ccl_r_1  ccl_f1_1   ccl_p_2  \
0     0.473684  0.562500  0.514286  0.526316  0.625000  0.571429  0.684211   
1     0.526316  0.769231  0.625000  0.684211  1.000000  0.812500  0.315789   
2     0.263158  0.555556  0.357143  0.315789  0.666667  0.428571  0.157895   
3     0.631579  0.923077  0.750000  0.315789  0.461538  0.375000  0.473684   
4     0.684211  0.684211  0.684211  0.684211  0.684211  0.684211  0.684211   
...        ...       ...       ...       ...       ...       ...       ...   
2634  0.631579  0.923077  0.750000  0.684211  1.000000  0.812500  0.631579   
2635  0.263158  0.555556  0.357143  0.315789  0.666667  0.428571  0.315789   
2636  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.052632   
2637  0.263158  0.416667  0.322581  0.315789  0.500000  0.387097  0.315789   
2638  0.473684  1.000000  0.642857  0.473684  1.000000  0.642857  0.473684   

       ccl_r_2  ccl_f1_2   ccp_p_1   ccp_r_1  ccp_f1_1   ccp_p_2   ccp_r_2  \
0     0.812500  0.742857  0.526316  0.625000  0.571429  0.473684  0.562500   
1     0.461538  0.375000  0.333333  0.461538  0.387097  0.526316  0.769231   
2     0.333333  0.214286  0.157895  0.333333  0.214286  0.157895  0.333333   
3     0.692308  0.562500  0.473684  0.692308  0.562500  0.631579  0.923077   
4     0.684211  0.684211  0.684211  0.684211  0.684211  0.842105  0.842105   
...        ...       ...       ...       ...       ...       ...       ...   
2634  0.923077  0.750000  0.500000  0.692308  0.580645  0.473684  0.692308   
2635  0.666667  0.428571  0.368421  0.777778  0.500000  0.368421  0.777778   
2636  1.000000  0.100000  0.052632  1.000000  0.100000  0.052632  1.000000   
2637  0.500000  0.387097  0.473684  0.750000  0.580645  0.444444  0.666667   
2638  1.000000  0.642857  0.444444  0.888889  0.592593  0.473684  1.000000   

      ccp_f1_2  
0     0.514286  
1     0.625000  
2     0.214286  
3     0.750000  
4     0.842105  
...        ...  
2634  0.562500  
2635  0.500000  
2636  0.100000  
2637  0.533333  
2638  0.642857  

[2639 rows x 20 columns]

In [92]:
metrics = pd.read_csv('results/metrics_code.csv')
metrics

Unnamed: 0                  regulatory   ccg_p_1   ccg_r_1  ccg_f1_1  \
0              0  Permen_Ristekdikti_2017_20  0.526316  0.625000  0.571429   
1              1            Permen_KP_2013_5  0.526316  0.769231  0.625000   
2              2         Permen_Keu_2011_249  0.263158  0.555556  0.357143   
3              3          Permen_Par_2015_14  0.684211  1.000000  0.812500   
4              4             Perpres_2019_67  0.684211  0.684211  0.684211   
...          ...                         ...       ...       ...       ...   
2634        2634       Peraturan_BPS_2012_49  0.684211  1.000000  0.812500   
2635        2635        Permen_Dagri_2019_15  0.315789  0.666667  0.428571   
2636        2636                  UU_2002_10  0.052632  1.000000  0.100000   
2637        2637         Peraturan_MA_2017_4  0.315789  0.500000  0.387097   
2638        2638            Perpres_2014_108  0.473684  1.000000  0.642857   

       ccg_p_2   ccg_r_2  ccg_f1_2   ccl_p_1   ccl_r_1  ...  ocl_f1_1  \
0     0.473684  0.562500  0.514286  0.526316  0.625000  ...  0.692308   
1     0.526316  0.769231  0.625000  0.684211  1.000000  ...  0.611765   
2     0.263158  0.555556  0.357143  0.315789  0.666667  ...  0.666667   
3     0.631579  0.923077  0.750000  0.315789  0.461538  ...  0.635294   
4     0.684211  0.684211  0.684211  0.684211  0.684211  ...  0.705882   
...        ...       ...       ...       ...       ...  ...       ...   
2634  0.631579  0.923077  0.750000  0.684211  1.000000  ...  0.466667   
2635  0.263158  0.555556  0.357143  0.315789  0.666667  ...  0.346154   
2636  0.000000  0.000000  0.000000  0.000000  0.000000  ...  0.216867   
2637  0.263158  0.416667  0.322581  0.315789  0.500000  ...  0.571429   
2638  0.473684  1.000000  0.642857  0.473684  1.000000  ...  0.654206   

       ocl_p_2   ocl_r_2  ocl_f1_2   ocp_p_1   ocp_r_1  ocp_f1_1   ocp_p_2  \
0     0.743590  0.725000  0.734177  0.641026  0.625000  0.632911  0.466667   
1     0.571429  0.666667  0.615385  0.466667  0.583333  0.518519  0.533333   
2     0.619048  0.722222  0.666667  0.571429  0.666667  0.615385  0.692308   
3     0.690476  0.674419  0.682353  0.648649  0.558140  0.600000  0.642857   
4     0.629630  0.708333  0.666667  0.592593  0.666667  0.627451  0.518519   
...        ...       ...       ...       ...       ...       ...       ...   
2634  0.369231  0.705882  0.484848  0.290909  0.470588  0.359551  0.338028   
2635  0.571429  0.289855  0.384615  0.588235  0.289855  0.388350  0.485714   
2636  0.232558  0.243902  0.238095  0.700000  0.682927  0.691358  0.600000   
2637  0.777778  0.724138  0.750000  0.485714  0.586207  0.531250  0.629630   
2638  0.761905  0.744186  0.752941  0.717391  0.767442  0.741573  0.517241   

       ocp_r_2  ocp_f1_2  
0     0.175000  0.254545  
1     0.222222  0.313725  
2     0.500000  0.580645  
3     0.209302  0.315789  
4     0.583333  0.549020  
...        ...       ...  
2634  0.705882  0.457143  
2635  0.246377  0.326923  
2636  0.658537  0.627907  
2637  0.586207  0.607143  
2638  0.697674  0.594059  

[2639 rows x 38 columns]

In [83]:
print_info(cc_llama, test_closing, 2, '2')

lexid:Permen_Keu_2011_249 lexid-s:hasPromulgationPlace lexid:Berita_Negara .
lexid:Permen_Keu_2011_249 lexid-s:hasEnactionDate "2011-12-28"^^xsd:date .
lexid:Permen_Keu_2011_249 lexid-s:hasEnactionLocation lexid:City_Jakarta .
lexid:City_Jakarta rdf:type lexid-s:City .
lexid:City_Jakarta rdfs:label "Jakarta"^^xsd:string .
lexid:Permen_Keu_2011_249 lexid-s:hasEnactionOfficial lexid:Person_Agus_Dw_Martowardojo .
lexid:Person_Agus_Dw_Martowardojo rdf:type lexid-s:Person .
lexid:Person_Agus_Dw_Martowardojo rdfs:label "Agus D.W. Martowardojo"^^xsd:string .
lexid:Permen_Keu_2011_249 lexid-s:hasEnactionOffice lexid:Position_Menteri_Keuangan .
lexid:Position_Menteri_Keuangan rdf:type lexid-s:Position .
lexid:Position_Menteri_Keuangan rdfs:label "Menteri Keuangan"^^xsd:string .
lexid:Permen_Keu_2011_249 lexid-s:hasPromulgationDate "2011-12-28"^^xsd:date .
lexid:Permen_Keu_2011_249 lexid-s:hasPromulgationLocation lexid:City_Jakarta .
lexid:City_Jakarta rdf:type lexid-s:City .
lexid:City_Jakarta 

# Opening

In [35]:
test_opening_name = "dataset-surface-info/new-opening/new-opening-1"
test_opening = load_from_disk(test_opening_name)
len(test_opening)

2640

In [26]:
of_gemma = pd.read_csv('results/new/OF_gemma_post.csv')
of_llama = pd.read_csv('results/new/OF_llama_post.csv')
of_phi = pd.read_csv('results/new/OF_phi_post.csv')

In [10]:
results = pd.DataFrame()
results = pd.DataFrame(columns=['regulatory'
                                , 'ofg_p_1'
                                , 'ofg_r_1'
                                , 'ofg_f1_1'
                                , 'ofg_p_2'
                                , 'ofg_r_2'
                                , 'ofg_f1_2'
                                , 'ofl_p_1'
                                , 'ofl_r_1'
                                , 'ofl_f1_1'
                                , 'ofl_p_2'
                                , 'ofl_r_2'
                                , 'ofl_f1_2'
                                , 'ofp_p_1'
                                , 'ofp_r_1'
                                , 'ofp_f1_1'
                                , 'ofp_p_2'
                                , 'ofp_r_2'
                                , 'ofp_f1_2'
                               ])

In [36]:
test_1('ofg', of_gemma, test_opening, '1', 'results/metrics_of.csv')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.175 || R: 0.175 || F1: 0.175
Case Insensitive : P: 0.2 || R: 0.2 || F1: 0.2
1 Permen_KP_2013_5
Case Sensitive   : P: 0.09090909090909091 || R: 0.1111111111111111 || F1: 0.09999999999999999
Case Insensitive : P: 0.136 || R: 0.167 || F1: 0.15
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.5 || R: 0.6111111111111112 || F1: 0.55
Case Insensitive : P: 0.545 || R: 0.667 || F1: 0.6
3 Permen_Par_2015_14
Case Sensitive   : P: 0.18604651162790697 || R: 0.18604651162790697 || F1: 0.18604651162790695
Case Insensitive : P: 0.209 || R: 0.209 || F1: 0.209
4 Perpres_2019_67
Case Sensitive   : P: 0.2857142857142857 || R: 0.3333333333333333 || F1: 0.30769230769230765
Case Insensitive : P: 0.321 || R: 0.375 || F1: 0.346
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.06766917293233082 || R: 0.05625 || F1: 0.061433447098976114
Case Insensitive : P: 0.075 || R: 0.062 || F1: 0.068
6 Perkab_Tabalong_2010_09
Case Sensitive   : P: 0.046875 || R: 0.0612244

Case Insensitive : P: 0.292 || R: 0.35 || F1: 0.318
63 Perkot_Sorong_2013_32
Case Sensitive   : P: 0.10294117647058823 || R: 0.1076923076923077 || F1: 0.10526315789473685
Case Insensitive : P: 0.118 || R: 0.123 || F1: 0.12
64 Perkot_Bogor_2006_11
Case Sensitive   : P: 0.33064516129032256 || R: 0.3360655737704918 || F1: 0.3333333333333333
Case Insensitive : P: 0.339 || R: 0.344 || F1: 0.341
65 Perprov_Jateng_2001_10
Case Sensitive   : P: 0.15217391304347827 || R: 0.1794871794871795 || F1: 0.16470588235294117
Case Insensitive : P: 0.152 || R: 0.179 || F1: 0.164
66 PP_2008_70
Case Sensitive   : P: 0.6956521739130435 || R: 0.6666666666666666 || F1: 0.6808510638297872
Case Insensitive : P: 0.696 || R: 0.667 || F1: 0.681
67 Permen_Dikbud_2012_7
Case Sensitive   : P: 0.27906976744186046 || R: 0.34285714285714286 || F1: 0.3076923076923077
Case Insensitive : P: 0.349 || R: 0.429 || F1: 0.385
68 Perpres_2013_103
Case Sensitive   : P: 0.425531914893617 || R: 0.5128205128205128 || F1: 0.4651162790

117 Perkab_Ponorogo_2011_8
Case Sensitive   : P: 0.035211267605633804 || R: 0.025252525252525252 || F1: 0.029411764705882353
Case Insensitive : P: 0.035 || R: 0.025 || F1: 0.029
118 Peraturan_BSSN_2011_4
Case Sensitive   : P: 0.2916666666666667 || R: 0.4375 || F1: 0.35000000000000003
Case Insensitive : P: 0.333 || R: 0.5 || F1: 0.4
119 Peraturan_LPS_2019_4
Case Sensitive   : P: 0.3684210526315789 || R: 0.4666666666666667 || F1: 0.4117647058823529
Case Insensitive : P: 0.421 || R: 0.533 || F1: 0.47
120 Perkab_Sleman_2012_1
Case Sensitive   : P: 0.1111111111111111 || R: 0.10869565217391304 || F1: 0.1098901098901099
Case Insensitive : P: 0.133 || R: 0.13 || F1: 0.131
121 Permen_Dagri_2017_111
Case Sensitive   : P: 0.14285714285714285 || R: 0.14583333333333334 || F1: 0.1443298969072165
Case Insensitive : P: 0.143 || R: 0.146 || F1: 0.144
122 Permen_ESDM_2013_17
Case Sensitive   : P: 0.3333333333333333 || R: 0.37142857142857144 || F1: 0.35135135135135137
Case Insensitive : P: 0.385 || R: 0.

Case Insensitive : P: 0.188 || R: 0.205 || F1: 0.196
178 Permen_Hub_2013_23
Case Sensitive   : P: 0.34615384615384615 || R: 0.34615384615384615 || F1: 0.34615384615384615
Case Insensitive : P: 0.385 || R: 0.385 || F1: 0.385
179 PP_1961_79
Case Sensitive   : P: 0.5555555555555556 || R: 0.5263157894736842 || F1: 0.5405405405405405
Case Insensitive : P: 0.556 || R: 0.526 || F1: 0.541
180 Peraturan_BNP2TKI_2017_11
Case Sensitive   : P: 0.09523809523809523 || R: 0.10526315789473684 || F1: 0.1
Case Insensitive : P: 0.119 || R: 0.132 || F1: 0.125
181 Permen_Tan_2010_45
Case Sensitive   : P: 0.16176470588235295 || R: 0.275 || F1: 0.20370370370370375
Case Insensitive : P: 0.176 || R: 0.3 || F1: 0.222
182 Permen_Dikbud_2013_87
Case Sensitive   : P: 0.3409090909090909 || R: 0.5357142857142857 || F1: 0.41666666666666663
Case Insensitive : P: 0.409 || R: 0.643 || F1: 0.5
183 Permen_Perin_2015_48
Case Sensitive   : P: 0.16279069767441862 || R: 0.1794871794871795 || F1: 0.17073170731707318
Case Insen

Case Insensitive : P: 0.131 || R: 0.129 || F1: 0.13
232 UU_2008_50
Case Sensitive   : P: 0.7666666666666667 || R: 0.575 || F1: 0.6571428571428571
Case Insensitive : P: 0.8 || R: 0.6 || F1: 0.686
233 Peraturan_PPATK_2011_14
Case Sensitive   : P: 0.5 || R: 0.3888888888888889 || F1: 0.43750000000000006
Case Insensitive : P: 0.571 || R: 0.444 || F1: 0.5
234 Permen_LHK_2019_56
Case Sensitive   : P: 0.13793103448275862 || R: 0.13793103448275862 || F1: 0.13793103448275862
Case Insensitive : P: 0.172 || R: 0.172 || F1: 0.172
235 Permen_PR_2011_09
Case Sensitive   : P: 0.07317073170731707 || R: 0.08108108108108109 || F1: 0.07692307692307691
Case Insensitive : P: 0.085 || R: 0.095 || F1: 0.09
236 Permen_Dagri_2013_67
Case Sensitive   : P: 0.2222222222222222 || R: 0.25 || F1: 0.23529411764705882
Case Insensitive : P: 0.25 || R: 0.281 || F1: 0.265
237 Perprov_Kalbar_2001_7
Case Sensitive   : P: 0.06153846153846154 || R: 0.06896551724137931 || F1: 0.06504065040650407
Case Insensitive : P: 0.062 || 

...

2415 Perkot_Tasikmalaya_2007_8
Case Sensitive   : P: 0.13333333333333333 || R: 0.6 || F1: 0.2181818181818182
Case Insensitive : P: 0.156 || R: 0.7 || F1: 0.255
2416 PP_1994_8
Case Sensitive   : P: 0.3333333333333333 || R: 0.2777777777777778 || F1: 0.303030303030303
Case Insensitive : P: 0.333 || R: 0.278 || F1: 0.303
2417 Permen_Hub_2018_27
Case Sensitive   : P: 0.25806451612903225 || R: 0.2962962962962963 || F1: 0.27586206896551724
Case Insensitive : P: 0.29 || R: 0.333 || F1: 0.31
2418 PP_1996_14
Case Sensitive   : P: 0.20512820512820512 || R: 0.3076923076923077 || F1: 0.2461538461538462
Case Insensitive : P: 0.231 || R: 0.346 || F1: 0.277
2419 Peraturan_LKPP_2018_11
Case Sensitive   : P: 0.26666666666666666 || R: 0.34782608695652173 || F1: 0.30188679245283023
Case Insensitive : P: 0.3 || R: 0.391 || F1: 0.34
2420 PP_1980_51
Case Sensitive   : P: 0.19047619047619047 || R: 0.24242424242424243 || F1: 0.21333333333333335
Case Insensitive : P: 0.214 || R: 0.273 || F1: 0.24
2421 Permen_Ke

Case Insensitive : P: 0.176 || R: 0.176 || F1: 0.176
2471 Permen_KP_2016_30
Case Sensitive   : P: 0.2777777777777778 || R: 0.2777777777777778 || F1: 0.2777777777777778
Case Insensitive : P: 0.333 || R: 0.333 || F1: 0.333
2472 Permen_Sos_2016_4
Case Sensitive   : P: 0.13253012048192772 || R: 0.14473684210526316 || F1: 0.13836477987421386
Case Insensitive : P: 0.145 || R: 0.158 || F1: 0.151
2473 Permen_Keu_2010_64
Case Sensitive   : P: 0.19047619047619047 || R: 0.21052631578947367 || F1: 0.2
Case Insensitive : P: 0.214 || R: 0.237 || F1: 0.225
2474 Perpres_2018_107
Case Sensitive   : P: 0.44 || R: 0.5238095238095238 || F1: 0.4782608695652174
Case Insensitive : P: 0.48 || R: 0.571 || F1: 0.522
2475 Peraturan_BKKBN_2016_481
Case Sensitive   : P: 0.19230769230769232 || R: 0.2777777777777778 || F1: 0.2272727272727273
Case Insensitive : P: 0.231 || R: 0.333 || F1: 0.273
2476 Peraturan_KY_2015_2
Case Sensitive   : P: 0.35 || R: 0.6363636363636364 || F1: 0.45161290322580644
Case Insensitive : P

Case Insensitive : P: 0.214 || R: 0.237 || F1: 0.225
2529 Perkab_Musi_Rawas_2005_7
Case Sensitive   : P: 0.2222222222222222 || R: 0.5454545454545454 || F1: 0.3157894736842105
Case Insensitive : P: 0.259 || R: 0.636 || F1: 0.368
2530 Permen_KP_2016_28
Case Sensitive   : P: 0.06896551724137931 || R: 0.06666666666666667 || F1: 0.06779661016949153
Case Insensitive : P: 0.103 || R: 0.1 || F1: 0.101
2531 Peraturan_Ombudsman_2012_9
Case Sensitive   : P: 0.21875 || R: 0.21875 || F1: 0.21875
Case Insensitive : P: 0.25 || R: 0.25 || F1: 0.25
2532 Perkab_Tanggamus_2012_01
Case Sensitive   : P: 0.053763440860215055 || R: 0.043859649122807015 || F1: 0.048309178743961345
Case Insensitive : P: 0.054 || R: 0.044 || F1: 0.048
2533 Permen_Dag_2015_104
Case Sensitive   : P: 0.0898876404494382 || R: 0.07547169811320754 || F1: 0.08205128205128207
Case Insensitive : P: 0.101 || R: 0.085 || F1: 0.092
2534 Peraturan_BNP2TKI_2017_06
Case Sensitive   : P: 0.0967741935483871 || R: 0.10344827586206896 || F1: 0.09

Case Insensitive : P: 0.084 || R: 0.085 || F1: 0.084
2579 Permen_Keu_2014_58
Case Sensitive   : P: 0.4 || R: 0.46153846153846156 || F1: 0.42857142857142855
Case Insensitive : P: 0.433 || R: 0.5 || F1: 0.464
2580 PP_1990_24
Case Sensitive   : P: 0.14583333333333334 || R: 0.2 || F1: 0.16867469879518074
Case Insensitive : P: 0.167 || R: 0.229 || F1: 0.193
2581 Permen_Dag_2015_76
Case Sensitive   : P: 0.2222222222222222 || R: 0.2702702702702703 || F1: 0.24390243902439024
Case Insensitive : P: 0.244 || R: 0.297 || F1: 0.268
2582 Peraturan_Polri_2008_8
Case Sensitive   : P: 0.3055555555555556 || R: 0.34375 || F1: 0.3235294117647059
Case Insensitive : P: 0.333 || R: 0.375 || F1: 0.353
2583 Permen_KP_2019_4
Case Sensitive   : P: 0.09302325581395349 || R: 0.10256410256410256 || F1: 0.0975609756097561
Case Insensitive : P: 0.14 || R: 0.154 || F1: 0.147
2584 Permen_Hut_2009_33
Case Sensitive   : P: 0.1076923076923077 || R: 0.11475409836065574 || F1: 0.1111111111111111
Case Insensitive : P: 0.123 

2635 Permen_Dagri_2019_15
Case Sensitive   : P: 0.34375 || R: 0.15942028985507245 || F1: 0.21782178217821777
Case Insensitive : P: 0.375 || R: 0.174 || F1: 0.238
2636 UU_2002_10
Case Sensitive   : P: 0.22727272727272727 || R: 0.24390243902439024 || F1: 0.2352941176470588
Case Insensitive : P: 0.25 || R: 0.268 || F1: 0.259
2637 Peraturan_MA_2017_4
Case Sensitive   : P: 0.39285714285714285 || R: 0.3793103448275862 || F1: 0.3859649122807017
Case Insensitive : P: 0.429 || R: 0.414 || F1: 0.421
2638 Perpres_2014_108
Case Sensitive   : P: 0.24 || R: 0.27906976744186046 || F1: 0.2580645161290322
Case Insensitive : P: 0.26 || R: 0.302 || F1: 0.279
2639 Perppu_2017_1
Case Sensitive   : P: 0.4444444444444444 || R: 0.4444444444444444 || F1: 0.4444444444444444
Case Insensitive : P: 0.5 || R: 0.5 || F1: 0.5

####################################################

ofg 1 Shot

Case Sensitive
Precision: 0.18294891921265546
Recall: 0.1941959135539775
F1 Score: 0.18840471571407252

Case Insensitive
Precis

In [37]:
test_1('ofg', of_gemma, test_opening, '2', 'results/metrics_of.csv')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.65 || R: 0.65 || F1: 0.65
Case Insensitive : P: 0.675 || R: 0.675 || F1: 0.675
1 Permen_KP_2013_5
Case Sensitive   : P: 0.6363636363636364 || R: 0.7777777777777778 || F1: 0.7000000000000001
Case Insensitive : P: 0.659 || R: 0.806 || F1: 0.725
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.7727272727272727 || R: 0.9444444444444444 || F1: 0.85
Case Insensitive : P: 0.818 || R: 1.0 || F1: 0.9
3 Permen_Par_2015_14
Case Sensitive   : P: 0.6170212765957447 || R: 0.6744186046511628 || F1: 0.6444444444444444
Case Insensitive : P: 0.638 || R: 0.698 || F1: 0.667
4 Perpres_2019_67
Case Sensitive   : P: 0.7857142857142857 || R: 0.9166666666666666 || F1: 0.8461538461538461
Case Insensitive : P: 0.821 || R: 0.958 || F1: 0.884
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.25925925925925924 || R: 0.0875 || F1: 0.13084112149532712
Case Insensitive : P: 0.259 || R: 0.087 || F1: 0.13
6 Perkab_Tabalong_2010_09
Case Sensitive   : P: 0.546875 || R: 0

Case Insensitive : P: 0.714 || R: 0.652 || F1: 0.682
60 Permen_Hut_2009_32
Case Sensitive   : P: 0.4 || R: 0.5185185185185185 || F1: 0.45161290322580644
Case Insensitive : P: 0.4 || R: 0.519 || F1: 0.452
61 Peraturan_KPU_2018_11
Case Sensitive   : P: 0.4782608695652174 || R: 0.5789473684210527 || F1: 0.5238095238095238
Case Insensitive : P: 0.478 || R: 0.579 || F1: 0.524
62 Permen_Tan_2017_49
Case Sensitive   : P: 0.5555555555555556 || R: 0.6666666666666666 || F1: 0.606060606060606
Case Insensitive : P: 0.556 || R: 0.667 || F1: 0.606
63 Perkot_Sorong_2013_32
Case Sensitive   : P: 0.859375 || R: 0.8461538461538461 || F1: 0.8527131782945736
Case Insensitive : P: 0.859 || R: 0.846 || F1: 0.852
64 Perkot_Bogor_2006_11
Case Sensitive   : P: 0.5588235294117647 || R: 0.3114754098360656 || F1: 0.4
Case Insensitive : P: 0.559 || R: 0.311 || F1: 0.4
65 Perprov_Jateng_2001_10
Case Sensitive   : P: 0.6956521739130435 || R: 0.8205128205128205 || F1: 0.7529411764705882
Case Insensitive : P: 0.696 ||

Case Insensitive : P: 0.821 || R: 0.885 || F1: 0.852
115 PP_2011_79
Case Sensitive   : P: 0.8148148148148148 || R: 0.9565217391304348 || F1: 0.8800000000000001
Case Insensitive : P: 0.852 || R: 1.0 || F1: 0.92
116 Permen_Humham_2013_10
Case Sensitive   : P: 0.5625 || R: 0.675 || F1: 0.6136363636363636
Case Insensitive : P: 0.583 || R: 0.7 || F1: 0.636
117 Perkab_Ponorogo_2011_8
Case Sensitive   : P: 0.39285714285714285 || R: 0.05555555555555555 || F1: 0.09734513274336283
Case Insensitive : P: 0.429 || R: 0.061 || F1: 0.107
118 Peraturan_BSSN_2011_4
Case Sensitive   : P: 0.375 || R: 0.5625 || F1: 0.45
Case Insensitive : P: 0.417 || R: 0.625 || F1: 0.5
119 Peraturan_LPS_2019_4
Case Sensitive   : P: 0.5789473684210527 || R: 0.7333333333333333 || F1: 0.6470588235294117
Case Insensitive : P: 0.632 || R: 0.8 || F1: 0.706
120 Perkab_Sleman_2012_1
Case Sensitive   : P: 0.8 || R: 0.782608695652174 || F1: 0.7912087912087912
Case Insensitive : P: 0.822 || R: 0.804 || F1: 0.813
121 Permen_Dagri_20

Case Insensitive : P: 0.803 || R: 0.803 || F1: 0.803
173 Perkab_Tanggamus_2004_8
Case Sensitive   : P: 0.08641975308641975 || R: 0.7 || F1: 0.15384615384615385
Case Insensitive : P: 0.086 || R: 0.7 || F1: 0.153
174 Peraturan_Komnas_HAM_2015_003
Case Sensitive   : P: 0.6 || R: 0.8181818181818182 || F1: 0.6923076923076923
Case Insensitive : P: 0.6 || R: 0.818 || F1: 0.692
175 Perkot_Sorong_2013_14
Case Sensitive   : P: 0.358974358974359 || R: 0.5185185185185185 || F1: 0.42424242424242425
Case Insensitive : P: 0.372 || R: 0.537 || F1: 0.44
176 Permen_ATRBPN_2018_12
Case Sensitive   : P: 0.7454545454545455 || R: 0.8723404255319149 || F1: 0.803921568627451
Case Insensitive : P: 0.745 || R: 0.872 || F1: 0.804
177 Permen_Kes_2012_003
Case Sensitive   : P: 0.4375 || R: 0.4772727272727273 || F1: 0.45652173913043476
Case Insensitive : P: 0.438 || R: 0.477 || F1: 0.457
178 Permen_Hub_2013_23
Case Sensitive   : P: 0.46153846153846156 || R: 0.46153846153846156 || F1: 0.46153846153846156
Case Insens

233 Peraturan_PPATK_2011_14
Case Sensitive   : P: 0.7777777777777778 || R: 0.7777777777777778 || F1: 0.7777777777777778
Case Insensitive : P: 0.778 || R: 0.778 || F1: 0.778
234 Permen_LHK_2019_56
Case Sensitive   : P: 0.7586206896551724 || R: 0.7586206896551724 || F1: 0.7586206896551724
Case Insensitive : P: 0.793 || R: 0.793 || F1: 0.793
235 Permen_PR_2011_09
Case Sensitive   : P: 0.573170731707317 || R: 0.6351351351351351 || F1: 0.6025641025641024
Case Insensitive : P: 0.585 || R: 0.649 || F1: 0.615
236 Permen_Dagri_2013_67
Case Sensitive   : P: 0.6388888888888888 || R: 0.71875 || F1: 0.676470588235294
Case Insensitive : P: 0.667 || R: 0.75 || F1: 0.706
237 Perprov_Kalbar_2001_7
Case Sensitive   : P: 0.6307692307692307 || R: 0.7068965517241379 || F1: 0.6666666666666666
Case Insensitive : P: 0.692 || R: 0.776 || F1: 0.732
238 Permen_Tan_2015_53
Case Sensitive   : P: 0.39473684210526316 || R: 0.5 || F1: 0.4411764705882353
Case Insensitive : P: 0.408 || R: 0.517 || F1: 0.456
239 Permen_

...

Case Insensitive : P: 0.745 || R: 0.814 || F1: 0.778
2396 Permen_Dagri_2016_63
Case Sensitive   : P: 0.631578947368421 || R: 0.9230769230769231 || F1: 0.7499999999999999
Case Insensitive : P: 0.632 || R: 0.923 || F1: 0.75
2397 Peraturan_BMKG_2014_4
Case Sensitive   : P: 0.75 || R: 0.875 || F1: 0.8076923076923077
Case Insensitive : P: 0.75 || R: 0.875 || F1: 0.808
2398 UU_2009_24
Case Sensitive   : P: 0.8823529411764706 || R: 0.8823529411764706 || F1: 0.8823529411764706
Case Insensitive : P: 0.941 || R: 0.941 || F1: 0.941
2399 Permen_Dagri_2012_60
Case Sensitive   : P: 0.76 || R: 1.0 || F1: 0.8636363636363636
Case Insensitive : P: 0.76 || R: 1.0 || F1: 0.864
2400 Permen_ESDM_2013_19
Case Sensitive   : P: 0.7142857142857143 || R: 0.8064516129032258 || F1: 0.7575757575757576
Case Insensitive : P: 0.771 || R: 0.871 || F1: 0.818
2401 Peraturan_LKPP_2019_14
Case Sensitive   : P: 0.6875 || R: 0.7857142857142857 || F1: 0.7333333333333334
Case Insensitive : P: 0.719 || R: 0.821 || F1: 0.767
240

Case Insensitive : P: 0.712 || R: 0.771 || F1: 0.74
2459 Permen_Keu_2019_118
Case Sensitive   : P: 0.43103448275862066 || R: 0.46296296296296297 || F1: 0.44642857142857145
Case Insensitive : P: 0.431 || R: 0.463 || F1: 0.446
2460 Permen_Naker_2018_2
Case Sensitive   : P: 0.5714285714285714 || R: 0.7407407407407407 || F1: 0.6451612903225806
Case Insensitive : P: 0.6 || R: 0.778 || F1: 0.678
2461 Perkab_Way_Kanan_2001_4
Case Sensitive   : P: 0.559322033898305 || R: 0.6346153846153846 || F1: 0.5945945945945946
Case Insensitive : P: 0.559 || R: 0.635 || F1: 0.595
2462 Perkab_Bulungan_2009_2
Case Sensitive   : P: 0.7794117647058824 || R: 0.7681159420289855 || F1: 0.7737226277372262
Case Insensitive : P: 0.779 || R: 0.768 || F1: 0.773
2463 Permen_PUPR_2015_10
Case Sensitive   : P: 0.6216216216216216 || R: 0.6216216216216216 || F1: 0.6216216216216216
Case Insensitive : P: 0.676 || R: 0.676 || F1: 0.676
2464 Perpres_2015_161
Case Sensitive   : P: 0.8837209302325582 || R: 0.9743589743589743 || 

Case Insensitive : P: 0.406 || R: 0.65 || F1: 0.5
2522 Permen_Keu_2018_34
Case Sensitive   : P: 0.6190476190476191 || R: 0.7647058823529411 || F1: 0.6842105263157895
Case Insensitive : P: 0.714 || R: 0.882 || F1: 0.789
2523 Permen_Dag_2019_41
Case Sensitive   : P: 0.5588235294117647 || R: 0.6785714285714286 || F1: 0.6129032258064516
Case Insensitive : P: 0.574 || R: 0.696 || F1: 0.629
2524 Permen_Dag_2019_16
Case Sensitive   : P: 0.47368421052631576 || R: 0.47368421052631576 || F1: 0.47368421052631576
Case Insensitive : P: 0.474 || R: 0.474 || F1: 0.474
2525 Permen_Keu_2015_237
Case Sensitive   : P: 0.9666666666666667 || R: 0.9666666666666667 || F1: 0.9666666666666667
Case Insensitive : P: 1.0 || R: 1.0 || F1: 1.0
2526 Perprov_Riau_2013_17
Case Sensitive   : P: 0.9655172413793104 || R: 0.9333333333333333 || F1: 0.9491525423728815
Case Insensitive : P: 0.966 || R: 0.933 || F1: 0.949
2527 Permen_PPPA_2010_10
Case Sensitive   : P: 0.17647058823529413 || R: 0.46153846153846156 || F1: 0.255

2573 Perpres_2019_2
Case Sensitive   : P: 0.5641025641025641 || R: 0.8148148148148148 || F1: 0.6666666666666667
Case Insensitive : P: 0.59 || R: 0.852 || F1: 0.697
2574 Perkab_Poso_2010_9
Case Sensitive   : P: 0.7402597402597403 || R: 0.7702702702702703 || F1: 0.7549668874172186
Case Insensitive : P: 0.74 || R: 0.77 || F1: 0.755
2575 UU_2007_5
Case Sensitive   : P: 0.6415094339622641 || R: 0.8292682926829268 || F1: 0.723404255319149
Case Insensitive : P: 0.66 || R: 0.854 || F1: 0.745
2576 Perkab_Musi_Rawas_2013_10
Case Sensitive   : P: 0.07272727272727272 || R: 0.4 || F1: 0.12307692307692307
Case Insensitive : P: 0.073 || R: 0.4 || F1: 0.123
2577 Permen_Perin_2017_07
Case Sensitive   : P: 0.4838709677419355 || R: 0.4838709677419355 || F1: 0.4838709677419355
Case Insensitive : P: 0.516 || R: 0.516 || F1: 0.516
2578 Permen_Desa_2016_25
Case Sensitive   : P: 0.6463414634146342 || R: 0.6463414634146342 || F1: 0.6463414634146342
Case Insensitive : P: 0.671 || R: 0.671 || F1: 0.671
2579 Perm

Case Insensitive : P: 0.723 || R: 0.773 || F1: 0.747
2634 Peraturan_BPS_2012_49
Case Sensitive   : P: 0.41379310344827586 || R: 0.7058823529411765 || F1: 0.5217391304347826
Case Insensitive : P: 0.431 || R: 0.735 || F1: 0.543
2635 Permen_Dagri_2019_15
Case Sensitive   : P: 0.3125 || R: 0.14492753623188406 || F1: 0.19801980198019803
Case Insensitive : P: 0.344 || R: 0.159 || F1: 0.217
2636 UU_2002_10
Case Sensitive   : P: 0.2708333333333333 || R: 0.3170731707317073 || F1: 0.29213483146067415
Case Insensitive : P: 0.292 || R: 0.341 || F1: 0.315
2637 Peraturan_MA_2017_4
Case Sensitive   : P: 0.35714285714285715 || R: 0.3448275862068966 || F1: 0.3508771929824561
Case Insensitive : P: 0.393 || R: 0.379 || F1: 0.386
2638 Perpres_2014_108
Case Sensitive   : P: 0.8936170212765957 || R: 0.9767441860465116 || F1: 0.9333333333333332
Case Insensitive : P: 0.915 || R: 1.0 || F1: 0.956
2639 Perppu_2017_1
Case Sensitive   : P: 0.8333333333333334 || R: 0.8333333333333334 || F1: 0.8333333333333334
Case

In [38]:
test_1('ofl', of_llama, test_opening, '1', 'results/metrics_of.csv')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.4883720930232558 || R: 0.525 || F1: 0.5060240963855422
Case Insensitive : P: 0.488 || R: 0.525 || F1: 0.506
1 Permen_KP_2013_5
Case Sensitive   : P: 0.0847457627118644 || R: 0.1388888888888889 || F1: 0.10526315789473684
Case Insensitive : P: 0.102 || R: 0.167 || F1: 0.127
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.7272727272727273 || R: 0.8888888888888888 || F1: 0.7999999999999999
Case Insensitive : P: 0.773 || R: 0.944 || F1: 0.85
3 Permen_Par_2015_14
Case Sensitive   : P: 0.09859154929577464 || R: 0.32558139534883723 || F1: 0.15135135135135136
Case Insensitive : P: 0.106 || R: 0.349 || F1: 0.163
4 Perpres_2019_67
Case Sensitive   : P: 0.5185185185185185 || R: 0.5833333333333334 || F1: 0.5490196078431373
Case Insensitive : P: 0.556 || R: 0.625 || F1: 0.588
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.8125 || R: 0.08125 || F1: 0.14772727272727273
Case Insensitive : P: 0.875 || R: 0.087 || F1: 0.158
6 Perkab_Tabalong_2010_09

Case Insensitive : P: 0.625 || R: 0.648 || F1: 0.636
52 UU_1998_5
Case Sensitive   : P: 0.375 || R: 0.5294117647058824 || F1: 0.4390243902439025
Case Insensitive : P: 0.375 || R: 0.529 || F1: 0.439
53 Permen_PANRB_2015_16
Case Sensitive   : P: 0.34782608695652173 || R: 0.38095238095238093 || F1: 0.3636363636363636
Case Insensitive : P: 0.37 || R: 0.405 || F1: 0.387
54 Perpres_2006_98
Case Sensitive   : P: 0.9565217391304348 || R: 0.9565217391304348 || F1: 0.9565217391304348
Case Insensitive : P: 1.0 || R: 1.0 || F1: 1.0
55 PP_1970_19
Case Sensitive   : P: 0.21739130434782608 || R: 0.38461538461538464 || F1: 0.27777777777777773
Case Insensitive : P: 0.217 || R: 0.385 || F1: 0.278
56 UU_1957_59
Case Sensitive   : P: 0.3888888888888889 || R: 0.5833333333333334 || F1: 0.4666666666666666
Case Insensitive : P: 0.389 || R: 0.583 || F1: 0.467
57 Permen_Dikbud_2013_46
Case Sensitive   : P: 0.043795620437956206 || R: 0.13953488372093023 || F1: 0.06666666666666667
Case Insensitive : P: 0.058 || R

Case Insensitive : P: 0.316 || R: 0.094 || F1: 0.145
106 Permen_Keu_2017_37
Case Sensitive   : P: 0.7857142857142857 || R: 0.7857142857142857 || F1: 0.7857142857142857
Case Insensitive : P: 0.857 || R: 0.857 || F1: 0.857
107 Permen_Keu_2016_193
Case Sensitive   : P: 0.7666666666666667 || R: 0.7666666666666667 || F1: 0.7666666666666667
Case Insensitive : P: 0.8 || R: 0.8 || F1: 0.8
108 Perpres_2018_127
Case Sensitive   : P: 0.6363636363636364 || R: 0.813953488372093 || F1: 0.7142857142857143
Case Insensitive : P: 0.655 || R: 0.837 || F1: 0.735
109 Permen_ESDM_2013_24
Case Sensitive   : P: 0.3090909090909091 || R: 0.4857142857142857 || F1: 0.3777777777777777
Case Insensitive : P: 0.345 || R: 0.543 || F1: 0.422
110 UU_1998_9
Case Sensitive   : P: 0.6470588235294118 || R: 0.6470588235294118 || F1: 0.6470588235294118
Case Insensitive : P: 0.706 || R: 0.706 || F1: 0.706
111 Perkot_Bandung_2012_17
Case Sensitive   : P: 0.55 || R: 0.2972972972972973 || F1: 0.38596491228070173
Case Insensitive 

Case Insensitive : P: 0.186 || R: 0.2 || F1: 0.193
158 Permen_Keu_2010_243
Case Sensitive   : P: 0.5277777777777778 || R: 0.5135135135135135 || F1: 0.5205479452054794
Case Insensitive : P: 0.556 || R: 0.541 || F1: 0.548
159 Perkab_Indramayu_1998_16
Case Sensitive   : P: 0.05357142857142857 || R: 0.3 || F1: 0.09090909090909091
Case Insensitive : P: 0.071 || R: 0.4 || F1: 0.121
160 Perprov_Gorontalo_2007_02
Case Sensitive   : P: 0.05442176870748299 || R: 0.06015037593984962 || F1: 0.05714285714285714
Case Insensitive : P: 0.061 || R: 0.068 || F1: 0.064
161 Permen_Han_2014_83
Case Sensitive   : P: 0.5806451612903226 || R: 0.6428571428571429 || F1: 0.6101694915254238
Case Insensitive : P: 0.613 || R: 0.679 || F1: 0.644
162 Permen_Humham_2015_16
Case Sensitive   : P: 0.3142857142857143 || R: 0.36666666666666664 || F1: 0.3384615384615384
Case Insensitive : P: 0.371 || R: 0.433 || F1: 0.4
163 Perkab_Indramayu_2006_1
Case Sensitive   : P: 0.17647058823529413 || R: 0.13846153846153847 || F1: 0.

Case Insensitive : P: 0.049 || R: 0.037 || F1: 0.042
211 PP_2012_13
Case Sensitive   : P: 0.2903225806451613 || R: 0.2903225806451613 || F1: 0.2903225806451613
Case Insensitive : P: 0.323 || R: 0.323 || F1: 0.323
212 Permen_Dikbud_2011_50
Case Sensitive   : P: 0.41935483870967744 || R: 0.5652173913043478 || F1: 0.4814814814814815
Case Insensitive : P: 0.484 || R: 0.652 || F1: 0.556
213 Permen_LH_2012_10
Case Sensitive   : P: 0.5925925925925926 || R: 0.5714285714285714 || F1: 0.5818181818181818
Case Insensitive : P: 0.593 || R: 0.571 || F1: 0.582
214 Permen_PANRB_2015_12
Case Sensitive   : P: 0.14084507042253522 || R: 0.5 || F1: 0.21978021978021978
Case Insensitive : P: 0.162 || R: 0.575 || F1: 0.253
215 Permen_KP_2016_6
Case Sensitive   : P: 0.2631578947368421 || R: 0.09259259259259259 || F1: 0.136986301369863
Case Insensitive : P: 0.316 || R: 0.111 || F1: 0.164
216 Perkab_Pontianak_2010_18
Case Sensitive   : P: 0.6923076923076923 || R: 0.6585365853658537 || F1: 0.675
Case Insensitive 

...

Case Insensitive : P: 0.243 || R: 0.129 || F1: 0.169
2347 PP_1961_132
Case Sensitive   : P: 0.43478260869565216 || R: 0.45454545454545453 || F1: 0.4444444444444445
Case Insensitive : P: 0.478 || R: 0.5 || F1: 0.489
2348 Perprov_Jabar_2011_20
Case Sensitive   : P: 0.2631578947368421 || R: 0.14705882352941177 || F1: 0.18867924528301885
Case Insensitive : P: 0.263 || R: 0.147 || F1: 0.189
2349 Permen_Dagri_2017_10
Case Sensitive   : P: 0.6296296296296297 || R: 0.7391304347826086 || F1: 0.68
Case Insensitive : P: 0.63 || R: 0.739 || F1: 0.68
2350 Permen_Dagri_2017_97
Case Sensitive   : P: 0.5714285714285714 || R: 0.5714285714285714 || F1: 0.5714285714285714
Case Insensitive : P: 0.6 || R: 0.6 || F1: 0.6
2351 PP_2018_32
Case Sensitive   : P: 0.9285714285714286 || R: 0.6842105263157895 || F1: 0.7878787878787878
Case Insensitive : P: 1.0 || R: 0.737 || F1: 0.849
2352 UU_2002_27
Case Sensitive   : P: 0.5384615384615384 || R: 0.4666666666666667 || F1: 0.5
Case Insensitive : P: 0.564 || R: 0.489

2422 Perkot_Tasikmalaya_2004_16
Case Sensitive   : P: 0.3157894736842105 || R: 0.0625 || F1: 0.10434782608695652
Case Insensitive : P: 0.368 || R: 0.073 || F1: 0.122
2423 Perkot_Binjai_2001_26
Case Sensitive   : P: 0.10256410256410256 || R: 0.17391304347826086 || F1: 0.12903225806451615
Case Insensitive : P: 0.128 || R: 0.217 || F1: 0.161
2424 PP_1986_23
Case Sensitive   : P: 0.45454545454545453 || R: 0.37037037037037035 || F1: 0.40816326530612246
Case Insensitive : P: 0.455 || R: 0.37 || F1: 0.408
2425 Perkot_Depok_2008_11
Case Sensitive   : P: 0.15789473684210525 || R: 0.04838709677419355 || F1: 0.07407407407407407
Case Insensitive : P: 0.184 || R: 0.056 || F1: 0.086
2426 Permen_Hub_2014_20
Case Sensitive   : P: 0.625 || R: 0.08379888268156424 || F1: 0.14778325123152708
Case Insensitive : P: 0.667 || R: 0.089 || F1: 0.157
2427 Perkab_Pacitan_2010_6
Case Sensitive   : P: 0.18421052631578946 || R: 0.1794871794871795 || F1: 0.18181818181818182
Case Insensitive : P: 0.211 || R: 0.205 || 

Case Insensitive : P: 0.237 || R: 0.095 || F1: 0.136
2498 PP_2007_35
Case Sensitive   : P: 0.9444444444444444 || R: 0.9444444444444444 || F1: 0.9444444444444444
Case Insensitive : P: 1.0 || R: 1.0 || F1: 1.0
2499 Permen_Dagri_2016_75
Case Sensitive   : P: 0.5 || R: 0.5833333333333334 || F1: 0.5384615384615384
Case Insensitive : P: 0.536 || R: 0.625 || F1: 0.577
2500 Permen_ESDM_2014_36
Case Sensitive   : P: 0.7692307692307693 || R: 0.5555555555555556 || F1: 0.6451612903225806
Case Insensitive : P: 0.769 || R: 0.556 || F1: 0.645
2501 Peraturan_Polri_2015_18
Case Sensitive   : P: 0.12 || R: 0.09375 || F1: 0.10526315789473684
Case Insensitive : P: 0.12 || R: 0.094 || F1: 0.105
2502 Perkot_Pangkalpinang_2006_12
Case Sensitive   : P: 0.6857142857142857 || R: 0.12834224598930483 || F1: 0.2162162162162162
Case Insensitive : P: 0.771 || R: 0.144 || F1: 0.243
2503 Permen_LH_2011_3
Case Sensitive   : P: 0.2571428571428571 || R: 0.32142857142857145 || F1: 0.2857142857142857
Case Insensitive : P: 

Case Insensitive : P: 0.811 || R: 0.5 || F1: 0.619
2550 PP_2005_15
Case Sensitive   : P: 0.9444444444444444 || R: 0.9444444444444444 || F1: 0.9444444444444444
Case Insensitive : P: 1.0 || R: 1.0 || F1: 1.0
2551 Perkab_Serdang_Bedagai_2012_14
Case Sensitive   : P: 0.2222222222222222 || R: 0.1568627450980392 || F1: 0.1839080459770115
Case Insensitive : P: 0.25 || R: 0.176 || F1: 0.207
2552 PP_2003_34
Case Sensitive   : P: 0.3 || R: 0.36 || F1: 0.3272727272727273
Case Insensitive : P: 0.333 || R: 0.4 || F1: 0.363
2553 Permen_Hub_2015_134
Case Sensitive   : P: 0.8529411764705882 || R: 0.58 || F1: 0.6904761904761905
Case Insensitive : P: 0.882 || R: 0.6 || F1: 0.714
2554 Permen_Ristekdikti_2016_55
Case Sensitive   : P: 0.4722222222222222 || R: 0.53125 || F1: 0.4999999999999999
Case Insensitive : P: 0.472 || R: 0.531 || F1: 0.5
2555 Peraturan_OJK_2019_13
Case Sensitive   : P: 0.7777777777777778 || R: 0.5833333333333334 || F1: 0.6666666666666666
Case Insensitive : P: 0.778 || R: 0.583 || F1: 

Case Insensitive : P: 0.973 || R: 0.562 || F1: 0.712
2608 Perkab_Indramayu_2005_1
Case Sensitive   : P: 0.23529411764705882 || R: 0.17777777777777778 || F1: 0.20253164556962028
Case Insensitive : P: 0.235 || R: 0.178 || F1: 0.203
2609 Permen_PANRB_2018_25
Case Sensitive   : P: 0.7368421052631579 || R: 0.45161290322580644 || F1: 0.56
Case Insensitive : P: 0.789 || R: 0.484 || F1: 0.6
2610 Permen_Humham_2018_04
Case Sensitive   : P: 0.3448275862068966 || R: 0.23255813953488372 || F1: 0.2777777777777778
Case Insensitive : P: 0.345 || R: 0.233 || F1: 0.278
2611 Permen_Humham_2019_8
Case Sensitive   : P: 0.2903225806451613 || R: 0.32142857142857145 || F1: 0.3050847457627119
Case Insensitive : P: 0.355 || R: 0.393 || F1: 0.373
2612 Peraturan_Basarnas_2017_3
Case Sensitive   : P: 0.37037037037037035 || R: 0.37037037037037035 || F1: 0.37037037037037035
Case Insensitive : P: 0.407 || R: 0.407 || F1: 0.407
2613 Permenko_Polhukam_2018_2
Case Sensitive   : P: 0.5 || R: 0.5 || F1: 0.5
Case Insensit

In [39]:
test_1('ofl', of_llama, test_opening, '2', 'results/metrics_of.csv')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.775 || R: 0.775 || F1: 0.775
Case Insensitive : P: 0.8 || R: 0.8 || F1: 0.8
1 Permen_KP_2013_5
Case Sensitive   : P: 0.3333333333333333 || R: 0.5555555555555556 || F1: 0.4166666666666667
Case Insensitive : P: 0.333 || R: 0.556 || F1: 0.417
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.5454545454545454 || R: 0.6666666666666666 || F1: 0.6
Case Insensitive : P: 0.591 || R: 0.722 || F1: 0.65
3 Permen_Par_2015_14
Case Sensitive   : P: 0.5897435897435898 || R: 0.5348837209302325 || F1: 0.5609756097560975
Case Insensitive : P: 0.615 || R: 0.558 || F1: 0.585
4 Perpres_2019_67
Case Sensitive   : P: 0.6428571428571429 || R: 0.75 || F1: 0.6923076923076924
Case Insensitive : P: 0.679 || R: 0.792 || F1: 0.731
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.6690647482014388 || R: 0.58125 || F1: 0.6220735785953176
Case Insensitive : P: 0.669 || R: 0.581 || F1: 0.622
6 Perkab_Tabalong_2010_09
Case Sensitive   : P: 0.5 || R: 0.5714285714285714 ||

Case Insensitive : P: 0.703 || R: 0.833 || F1: 0.762
52 UU_1998_5
Case Sensitive   : P: 0.2777777777777778 || R: 0.5882352941176471 || F1: 0.3773584905660377
Case Insensitive : P: 0.278 || R: 0.588 || F1: 0.378
53 Permen_PANRB_2015_16
Case Sensitive   : P: 0.43478260869565216 || R: 0.47619047619047616 || F1: 0.4545454545454545
Case Insensitive : P: 0.478 || R: 0.524 || F1: 0.5
54 Perpres_2006_98
Case Sensitive   : P: 0.9130434782608695 || R: 0.9130434782608695 || F1: 0.9130434782608695
Case Insensitive : P: 0.957 || R: 0.957 || F1: 0.957
55 PP_1970_19
Case Sensitive   : P: 0.125 || R: 0.23076923076923078 || F1: 0.16216216216216217
Case Insensitive : P: 0.125 || R: 0.231 || F1: 0.162
56 UU_1957_59
Case Sensitive   : P: 0.35 || R: 0.5833333333333334 || F1: 0.4375
Case Insensitive : P: 0.4 || R: 0.667 || F1: 0.5
57 Permen_Dikbud_2013_46
Case Sensitive   : P: 0.5116279069767442 || R: 0.5116279069767442 || F1: 0.5116279069767442
Case Insensitive : P: 0.558 || R: 0.558 || F1: 0.558
58 Permen

Case Insensitive : P: 0.765 || R: 0.907 || F1: 0.83
109 Permen_ESDM_2013_24
Case Sensitive   : P: 0.5813953488372093 || R: 0.7142857142857143 || F1: 0.6410256410256411
Case Insensitive : P: 0.605 || R: 0.743 || F1: 0.667
110 UU_1998_9
Case Sensitive   : P: 0.6111111111111112 || R: 0.6470588235294118 || F1: 0.6285714285714287
Case Insensitive : P: 0.667 || R: 0.706 || F1: 0.686
111 Perkot_Bandung_2012_17
Case Sensitive   : P: 0.6818181818181818 || R: 0.8108108108108109 || F1: 0.7407407407407407
Case Insensitive : P: 0.682 || R: 0.811 || F1: 0.741
112 Permen_ESDM_2016_21
Case Sensitive   : P: 0.47619047619047616 || R: 0.6382978723404256 || F1: 0.5454545454545455
Case Insensitive : P: 0.508 || R: 0.681 || F1: 0.582
113 Perkot_Pasuruan_2011_24
Case Sensitive   : P: 0.6181818181818182 || R: 0.6071428571428571 || F1: 0.6126126126126126
Case Insensitive : P: 0.618 || R: 0.607 || F1: 0.612
114 Permen_Naker_2015_25
Case Sensitive   : P: 0.35294117647058826 || R: 0.46153846153846156 || F1: 0.400

Case Insensitive : P: 0.797 || R: 0.836 || F1: 0.816
168 PP_2013_67
Case Sensitive   : P: 0.28125 || R: 1.0 || F1: 0.43902439024390244
Case Insensitive : P: 0.281 || R: 1.0 || F1: 0.439
169 Peraturan_OJK_2019_5
Case Sensitive   : P: 0.65 || R: 0.65 || F1: 0.65
Case Insensitive : P: 0.7 || R: 0.7 || F1: 0.7
170 Peraturan_LPSK_2011_1
Case Sensitive   : P: 0.75 || R: 0.75 || F1: 0.75
Case Insensitive : P: 0.786 || R: 0.786 || F1: 0.786
171 Permen_Ristekdikti_2015_36
Case Sensitive   : P: 0.2564102564102564 || R: 0.2777777777777778 || F1: 0.26666666666666666
Case Insensitive : P: 0.282 || R: 0.306 || F1: 0.294
172 Permen_Tan_2018_22
Case Sensitive   : P: 0.5178571428571429 || R: 0.47540983606557374 || F1: 0.4957264957264957
Case Insensitive : P: 0.518 || R: 0.475 || F1: 0.496
173 Perkab_Tanggamus_2004_8
Case Sensitive   : P: 0.14285714285714285 || R: 0.7 || F1: 0.23728813559322035
Case Insensitive : P: 0.143 || R: 0.7 || F1: 0.237
174 Peraturan_Komnas_HAM_2015_003
Case Sensitive   : P: 0.6

Case Insensitive : P: 0.168 || R: 0.353 || F1: 0.228
227 Perkab_Purworejo_2012_3
Case Sensitive   : P: 0.3923076923076923 || R: 0.6455696202531646 || F1: 0.4880382775119617
Case Insensitive : P: 0.392 || R: 0.646 || F1: 0.488
228 Permen_Tan_2013_81
Case Sensitive   : P: 0.2765957446808511 || R: 0.65 || F1: 0.3880597014925373
Case Insensitive : P: 0.277 || R: 0.65 || F1: 0.388
229 Peraturan_Bawaslu_2018_32
Case Sensitive   : P: 0.6521739130434783 || R: 0.7894736842105263 || F1: 0.7142857142857143
Case Insensitive : P: 0.652 || R: 0.789 || F1: 0.714
230 Perkot_Bekasi_2013_07
Case Sensitive   : P: 0.5346534653465347 || R: 0.6352941176470588 || F1: 0.5806451612903226
Case Insensitive : P: 0.535 || R: 0.635 || F1: 0.581
231 Perkab_Kotabaru_2012_13
Case Sensitive   : P: 0.5737704918032787 || R: 0.5645161290322581 || F1: 0.5691056910569106
Case Insensitive : P: 0.574 || R: 0.565 || F1: 0.569
232 UU_2008_50
Case Sensitive   : P: 0.20408163265306123 || R: 0.75 || F1: 0.32085561497326204
Case In

...

Case Insensitive : P: 0.667 || R: 0.257 || F1: 0.371
2368 Permen_Kominfo_2013_26
Case Sensitive   : P: 0.6388888888888888 || R: 0.45098039215686275 || F1: 0.5287356321839081
Case Insensitive : P: 0.667 || R: 0.471 || F1: 0.552
2369 Permen_Hub_2016_93
Case Sensitive   : P: 0.42105263157894735 || R: 0.2222222222222222 || F1: 0.2909090909090909
Case Insensitive : P: 0.421 || R: 0.222 || F1: 0.291
2370 Peraturan_Jagung_2013_002
Case Sensitive   : P: 0.4444444444444444 || R: 0.4444444444444444 || F1: 0.4444444444444444
Case Insensitive : P: 0.472 || R: 0.472 || F1: 0.472
2371 Permen_Agama_2013_32
Case Sensitive   : P: 0.8108108108108109 || R: 0.6382978723404256 || F1: 0.7142857142857143
Case Insensitive : P: 0.838 || R: 0.66 || F1: 0.738
2372 Permen_Keu_2019_95
Case Sensitive   : P: 0.5 || R: 0.52 || F1: 0.5098039215686274
Case Insensitive : P: 0.538 || R: 0.56 || F1: 0.549
2373 Perpres_2014_44
Case Sensitive   : P: 1.0 || R: 1.0 || F1: 1.0
Case Insensitive : P: 1.0 || R: 1.0 || F1: 1.0
237

2422 Perkot_Tasikmalaya_2004_16
Case Sensitive   : P: 0.9714285714285714 || R: 0.3541666666666667 || F1: 0.5190839694656488
Case Insensitive : P: 0.971 || R: 0.354 || F1: 0.519
2423 Perkot_Binjai_2001_26
Case Sensitive   : P: 0.5263157894736842 || R: 0.8695652173913043 || F1: 0.6557377049180327
Case Insensitive : P: 0.526 || R: 0.87 || F1: 0.656
2424 PP_1986_23
Case Sensitive   : P: 0.45 || R: 0.6666666666666666 || F1: 0.5373134328358209
Case Insensitive : P: 0.475 || R: 0.704 || F1: 0.567
2425 Perkot_Depok_2008_11
Case Sensitive   : P: 0.8055555555555556 || R: 0.23387096774193547 || F1: 0.3625
Case Insensitive : P: 0.833 || R: 0.242 || F1: 0.375
2426 Permen_Hub_2014_20
Case Sensitive   : P: 0.8055555555555556 || R: 0.16201117318435754 || F1: 0.2697674418604651
Case Insensitive : P: 0.806 || R: 0.162 || F1: 0.27
2427 Perkab_Pacitan_2010_6
Case Sensitive   : P: 0.7777777777777778 || R: 0.717948717948718 || F1: 0.7466666666666666
Case Insensitive : P: 0.778 || R: 0.718 || F1: 0.747
2428 

2483 PP_1981_6
Case Sensitive   : P: 0.8387096774193549 || R: 0.8387096774193549 || F1: 0.8387096774193549
Case Insensitive : P: 0.839 || R: 0.839 || F1: 0.839
2484 Permen_Keu_2014_59
Case Sensitive   : P: 0.6 || R: 0.75 || F1: 0.6666666666666665
Case Insensitive : P: 0.6 || R: 0.75 || F1: 0.667
2485 Peraturan_BPOM_2013_29
Case Sensitive   : P: 0.45454545454545453 || R: 0.5357142857142857 || F1: 0.49180327868852464
Case Insensitive : P: 0.485 || R: 0.571 || F1: 0.524
2486 PP_1961_166
Case Sensitive   : P: 0.4090909090909091 || R: 0.4090909090909091 || F1: 0.4090909090909091
Case Insensitive : P: 0.455 || R: 0.455 || F1: 0.455
2487 Permen_Humham_2016_66
Case Sensitive   : P: 0.5625 || R: 0.6428571428571429 || F1: 0.6000000000000001
Case Insensitive : P: 0.594 || R: 0.679 || F1: 0.634
2488 PP_2007_62
Case Sensitive   : P: 0.782608695652174 || R: 0.9473684210526315 || F1: 0.8571428571428571
Case Insensitive : P: 0.826 || R: 1.0 || F1: 0.905
2489 Permen_Dikbud_2013_1
Case Sensitive   : P: 

Case Insensitive : P: 0.757 || R: 0.538 || F1: 0.629
2543 Permen_Hut_2010_12
Case Sensitive   : P: 0.32432432432432434 || R: 0.2033898305084746 || F1: 0.25
Case Insensitive : P: 0.351 || R: 0.22 || F1: 0.27
2544 Peraturan_KPU_2017_9
Case Sensitive   : P: 0.6521739130434783 || R: 0.7894736842105263 || F1: 0.7142857142857143
Case Insensitive : P: 0.652 || R: 0.789 || F1: 0.714
2545 Permen_Pora_2017_15
Case Sensitive   : P: 0.5945945945945946 || R: 0.5116279069767442 || F1: 0.55
Case Insensitive : P: 0.622 || R: 0.535 || F1: 0.575
2546 Peraturan_MA_2018_6
Case Sensitive   : P: 0.53125 || R: 0.5862068965517241 || F1: 0.5573770491803278
Case Insensitive : P: 0.531 || R: 0.586 || F1: 0.557
2547 Permen_Kes_2014_72
Case Sensitive   : P: 0.20588235294117646 || R: 0.6363636363636364 || F1: 0.3111111111111111
Case Insensitive : P: 0.235 || R: 0.727 || F1: 0.355
2548 Permen_Hub_2016_2
Case Sensitive   : P: 0.4 || R: 0.45161290322580644 || F1: 0.4242424242424243
Case Insensitive : P: 0.4 || R: 0.45

Case Insensitive : P: 0.579 || R: 0.423 || F1: 0.489
2599 Permen_Hut_2010_41
Case Sensitive   : P: 0.5 || R: 0.47368421052631576 || F1: 0.4864864864864865
Case Insensitive : P: 0.5 || R: 0.474 || F1: 0.487
2600 PP_2015_69
Case Sensitive   : P: 0.5909090909090909 || R: 0.7222222222222222 || F1: 0.65
Case Insensitive : P: 0.636 || R: 0.778 || F1: 0.7
2601 Permen_LH_2012_20
Case Sensitive   : P: 0.7142857142857143 || R: 0.8 || F1: 0.7547169811320756
Case Insensitive : P: 0.75 || R: 0.84 || F1: 0.792
2602 UU_1954_76
Case Sensitive   : P: 0.3333333333333333 || R: 0.5 || F1: 0.4
Case Insensitive : P: 0.333 || R: 0.5 || F1: 0.4
2603 Perkab_Magelang_2010_12
Case Sensitive   : P: 0.7837837837837838 || R: 0.5087719298245614 || F1: 0.6170212765957447
Case Insensitive : P: 0.784 || R: 0.509 || F1: 0.617
2604 Perpres_2016_68
Case Sensitive   : P: 0.5862068965517241 || R: 0.8095238095238095 || F1: 0.68
Case Insensitive : P: 0.586 || R: 0.81 || F1: 0.68
2605 Permen_Agama_2015_41
Case Sensitive   : P:

In [40]:
test_1('ofp', of_phi, test_opening, '1', 'results/metrics_of.csv')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.5909090909090909 || R: 0.325 || F1: 0.41935483870967744
Case Insensitive : P: 0.636 || R: 0.35 || F1: 0.452
1 Permen_KP_2013_5
Case Sensitive   : P: 0.6538461538461539 || R: 0.4722222222222222 || F1: 0.5483870967741936
Case Insensitive : P: 0.692 || R: 0.5 || F1: 0.581
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.47619047619047616 || R: 0.5555555555555556 || F1: 0.5128205128205129
Case Insensitive : P: 0.524 || R: 0.611 || F1: 0.564
3 Permen_Par_2015_14
Case Sensitive   : P: 0.6086956521739131 || R: 0.32558139534883723 || F1: 0.42424242424242425
Case Insensitive : P: 0.652 || R: 0.349 || F1: 0.455
4 Perpres_2019_67
Case Sensitive   : P: 0.625 || R: 0.625 || F1: 0.625
Case Insensitive : P: 0.667 || R: 0.667 || F1: 0.667
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.5625 || R: 0.1125 || F1: 0.18749999999999997
Case Insensitive : P: 0.594 || R: 0.119 || F1: 0.198
6 Perkab_Tabalong_2010_09
Case Sensitive   : P: 0.7142857142857143 

62 Permen_Tan_2017_49
Case Sensitive   : P: 0.5 || R: 0.31666666666666665 || F1: 0.3877551020408163
Case Insensitive : P: 0.526 || R: 0.333 || F1: 0.408
63 Perkot_Sorong_2013_32
Case Sensitive   : P: 0.625 || R: 0.23076923076923078 || F1: 0.33707865168539325
Case Insensitive : P: 0.667 || R: 0.246 || F1: 0.359
64 Perkot_Bogor_2006_11
Case Sensitive   : P: 0.36 || R: 0.07377049180327869 || F1: 0.12244897959183675
Case Insensitive : P: 0.4 || R: 0.082 || F1: 0.136
65 Perprov_Jateng_2001_10
Case Sensitive   : P: 0.6875 || R: 0.28205128205128205 || F1: 0.4
Case Insensitive : P: 0.688 || R: 0.282 || F1: 0.4
66 PP_2008_70
Case Sensitive   : P: 0.7391304347826086 || R: 0.7083333333333334 || F1: 0.723404255319149
Case Insensitive : P: 0.783 || R: 0.75 || F1: 0.766
67 Permen_Dikbud_2012_7
Case Sensitive   : P: 0.5238095238095238 || R: 0.3142857142857143 || F1: 0.39285714285714285
Case Insensitive : P: 0.571 || R: 0.343 || F1: 0.429
68 Perpres_2013_103
Case Sensitive   : P: 0.48717948717948717 |

117 Perkab_Ponorogo_2011_8
Case Sensitive   : P: 0.6666666666666666 || R: 0.04040404040404041 || F1: 0.0761904761904762
Case Insensitive : P: 0.75 || R: 0.045 || F1: 0.085
118 Peraturan_BSSN_2011_4
Case Sensitive   : P: 0.13636363636363635 || R: 0.1875 || F1: 0.15789473684210525
Case Insensitive : P: 0.182 || R: 0.25 || F1: 0.211
119 Peraturan_LPS_2019_4
Case Sensitive   : P: 0.35294117647058826 || R: 0.4 || F1: 0.37500000000000006
Case Insensitive : P: 0.412 || R: 0.467 || F1: 0.438
120 Perkab_Sleman_2012_1
Case Sensitive   : P: 0.6666666666666666 || R: 0.34782608695652173 || F1: 0.4571428571428571
Case Insensitive : P: 0.708 || R: 0.37 || F1: 0.486
121 Permen_Dagri_2017_111
Case Sensitive   : P: 0.4634146341463415 || R: 0.3958333333333333 || F1: 0.42696629213483145
Case Insensitive : P: 0.463 || R: 0.396 || F1: 0.427
122 Permen_ESDM_2013_17
Case Sensitive   : P: 0.47619047619047616 || R: 0.2857142857142857 || F1: 0.3571428571428571
Case Insensitive : P: 0.524 || R: 0.314 || F1: 0.393

187 Permen_Bappenas_2017_14
Case Sensitive   : P: 0.3918918918918919 || R: 0.3972602739726027 || F1: 0.39455782312925164
Case Insensitive : P: 0.392 || R: 0.397 || F1: 0.394
188 PP_2013_94
Case Sensitive   : P: 0.7619047619047619 || R: 0.6666666666666666 || F1: 0.7111111111111111
Case Insensitive : P: 0.81 || R: 0.708 || F1: 0.756
189 Perprov_Jatim_2009_3
Case Sensitive   : P: 0.19607843137254902 || R: 0.08333333333333333 || F1: 0.11695906432748536
Case Insensitive : P: 0.216 || R: 0.092 || F1: 0.129
190 Permen_Perin_2014_56
Case Sensitive   : P: 0.45161290322580644 || R: 0.27450980392156865 || F1: 0.34146341463414637
Case Insensitive : P: 0.484 || R: 0.294 || F1: 0.366
191 Permen_Perin_2013_35
Case Sensitive   : P: 0.47619047619047616 || R: 0.23255813953488372 || F1: 0.3125
Case Insensitive : P: 0.476 || R: 0.233 || F1: 0.313
192 Peraturan_BNPP_2018_6
Case Sensitive   : P: 0.6190476190476191 || R: 0.41935483870967744 || F1: 0.5
Case Insensitive : P: 0.667 || R: 0.452 || F1: 0.539
193 

Case Insensitive : P: 0.556 || R: 0.062 || F1: 0.112
245 Perkab_Buru_2012_01
Case Sensitive   : P: 0.24489795918367346 || R: 0.17391304347826086 || F1: 0.20338983050847456
Case Insensitive : P: 0.265 || R: 0.188 || F1: 0.22
246 Permen_ESDM_2011_17
Case Sensitive   : P: 0.391304347826087 || R: 0.20930232558139536 || F1: 0.2727272727272727
Case Insensitive : P: 0.391 || R: 0.209 || F1: 0.272
247 Perkab_Buol_2006_9
Case Sensitive   : P: 0.25 || R: 0.6666666666666666 || F1: 0.36363636363636365
Case Insensitive : P: 0.292 || R: 0.778 || F1: 0.425
248 Permen_Hub_2015_137
Case Sensitive   : P: 0.40540540540540543 || R: 0.375 || F1: 0.3896103896103896
Case Insensitive : P: 0.432 || R: 0.4 || F1: 0.415
249 Peraturan_BPH_Migas_2015_7
Case Sensitive   : P: 0.19047619047619047 || R: 0.08163265306122448 || F1: 0.11428571428571428
Case Insensitive : P: 0.19 || R: 0.082 || F1: 0.115
250 UU_2019_17
Case Sensitive   : P: 0.5 || R: 0.3333333333333333 || F1: 0.4
Case Insensitive : P: 0.583 || R: 0.389 ||

...

2378 Perkab_Garut_2011_4
Case Sensitive   : P: 0.6666666666666666 || R: 0.06818181818181818 || F1: 0.12371134020618554
Case Insensitive : P: 0.667 || R: 0.068 || F1: 0.123
2379 Permen_Dagri_2013_25
Case Sensitive   : P: 0.41935483870967744 || R: 0.2708333333333333 || F1: 0.3291139240506329
Case Insensitive : P: 0.452 || R: 0.292 || F1: 0.355
2380 Permen_Keu_2017_23
Case Sensitive   : P: 0.5 || R: 0.42857142857142855 || F1: 0.4615384615384615
Case Insensitive : P: 0.556 || R: 0.476 || F1: 0.513
2381 Permen_Ristekdikti_2017_8
Case Sensitive   : P: 0.47368421052631576 || R: 0.20454545454545456 || F1: 0.28571428571428575
Case Insensitive : P: 0.526 || R: 0.227 || F1: 0.317
2382 Permen_PR_2012_24
Case Sensitive   : P: 0.7931034482758621 || R: 0.27380952380952384 || F1: 0.4070796460176992
Case Insensitive : P: 0.793 || R: 0.274 || F1: 0.407
2383 Permen_Keu_2011_232
Case Sensitive   : P: 0.6060606060606061 || R: 0.625 || F1: 0.6153846153846154
Case Insensitive : P: 0.606 || R: 0.625 || F1: 0.

2433 Permen_PANRB_2016_22
Case Sensitive   : P: 0.34146341463414637 || R: 0.17721518987341772 || F1: 0.23333333333333334
Case Insensitive : P: 0.366 || R: 0.19 || F1: 0.25
2434 Permen_PPPA_2011_4
Case Sensitive   : P: 0.7307692307692307 || R: 0.5757575757575758 || F1: 0.6440677966101696
Case Insensitive : P: 0.769 || R: 0.606 || F1: 0.678
2435 Perkot_Malang_2007_4
Case Sensitive   : P: 0.5526315789473685 || R: 0.2079207920792079 || F1: 0.302158273381295
Case Insensitive : P: 0.553 || R: 0.208 || F1: 0.302
2436 Permen_Han_2015_35
Case Sensitive   : P: 0.5 || R: 0.32142857142857145 || F1: 0.391304347826087
Case Insensitive : P: 0.5 || R: 0.321 || F1: 0.391
2437 Perkot_Bandung_2000_04
Case Sensitive   : P: 0.43478260869565216 || R: 0.1388888888888889 || F1: 0.21052631578947367
Case Insensitive : P: 0.435 || R: 0.139 || F1: 0.211
2438 Permen_PR_2012_39
Case Sensitive   : P: 0.225 || R: 0.15517241379310345 || F1: 0.1836734693877551
Case Insensitive : P: 0.225 || R: 0.155 || F1: 0.184
2439 P

Case Insensitive : P: 0.324 || R: 0.19 || F1: 0.24
2491 Perkot_Depok_2012_02
Case Sensitive   : P: 0.2702702702702703 || R: 0.06896551724137931 || F1: 0.10989010989010989
Case Insensitive : P: 0.27 || R: 0.069 || F1: 0.11
2492 Permen_Keu_2011_238
Case Sensitive   : P: 0.3125 || R: 0.35714285714285715 || F1: 0.3333333333333333
Case Insensitive : P: 0.375 || R: 0.429 || F1: 0.4
2493 Perkab_Kulon_Progo_2006_3
Case Sensitive   : P: 0.10869565217391304 || R: 0.03676470588235294 || F1: 0.05494505494505495
Case Insensitive : P: 0.13 || R: 0.044 || F1: 0.066
2494 Perkot_Samarinda_2008_18
Case Sensitive   : P: 0.5357142857142857 || R: 0.17857142857142858 || F1: 0.26785714285714285
Case Insensitive : P: 0.536 || R: 0.179 || F1: 0.268
2495 UU_1974_4
Case Sensitive   : P: 0.47058823529411764 || R: 0.8421052631578947 || F1: 0.6037735849056604
Case Insensitive : P: 0.471 || R: 0.842 || F1: 0.604
2496 Peraturan_BPKP_2017_6
Case Sensitive   : P: 0.3333333333333333 || R: 0.18421052631578946 || F1: 0.23

Case Insensitive : P: 0.194 || R: 0.1 || F1: 0.132
2550 PP_2005_15
Case Sensitive   : P: 0.4 || R: 0.4444444444444444 || F1: 0.4210526315789474
Case Insensitive : P: 0.45 || R: 0.5 || F1: 0.474
2551 Perkab_Serdang_Bedagai_2012_14
Case Sensitive   : P: 0.7368421052631579 || R: 0.27450980392156865 || F1: 0.4
Case Insensitive : P: 0.789 || R: 0.294 || F1: 0.428
2552 PP_2003_34
Case Sensitive   : P: 0.6363636363636364 || R: 0.56 || F1: 0.5957446808510639
Case Insensitive : P: 0.636 || R: 0.56 || F1: 0.596
2553 Permen_Hub_2015_134
Case Sensitive   : P: 0.38095238095238093 || R: 0.32 || F1: 0.34782608695652173
Case Insensitive : P: 0.381 || R: 0.32 || F1: 0.348
2554 Permen_Ristekdikti_2016_55
Case Sensitive   : P: 0.5 || R: 0.34375 || F1: 0.4074074074074074
Case Insensitive : P: 0.545 || R: 0.375 || F1: 0.444
2555 Peraturan_OJK_2019_13
Case Sensitive   : P: 0.8181818181818182 || R: 0.75 || F1: 0.7826086956521738
Case Insensitive : P: 0.818 || R: 0.75 || F1: 0.783
2556 Permen_Kes_2013_75
Case

2611 Permen_Humham_2019_8
Case Sensitive   : P: 0.6190476190476191 || R: 0.4642857142857143 || F1: 0.5306122448979592
Case Insensitive : P: 0.667 || R: 0.5 || F1: 0.572
2612 Peraturan_Basarnas_2017_3
Case Sensitive   : P: 0.4 || R: 0.2962962962962963 || F1: 0.3404255319148936
Case Insensitive : P: 0.45 || R: 0.333 || F1: 0.383
2613 Permenko_Polhukam_2018_2
Case Sensitive   : P: 0.5625 || R: 0.5 || F1: 0.5294117647058824
Case Insensitive : P: 0.562 || R: 0.5 || F1: 0.529
2614 Permen_Hub_2013_81
Case Sensitive   : P: 0.17391304347826086 || R: 0.06060606060606061 || F1: 0.08988764044943821
Case Insensitive : P: 0.217 || R: 0.076 || F1: 0.113
2615 Perkab_Bantul_1995_8
Case Sensitive   : P: 0.19047619047619047 || R: 0.23529411764705882 || F1: 0.21052631578947367
Case Insensitive : P: 0.238 || R: 0.294 || F1: 0.263
2616 Permen_Agama_2017_2
Case Sensitive   : P: 0.375 || R: 0.1 || F1: 0.15789473684210528
Case Insensitive : P: 0.4 || R: 0.107 || F1: 0.169
2617 PP_1961_163
Case Sensitive   : P:

In [41]:
test_1('ofp', of_phi, test_opening, '2', 'results/metrics_of.csv')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.4482758620689655 || R: 0.325 || F1: 0.3768115942028986
Case Insensitive : P: 0.517 || R: 0.375 || F1: 0.435
1 Permen_KP_2013_5
Case Sensitive   : P: 0.59375 || R: 0.5277777777777778 || F1: 0.5588235294117648
Case Insensitive : P: 0.594 || R: 0.528 || F1: 0.559
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.7 || R: 0.7777777777777778 || F1: 0.7368421052631577
Case Insensitive : P: 0.75 || R: 0.833 || F1: 0.789
3 Permen_Par_2015_14
Case Sensitive   : P: 0.7714285714285715 || R: 0.627906976744186 || F1: 0.6923076923076923
Case Insensitive : P: 0.8 || R: 0.651 || F1: 0.718
4 Perpres_2019_67
Case Sensitive   : P: 0.6071428571428571 || R: 0.7083333333333334 || F1: 0.6538461538461539
Case Insensitive : P: 0.643 || R: 0.75 || F1: 0.692
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.8181818181818182 || R: 0.05625 || F1: 0.10526315789473685
Case Insensitive : P: 0.909 || R: 0.062 || F1: 0.116
6 Perkab_Tabalong_2010_09
Case Sensitive   : P:

Case Insensitive : P: 0.571 || R: 0.667 || F1: 0.615
54 Perpres_2006_98
Case Sensitive   : P: 0.6666666666666666 || R: 0.6086956521739131 || F1: 0.6363636363636365
Case Insensitive : P: 0.714 || R: 0.652 || F1: 0.682
55 PP_1970_19
Case Sensitive   : P: 0.2727272727272727 || R: 0.46153846153846156 || F1: 0.3428571428571428
Case Insensitive : P: 0.273 || R: 0.462 || F1: 0.343
56 UU_1957_59
Case Sensitive   : P: 0.4 || R: 0.5 || F1: 0.4444444444444445
Case Insensitive : P: 0.4 || R: 0.5 || F1: 0.444
57 Permen_Dikbud_2013_46
Case Sensitive   : P: 0.4117647058823529 || R: 0.32558139534883723 || F1: 0.36363636363636365
Case Insensitive : P: 0.471 || R: 0.372 || F1: 0.416
58 Permen_Keu_2015_201
Case Sensitive   : P: 0.25 || R: 0.2777777777777778 || F1: 0.2631578947368421
Case Insensitive : P: 0.25 || R: 0.278 || F1: 0.263
59 Permen_Hub_2012_36
Case Sensitive   : P: 0.16666666666666666 || R: 0.043478260869565216 || F1: 0.06896551724137931
Case Insensitive : P: 0.167 || R: 0.043 || F1: 0.068
60

Case Insensitive : P: 0.581 || R: 0.532 || F1: 0.555
113 Perkot_Pasuruan_2011_24
Case Sensitive   : P: 0.7441860465116279 || R: 0.5714285714285714 || F1: 0.6464646464646464
Case Insensitive : P: 0.744 || R: 0.571 || F1: 0.646
114 Permen_Naker_2015_25
Case Sensitive   : P: 0.5714285714285714 || R: 0.3076923076923077 || F1: 0.4
Case Insensitive : P: 0.571 || R: 0.308 || F1: 0.4
115 PP_2011_79
Case Sensitive   : P: 0.5925925925925926 || R: 0.6956521739130435 || F1: 0.6399999999999999
Case Insensitive : P: 0.667 || R: 0.783 || F1: 0.72
116 Permen_Humham_2013_10
Case Sensitive   : P: 0.5909090909090909 || R: 0.325 || F1: 0.41935483870967744
Case Insensitive : P: 0.682 || R: 0.375 || F1: 0.484
117 Perkab_Ponorogo_2011_8
Case Sensitive   : P: 0.9166666666666666 || R: 0.05555555555555555 || F1: 0.10476190476190475
Case Insensitive : P: 0.917 || R: 0.056 || F1: 0.106
118 Peraturan_BSSN_2011_4
Case Sensitive   : P: 0.25 || R: 0.375 || F1: 0.3
Case Insensitive : P: 0.292 || R: 0.438 || F1: 0.35
1

167 Perkab_Cilacap_2012_13
Case Sensitive   : P: 0.6785714285714286 || R: 0.6229508196721312 || F1: 0.6495726495726496
Case Insensitive : P: 0.696 || R: 0.639 || F1: 0.666
168 PP_2013_67
Case Sensitive   : P: 0.6666666666666666 || R: 0.6666666666666666 || F1: 0.6666666666666666
Case Insensitive : P: 0.722 || R: 0.722 || F1: 0.722
169 Peraturan_OJK_2019_5
Case Sensitive   : P: 0.75 || R: 0.75 || F1: 0.75
Case Insensitive : P: 0.8 || R: 0.8 || F1: 0.8
170 Peraturan_LPSK_2011_1
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
171 Permen_Ristekdikti_2015_36
Case Sensitive   : P: 0.5357142857142857 || R: 0.4166666666666667 || F1: 0.46875000000000006
Case Insensitive : P: 0.571 || R: 0.444 || F1: 0.5
172 Permen_Tan_2018_22
Case Sensitive   : P: 0.36 || R: 0.29508196721311475 || F1: 0.32432432432432434
Case Insensitive : P: 0.42 || R: 0.344 || F1: 0.378
173 Perkab_Tanggamus_2004_8
Case Sensitive   : P: 0.08695652173913043 || R: 0.6 || F1: 0.15189873417

Case Insensitive : P: 0.283 || R: 0.386 || F1: 0.327
225 Perpres_2015_22
Case Sensitive   : P: 0.4117647058823529 || R: 0.21875 || F1: 0.2857142857142857
Case Insensitive : P: 0.471 || R: 0.25 || F1: 0.327
226 Permen_Hub_2012_68
Case Sensitive   : P: 0.2777777777777778 || R: 0.07352941176470588 || F1: 0.11627906976744186
Case Insensitive : P: 0.278 || R: 0.074 || F1: 0.117
227 Perkab_Purworejo_2012_3
Case Sensitive   : P: 0.37037037037037035 || R: 0.379746835443038 || F1: 0.375
Case Insensitive : P: 0.383 || R: 0.392 || F1: 0.387
228 Permen_Tan_2013_81
Case Sensitive   : P: 0.2909090909090909 || R: 0.26666666666666666 || F1: 0.2782608695652174
Case Insensitive : P: 0.309 || R: 0.283 || F1: 0.295
229 Peraturan_Bawaslu_2018_32
Case Sensitive   : P: 0.6086956521739131 || R: 0.7368421052631579 || F1: 0.6666666666666666
Case Insensitive : P: 0.609 || R: 0.737 || F1: 0.667
230 Perkot_Bekasi_2013_07
Case Sensitive   : P: 0.08333333333333333 || R: 0.011764705882352941 || F1: 0.0206185567010309

...

2402 Permen_Hub_2017_87
Case Sensitive   : P: 0.16666666666666666 || R: 0.08695652173913043 || F1: 0.11428571428571427
Case Insensitive : P: 0.167 || R: 0.087 || F1: 0.114
2403 Peraturan_Batan_2016_4
Case Sensitive   : P: 0.6363636363636364 || R: 0.6363636363636364 || F1: 0.6363636363636364
Case Insensitive : P: 0.636 || R: 0.636 || F1: 0.636
2404 PP_1957_13
Case Sensitive   : P: 0.3333333333333333 || R: 0.42105263157894735 || F1: 0.372093023255814
Case Insensitive : P: 0.333 || R: 0.421 || F1: 0.372
2405 Peraturan_BPJSTK_2018_1
Case Sensitive   : P: 0.4857142857142857 || R: 0.5483870967741935 || F1: 0.5151515151515151
Case Insensitive : P: 0.486 || R: 0.548 || F1: 0.515
2406 Peraturan_LIPI_2017_1
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2407 Permen_Keu_2010_19
Case Sensitive   : P: 0.5714285714285714 || R: 0.64 || F1: 0.6037735849056605
Case Insensitive : P: 0.607 || R: 0.68 || F1: 0.641
2408 Permen_Dikbud_2012_72
Case Sensitive   : P: 

2458 Permen_Hut_2012_42
Case Sensitive   : P: 0.3409090909090909 || R: 0.3125 || F1: 0.32608695652173914
Case Insensitive : P: 0.341 || R: 0.312 || F1: 0.326
2459 Permen_Keu_2019_118
Case Sensitive   : P: 0.37142857142857144 || R: 0.24074074074074073 || F1: 0.29213483146067415
Case Insensitive : P: 0.371 || R: 0.241 || F1: 0.292
2460 Permen_Naker_2018_2
Case Sensitive   : P: 0.21428571428571427 || R: 0.2222222222222222 || F1: 0.21818181818181817
Case Insensitive : P: 0.214 || R: 0.222 || F1: 0.218
2461 Perkab_Way_Kanan_2001_4
Case Sensitive   : P: 0.8333333333333334 || R: 0.6730769230769231 || F1: 0.74468085106383
Case Insensitive : P: 0.857 || R: 0.692 || F1: 0.766
2462 Perkab_Bulungan_2009_2
Case Sensitive   : P: 0.7575757575757576 || R: 0.36231884057971014 || F1: 0.49019607843137253
Case Insensitive : P: 0.758 || R: 0.362 || F1: 0.49
2463 Permen_PUPR_2015_10
Case Sensitive   : P: 0.75 || R: 0.4864864864864865 || F1: 0.5901639344262296
Case Insensitive : P: 0.792 || R: 0.514 || F1: 0

2511 Permen_Sos_2017_30
Case Sensitive   : P: 0.5777777777777777 || R: 0.6046511627906976 || F1: 0.5909090909090908
Case Insensitive : P: 0.578 || R: 0.605 || F1: 0.591
2512 Permen_Agama_2018_4
Case Sensitive   : P: 0.5 || R: 0.4166666666666667 || F1: 0.45454545454545453
Case Insensitive : P: 0.533 || R: 0.444 || F1: 0.484
2513 PP_1977_24
Case Sensitive   : P: 0.6666666666666666 || R: 0.7058823529411765 || F1: 0.6857142857142857
Case Insensitive : P: 0.722 || R: 0.765 || F1: 0.743
2514 Peraturan_LAN_2017_14
Case Sensitive   : P: 0.42857142857142855 || R: 0.2926829268292683 || F1: 0.34782608695652173
Case Insensitive : P: 0.429 || R: 0.293 || F1: 0.348
2515 Permen_Keu_2010_219
Case Sensitive   : P: 0.6818181818181818 || R: 0.8333333333333334 || F1: 0.7499999999999999
Case Insensitive : P: 0.727 || R: 0.889 || F1: 0.8
2516 Permen_Tan_2015_59
Case Sensitive   : P: 0.5238095238095238 || R: 0.3728813559322034 || F1: 0.43564356435643564
Case Insensitive : P: 0.524 || R: 0.373 || F1: 0.436
25

2570 Permenko_Kesra_2014_9
Case Sensitive   : P: 0.25 || R: 0.19444444444444445 || F1: 0.21875000000000003
Case Insensitive : P: 0.286 || R: 0.222 || F1: 0.25
2571 Peraturan_Basarnas_2016_2
Case Sensitive   : P: 0.32142857142857145 || R: 0.21428571428571427 || F1: 0.2571428571428572
Case Insensitive : P: 0.357 || R: 0.238 || F1: 0.286
2572 Peraturan_Bapeten_2011_7
Case Sensitive   : P: 0.2727272727272727 || R: 0.23076923076923078 || F1: 0.24999999999999994
Case Insensitive : P: 0.273 || R: 0.231 || F1: 0.25
2573 Perpres_2019_2
Case Sensitive   : P: 0.625 || R: 0.37037037037037035 || F1: 0.4651162790697674
Case Insensitive : P: 0.688 || R: 0.407 || F1: 0.511
2574 Perkab_Poso_2010_9
Case Sensitive   : P: 0.75 || R: 0.4864864864864865 || F1: 0.5901639344262296
Case Insensitive : P: 0.75 || R: 0.486 || F1: 0.59
2575 UU_2007_5
Case Sensitive   : P: 0.35135135135135137 || R: 0.3170731707317073 || F1: 0.33333333333333337
Case Insensitive : P: 0.378 || R: 0.341 || F1: 0.359
2576 Perkab_Musi_Ra

Case Insensitive : P: 0.727 || R: 0.333 || F1: 0.457
2629 Peraturan_OJK_2014_37
Case Sensitive   : P: 0.4 || R: 0.4 || F1: 0.4000000000000001
Case Insensitive : P: 0.4 || R: 0.4 || F1: 0.4
2630 Permen_Dag_2015_115
Case Sensitive   : P: 0.4 || R: 0.029850746268656716 || F1: 0.05555555555555556
Case Insensitive : P: 0.4 || R: 0.03 || F1: 0.056
2631 Perpres_2011_24
Case Sensitive   : P: 0.6842105263157895 || R: 0.6842105263157895 || F1: 0.6842105263157895
Case Insensitive : P: 0.684 || R: 0.684 || F1: 0.684
2632 PP_1954_4
Case Sensitive   : P: 0.2727272727272727 || R: 0.75 || F1: 0.39999999999999997
Case Insensitive : P: 0.273 || R: 0.75 || F1: 0.4
2633 Perkab_Bantul_2000_45
Case Sensitive   : P: 0.7083333333333334 || R: 0.38636363636363635 || F1: 0.5
Case Insensitive : P: 0.708 || R: 0.386 || F1: 0.5
2634 Peraturan_BPS_2012_49
Case Sensitive   : P: 0.05263157894736842 || R: 0.029411764705882353 || F1: 0.03773584905660377
Case Insensitive : P: 0.053 || R: 0.029 || F1: 0.037
2635 Permen_Da

#### Body

In [65]:
test_body_name = "dataset-surface-info/body-struktur/body-struktur-1"
test_body = load_from_disk(test_body_name)
len(test_body)

2640

In [66]:
bf_gemma = pd.read_csv('results/new/BF_gemma_post.csv')
bf_llama = pd.read_csv('results/new/BF_llama_post.csv')
bf_phi = pd.read_csv('results/new/BF_phi_post.csv')

In [67]:
results = pd.DataFrame()
results = pd.DataFrame(columns=['regulatory'
                                , 'bfg_p_1'
                                , 'bfg_r_1'
                                , 'bfg_f1_1'
                                , 'bfg_p_2'
                                , 'bfg_r_2'
                                , 'bfg_f1_2'
                                , 'bfl_p_1'
                                , 'bfl_r_1'
                                , 'bfl_f1_1'
                                , 'bfl_p_2'
                                , 'bfl_r_2'
                                , 'bfl_f1_2'
                                , 'bfp_p_1'
                                , 'bfp_r_1'
                                , 'bfp_f1_1'
                                , 'bfp_p_2'
                                , 'bfp_r_2'
                                , 'bfp_f1_2'
                               ])

In [ ]:
test_1('bfg', bf_gemma, test_body, '1', 'results/metrics_bf.csv')

In [ ]:
test_1('bfg', bf_gemma, test_body, '2', 'results/metrics_bf.csv')

In [69]:
test_1('bfl', bf_llama, test_body, '1', 'results/metrics_bf.csv')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.9473684210526315 || R: 0.6666666666666666 || F1: 0.782608695652174
Case Insensitive : P: 0.947 || R: 0.667 || F1: 0.783
1 Permen_KP_2013_5
Case Sensitive   : P: 0.45652173913043476 || R: 0.0945945945945946 || F1: 0.1567164179104478
Case Insensitive : P: 0.457 || R: 0.095 || F1: 0.157
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.5357142857142857 || R: 0.15151515151515152 || F1: 0.2362204724409449
Case Insensitive : P: 0.536 || R: 0.152 || F1: 0.237
3 Permen_Par_2015_14
Case Sensitive   : P: 1.0 || R: 0.3333333333333333 || F1: 0.5
Case Insensitive : P: 1.0 || R: 0.333 || F1: 0.5
4 Perpres_2019_67
Case Sensitive   : P: 1.0 || R: 0.3333333333333333 || F1: 0.5
Case Insensitive : P: 1.0 || R: 0.333 || F1: 0.5
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.125 || R: 0.02005730659025788 || F1: 0.0345679012345679
Case Insensitive : P: 0.125 || R: 0.02 || F1: 0.034
6 Perkab_Tabalong_2010_09
Case Sensitive   : P: 0.3684210526315789 || R: 

Case Insensitive : P: 0.432 || R: 0.127 || F1: 0.196
59 Permen_Hub_2012_36
Case Sensitive   : P: 0.3541666666666667 || R: 0.13178294573643412 || F1: 0.192090395480226
Case Insensitive : P: 0.354 || R: 0.132 || F1: 0.192
60 Permen_Hut_2009_32
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
61 Peraturan_KPU_2018_11
Case Sensitive   : P: 0.9 || R: 0.09 || F1: 0.16363636363636364
Case Insensitive : P: 0.9 || R: 0.09 || F1: 0.164
62 Permen_Tan_2017_49
Case Sensitive   : P: 0.3333333333333333 || R: 0.10884353741496598 || F1: 0.16410256410256407
Case Insensitive : P: 0.333 || R: 0.109 || F1: 0.164
63 Perkot_Sorong_2013_32
Case Sensitive   : P: 0.5217391304347826 || R: 0.23300970873786409 || F1: 0.3221476510067114
Case Insensitive : P: 0.522 || R: 0.233 || F1: 0.322
64 Perkot_Bogor_2006_11
Case Sensitive   : P: 0.3333333333333333 || R: 0.14615384615384616 || F1: 0.20320855614973263
Case Insensitive : P: 0.333 || R: 0.146 || F1: 0.203
65 Perprov_Jateng_

122 Permen_ESDM_2013_17
Case Sensitive   : P: 0.275 || R: 0.07801418439716312 || F1: 0.12154696132596686
Case Insensitive : P: 0.275 || R: 0.078 || F1: 0.122
123 Perprov_Yogya_2001_8
Case Sensitive   : P: 1.0 || R: 0.5714285714285714 || F1: 0.7272727272727273
Case Insensitive : P: 1.0 || R: 0.571 || F1: 0.727
124 Permen_Dikbud_2014_115
Case Sensitive   : P: 0.4576271186440678 || R: 0.05521472392638037 || F1: 0.09854014598540146
Case Insensitive : P: 0.458 || R: 0.055 || F1: 0.098
125 Peraturan_BPKP_2016_23
Case Sensitive   : P: 1.0 || R: 0.6666666666666666 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
126 Permen_Tan_2012_53
Case Sensitive   : P: 1.0 || R: 0.6666666666666666 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
127 Perpres_2010_2
Case Sensitive   : P: 1.0 || R: 0.6666666666666666 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
128 Permen_Dikbud_2012_58
Case Sensitive   : P: 1.0 || R: 0.6666666666666666 || F1: 0.8
Case Insensitive : P: 1.0

Case Insensitive : P: 0.474 || R: 0.176 || F1: 0.257
184 Perprov_Sulteng_2002_06
Case Sensitive   : P: 0.35555555555555557 || R: 0.12030075187969924 || F1: 0.1797752808988764
Case Insensitive : P: 0.356 || R: 0.12 || F1: 0.179
185 PP_1990_46
Case Sensitive   : P: 1.0 || R: 0.30303030303030304 || F1: 0.4651162790697675
Case Insensitive : P: 1.0 || R: 0.303 || F1: 0.465
186 Permen_Ristekdikti_2016_57
Case Sensitive   : P: 1.0 || R: 0.6666666666666666 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
187 Permen_Bappenas_2017_14
Case Sensitive   : P: 0.23255813953488372 || R: 0.0641025641025641 || F1: 0.10050251256281408
Case Insensitive : P: 0.233 || R: 0.064 || F1: 0.1
188 PP_2013_94
Case Sensitive   : P: 1.0 || R: 0.3333333333333333 || F1: 0.5
Case Insensitive : P: 1.0 || R: 0.333 || F1: 0.5
189 Perprov_Jatim_2009_3
Case Sensitive   : P: 0.2972972972972973 || R: 0.044534412955465584 || F1: 0.07746478873239437
Case Insensitive : P: 0.297 || R: 0.045 || F1: 0.078
190 Permen_Peri

243 Permen_Agama_2018_19
Case Sensitive   : P: 0.5641025641025641 || R: 0.08979591836734693 || F1: 0.15492957746478872
Case Insensitive : P: 0.564 || R: 0.09 || F1: 0.155
244 Permen_Tan_2014_127
Case Sensitive   : P: 0.3488372093023256 || R: 0.07352941176470588 || F1: 0.12145748987854252
Case Insensitive : P: 0.349 || R: 0.074 || F1: 0.122
245 Perkab_Buru_2012_01
Case Sensitive   : P: 0.25 || R: 0.10810810810810811 || F1: 0.1509433962264151
Case Insensitive : P: 0.25 || R: 0.108 || F1: 0.151
246 Permen_ESDM_2011_17
Case Sensitive   : P: 1.0 || R: 0.3333333333333333 || F1: 0.5
Case Insensitive : P: 1.0 || R: 0.333 || F1: 0.5
247 Perkab_Buol_2006_9
Case Sensitive   : P: 0.5882352941176471 || R: 0.16393442622950818 || F1: 0.25641025641025644
Case Insensitive : P: 0.588 || R: 0.164 || F1: 0.256
248 Permen_Hub_2015_137
Case Sensitive   : P: 1.0 || R: 0.3333333333333333 || F1: 0.5
Case Insensitive : P: 1.0 || R: 0.333 || F1: 0.5
249 Peraturan_BPH_Migas_2015_7
Case Sensitive   : P: 1.0 || R: 

...

Case Insensitive : P: 0.361 || R: 0.047 || F1: 0.083
2368 Permen_Kominfo_2013_26
Case Sensitive   : P: 1.0 || R: 0.6666666666666666 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
2369 Permen_Hub_2016_93
Case Sensitive   : P: 1.0 || R: 0.6666666666666666 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
2370 Peraturan_Jagung_2013_002
Case Sensitive   : P: 0.25 || R: 0.0990990990990991 || F1: 0.14193548387096774
Case Insensitive : P: 0.25 || R: 0.099 || F1: 0.142
2371 Permen_Agama_2013_32
Case Sensitive   : P: 0.35 || R: 0.045307443365695796 || F1: 0.08022922636103151
Case Insensitive : P: 0.35 || R: 0.045 || F1: 0.08
2372 Permen_Keu_2019_95
Case Sensitive   : P: 1.0 || R: 0.3333333333333333 || F1: 0.5
Case Insensitive : P: 1.0 || R: 0.333 || F1: 0.5
2373 Perpres_2014_44
Case Sensitive   : P: 0.8181818181818182 || R: 0.36585365853658536 || F1: 0.5056179775280899
Case Insensitive : P: 0.818 || R: 0.366 || F1: 0.506
2374 Perkab_Tuban_2012_10
Case Sensitive   : P: 0.2

Case Insensitive : P: 1.0 || R: 0.094 || F1: 0.172
2427 Perkab_Pacitan_2010_6
Case Sensitive   : P: 1.0 || R: 0.5714285714285714 || F1: 0.7272727272727273
Case Insensitive : P: 1.0 || R: 0.571 || F1: 0.727
2428 Perkab_Bengkulu_Tengah_2011_12
Case Sensitive   : P: 0.4444444444444444 || R: 0.14285714285714285 || F1: 0.21621621621621623
Case Insensitive : P: 0.444 || R: 0.143 || F1: 0.216
2429 Permen_KP_2018_64
Case Sensitive   : P: 0.6 || R: 0.20689655172413793 || F1: 0.3076923076923077
Case Insensitive : P: 0.6 || R: 0.207 || F1: 0.308
2430 Perprov_Kaltim_2011_08
Case Sensitive   : P: 0.42857142857142855 || R: 0.3 || F1: 0.3529411764705882
Case Insensitive : P: 0.429 || R: 0.3 || F1: 0.353
2431 Perkab_Jembrana_2011_4
Case Sensitive   : P: 0.78125 || R: 0.2066115702479339 || F1: 0.32679738562091504
Case Insensitive : P: 0.781 || R: 0.207 || F1: 0.327
2432 PP_2016_59
Case Sensitive   : P: 0.6904761904761905 || R: 0.2196969696969697 || F1: 0.3333333333333333
Case Insensitive : P: 0.69 || R

Case Insensitive : P: 0.158 || R: 0.021 || F1: 0.037
2492 Permen_Keu_2011_238
Case Sensitive   : P: 1.0 || R: 0.4523809523809524 || F1: 0.6229508196721312
Case Insensitive : P: 1.0 || R: 0.452 || F1: 0.623
2493 Perkab_Kulon_Progo_2006_3
Case Sensitive   : P: 0.2857142857142857 || R: 0.16 || F1: 0.20512820512820512
Case Insensitive : P: 0.286 || R: 0.16 || F1: 0.205
2494 Perkot_Samarinda_2008_18
Case Sensitive   : P: 0.2558139534883721 || R: 0.07142857142857142 || F1: 0.1116751269035533
Case Insensitive : P: 0.256 || R: 0.071 || F1: 0.111
2495 UU_1974_4
Case Sensitive   : P: 1.0 || R: 0.4166666666666667 || F1: 0.5882352941176471
Case Insensitive : P: 1.0 || R: 0.417 || F1: 0.589
2496 Peraturan_BPKP_2017_6
Case Sensitive   : P: 0.9615384615384616 || R: 0.2777777777777778 || F1: 0.43103448275862066
Case Insensitive : P: 0.962 || R: 0.278 || F1: 0.431
2497 Permen_Perin_2019_35
Case Sensitive   : P: 1.0 || R: 0.3333333333333333 || F1: 0.5
Case Insensitive : P: 1.0 || R: 0.333 || F1: 0.5
249

Case Insensitive : P: 0.154 || R: 0.03 || F1: 0.05
2554 Permen_Ristekdikti_2016_55
Case Sensitive   : P: 1.0 || R: 0.6666666666666666 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
2555 Peraturan_OJK_2019_13
Case Sensitive   : P: 1.0 || R: 0.3 || F1: 0.4615384615384615
Case Insensitive : P: 1.0 || R: 0.3 || F1: 0.462
2556 Permen_Kes_2013_75
Case Sensitive   : P: 1.0 || R: 0.3333333333333333 || F1: 0.5
Case Insensitive : P: 1.0 || R: 0.333 || F1: 0.5
2557 Permen_Dagri_2012_16
Case Sensitive   : P: 1.0 || R: 0.6666666666666666 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
2558 Perkot_Bogor_2011_4
Case Sensitive   : P: 0.21428571428571427 || R: 0.05844155844155844 || F1: 0.09183673469387756
Case Insensitive : P: 0.214 || R: 0.058 || F1: 0.091
2559 Perkot_Madiun_2008_07
Case Sensitive   : P: 0.14285714285714285 || R: 0.08536585365853659 || F1: 0.10687022900763359
Case Insensitive : P: 0.143 || R: 0.085 || F1: 0.107
2560 Permen_Dagri_2016_32
Case Sensitive   : P: 

2612 Peraturan_Basarnas_2017_3
Case Sensitive   : P: 1.0 || R: 0.39285714285714285 || F1: 0.5641025641025641
Case Insensitive : P: 1.0 || R: 0.393 || F1: 0.564
2613 Permenko_Polhukam_2018_2
Case Sensitive   : P: 0.7777777777777778 || R: 0.09523809523809523 || F1: 0.16969696969696968
Case Insensitive : P: 0.778 || R: 0.095 || F1: 0.169
2614 Permen_Hub_2013_81
Case Sensitive   : P: 1.0 || R: 0.6666666666666666 || F1: 0.8
Case Insensitive : P: 1.0 || R: 0.667 || F1: 0.8
2615 Perkab_Bantul_1995_8
Case Sensitive   : P: 1.0 || R: 0.41304347826086957 || F1: 0.5846153846153846
Case Insensitive : P: 1.0 || R: 0.413 || F1: 0.585
2616 Permen_Agama_2017_2
Case Sensitive   : P: 0.09836065573770492 || R: 0.0106951871657754 || F1: 0.019292604501607715
Case Insensitive : P: 0.098 || R: 0.011 || F1: 0.02
2617 PP_1961_163
Case Sensitive   : P: 0.25 || R: 0.16666666666666666 || F1: 0.2
Case Insensitive : P: 0.25 || R: 0.167 || F1: 0.2
2618 PP_2008_69
Case Sensitive   : P: 1.0 || R: 0.3333333333333333 || 

In [70]:
test_1('bfl', bf_llama, test_body, '2', 'results/metrics_bf.csv')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.9473684210526315 || R: 0.3333333333333333 || F1: 0.4931506849315068
Case Insensitive : P: 0.947 || R: 0.333 || F1: 0.493
1 Permen_KP_2013_5
Case Sensitive   : P: 0.46875 || R: 0.13513513513513514 || F1: 0.20979020979020982
Case Insensitive : P: 0.469 || R: 0.135 || F1: 0.21
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.6363636363636364 || R: 0.1414141414141414 || F1: 0.23140495867768593
Case Insensitive : P: 0.636 || R: 0.141 || F1: 0.231
3 Permen_Par_2015_14
Case Sensitive   : P: 0.17391304347826086 || R: 0.3333333333333333 || F1: 0.22857142857142854
Case Insensitive : P: 0.174 || R: 0.333 || F1: 0.229
4 Perpres_2019_67
Case Sensitive   : P: 1.0 || R: 0.42028985507246375 || F1: 0.5918367346938774
Case Insensitive : P: 1.0 || R: 0.42 || F1: 0.592
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.12280701754385964 || R: 0.02005730659025788 || F1: 0.034482758620689655
Case Insensitive : P: 0.123 || R: 0.02 || F1: 0.034
6 Perkab_Tabal

57 Permen_Dikbud_2013_46
Case Sensitive   : P: 0.09433962264150944 || R: 0.010752688172043012 || F1: 0.019305019305019308
Case Insensitive : P: 0.094 || R: 0.011 || F1: 0.02
58 Permen_Keu_2015_201
Case Sensitive   : P: 0.2413793103448276 || R: 0.05555555555555555 || F1: 0.09032258064516129
Case Insensitive : P: 0.241 || R: 0.056 || F1: 0.091
59 Permen_Hub_2012_36
Case Sensitive   : P: 0.3548387096774194 || R: 0.17054263565891473 || F1: 0.23036649214659688
Case Insensitive : P: 0.355 || R: 0.171 || F1: 0.231
60 Permen_Hut_2009_32
Case Sensitive   : P: 0.09836065573770492 || R: 0.6666666666666666 || F1: 0.1714285714285714
Case Insensitive : P: 0.098 || R: 0.667 || F1: 0.171
61 Peraturan_KPU_2018_11
Case Sensitive   : P: 0.2631578947368421 || R: 0.05 || F1: 0.08403361344537816
Case Insensitive : P: 0.263 || R: 0.05 || F1: 0.084
62 Permen_Tan_2017_49
Case Sensitive   : P: 0.6666666666666666 || R: 0.06802721088435375 || F1: 0.1234567901234568
Case Insensitive : P: 0.667 || R: 0.068 || F1: 0

Case Insensitive : P: 0.882 || R: 0.417 || F1: 0.566
111 Perkot_Bandung_2012_17
Case Sensitive   : P: 0.41304347826086957 || R: 0.12101910828025478 || F1: 0.18719211822660098
Case Insensitive : P: 0.413 || R: 0.121 || F1: 0.187
112 Permen_ESDM_2016_21
Case Sensitive   : P: 0.5277777777777778 || R: 0.21839080459770116 || F1: 0.3089430894308943
Case Insensitive : P: 0.528 || R: 0.218 || F1: 0.309
113 Perkot_Pasuruan_2011_24
Case Sensitive   : P: 0.5151515151515151 || R: 0.29310344827586204 || F1: 0.3736263736263736
Case Insensitive : P: 0.515 || R: 0.293 || F1: 0.374
114 Permen_Naker_2015_25
Case Sensitive   : P: 0.55 || R: 0.21568627450980393 || F1: 0.30985915492957744
Case Insensitive : P: 0.55 || R: 0.216 || F1: 0.31
115 PP_2011_79
Case Sensitive   : P: 0.0625 || R: 0.3333333333333333 || F1: 0.10526315789473684
Case Insensitive : P: 0.062 || R: 0.333 || F1: 0.105
116 Permen_Humham_2013_10
Case Sensitive   : P: 1.0 || R: 0.27450980392156865 || F1: 0.43076923076923085
Case Insensitive :

Case Insensitive : P: 0.231 || R: 0.123 || F1: 0.161
165 Peraturan_OJK_2014_28
Case Sensitive   : P: 0.07407407407407407 || R: 0.011204481792717087 || F1: 0.019464720194647202
Case Insensitive : P: 0.074 || R: 0.011 || F1: 0.019
166 Permen_Par_2014_2
Case Sensitive   : P: 0.2962962962962963 || R: 0.3333333333333333 || F1: 0.3137254901960785
Case Insensitive : P: 0.296 || R: 0.333 || F1: 0.313
167 Perkab_Cilacap_2012_13
Case Sensitive   : P: 0.9736842105263158 || R: 0.26618705035971224 || F1: 0.4180790960451978
Case Insensitive : P: 0.974 || R: 0.266 || F1: 0.418
168 PP_2013_67
Case Sensitive   : P: 0.17647058823529413 || R: 0.03529411764705882 || F1: 0.0588235294117647
Case Insensitive : P: 0.176 || R: 0.035 || F1: 0.058
169 Peraturan_OJK_2019_5
Case Sensitive   : P: 1.0 || R: 0.24242424242424243 || F1: 0.3902439024390244
Case Insensitive : P: 1.0 || R: 0.242 || F1: 0.39
170 Peraturan_LPSK_2011_1
Case Sensitive   : P: 0.7272727272727273 || R: 0.17204301075268819 || F1: 0.27826086956521

Case Insensitive : P: 0.113 || R: 0.036 || F1: 0.055
218 Peraturan_BPOM_2013_24
Case Sensitive   : P: 0.9375 || R: 0.25 || F1: 0.39473684210526316
Case Insensitive : P: 0.938 || R: 0.25 || F1: 0.395
219 PP_1980_40
Case Sensitive   : P: 0.1 || R: 0.3333333333333333 || F1: 0.15384615384615383
Case Insensitive : P: 0.1 || R: 0.333 || F1: 0.154
220 PP_1984_27
Case Sensitive   : P: 0.078125 || R: 0.0228310502283105 || F1: 0.0353356890459364
Case Insensitive : P: 0.078 || R: 0.023 || F1: 0.036
221 PP_1981_7
Case Sensitive   : P: 1.0 || R: 0.45454545454545453 || F1: 0.625
Case Insensitive : P: 1.0 || R: 0.455 || F1: 0.625
222 Permen_Keu_2013_218
Case Sensitive   : P: 0.21875 || R: 0.21212121212121213 || F1: 0.21538461538461537
Case Insensitive : P: 0.219 || R: 0.212 || F1: 0.215
223 Perkab_Garut_2008_2
Case Sensitive   : P: 0.7 || R: 0.2966101694915254 || F1: 0.41666666666666663
Case Insensitive : P: 0.7 || R: 0.297 || F1: 0.417
224 Permen_Humham_2012_26
Case Sensitive   : P: 0.93333333333333

...

2412 Peraturan_Polri_2018_4
Case Sensitive   : P: 0.5 || R: 0.11904761904761904 || F1: 0.1923076923076923
Case Insensitive : P: 0.5 || R: 0.119 || F1: 0.192
2413 UU_1953_7
Case Sensitive   : P: 0.2318840579710145 || R: 0.037037037037037035 || F1: 0.06387225548902196
Case Insensitive : P: 0.232 || R: 0.037 || F1: 0.064
2414 Permen_Kes_2016_1
Case Sensitive   : P: 1.0 || R: 0.4126984126984127 || F1: 0.5842696629213483
Case Insensitive : P: 1.0 || R: 0.413 || F1: 0.585
2415 Perkot_Tasikmalaya_2007_8
Case Sensitive   : P: 0.4444444444444444 || R: 0.16216216216216217 || F1: 0.23762376237623764
Case Insensitive : P: 0.444 || R: 0.162 || F1: 0.237
2416 PP_1994_8
Case Sensitive   : P: 0.1836734693877551 || R: 0.17647058823529413 || F1: 0.18000000000000002
Case Insensitive : P: 0.184 || R: 0.176 || F1: 0.18
2417 Permen_Hub_2018_27
Case Sensitive   : P: 0.06557377049180328 || R: 0.009456264775413711 || F1: 0.016528925619834708
Case Insensitive : P: 0.066 || R: 0.009 || F1: 0.016
2418 PP_1996_14


Case Insensitive : P: 0.6 || R: 0.132 || F1: 0.216
2473 Permen_Keu_2010_64
Case Sensitive   : P: 1.0 || R: 0.3333333333333333 || F1: 0.5
Case Insensitive : P: 1.0 || R: 0.333 || F1: 0.5
2474 Perpres_2018_107
Case Sensitive   : P: 1.0 || R: 0.3333333333333333 || F1: 0.5
Case Insensitive : P: 1.0 || R: 0.333 || F1: 0.5
2475 Peraturan_BKKBN_2016_481
Case Sensitive   : P: 0.45714285714285713 || R: 0.13675213675213677 || F1: 0.21052631578947367
Case Insensitive : P: 0.457 || R: 0.137 || F1: 0.211
2476 Peraturan_KY_2015_2
Case Sensitive   : P: 0.2542372881355932 || R: 0.05660377358490566 || F1: 0.0925925925925926
Case Insensitive : P: 0.254 || R: 0.057 || F1: 0.093
2477 Perpres_2016_46
Case Sensitive   : P: 1.0 || R: 0.3333333333333333 || F1: 0.5
Case Insensitive : P: 1.0 || R: 0.333 || F1: 0.5
2478 Peraturan_BKN_2012_9
Case Sensitive   : P: 0.21739130434782608 || R: 0.3333333333333333 || F1: 0.26315789473684204
Case Insensitive : P: 0.217 || R: 0.333 || F1: 0.263
2479 Peraturan_LIPI_2016_12

Case Insensitive : P: 0.228 || R: 0.034 || F1: 0.059
2527 Permen_PPPA_2010_10
Case Sensitive   : P: 0.5555555555555556 || R: 0.3333333333333333 || F1: 0.4166666666666667
Case Insensitive : P: 0.556 || R: 0.333 || F1: 0.417
2528 Peraturan_BSSN_2016_16
Case Sensitive   : P: 0.11764705882352941 || R: 0.3333333333333333 || F1: 0.1739130434782609
Case Insensitive : P: 0.118 || R: 0.333 || F1: 0.174
2529 Perkab_Musi_Rawas_2005_7
Case Sensitive   : P: 1.0 || R: 0.4383561643835616 || F1: 0.6095238095238095
Case Insensitive : P: 1.0 || R: 0.438 || F1: 0.609
2530 Permen_KP_2016_28
Case Sensitive   : P: 0.0967741935483871 || R: 0.3333333333333333 || F1: 0.15000000000000002
Case Insensitive : P: 0.097 || R: 0.333 || F1: 0.15
2531 Peraturan_Ombudsman_2012_9
Case Sensitive   : P: 1.0 || R: 0.4166666666666667 || F1: 0.5882352941176471
Case Insensitive : P: 1.0 || R: 0.417 || F1: 0.589
2532 Perkab_Tanggamus_2012_01
Case Sensitive   : P: 0.8787878787878788 || R: 0.17791411042944785 || F1: 0.29591836734

2584 Permen_Hut_2009_33
Case Sensitive   : P: 0.10810810810810811 || R: 0.3333333333333333 || F1: 0.163265306122449
Case Insensitive : P: 0.108 || R: 0.333 || F1: 0.163
2585 Perprov_Riau_2013_7
Case Sensitive   : P: 0.5357142857142857 || R: 0.09554140127388536 || F1: 0.1621621621621622
Case Insensitive : P: 0.536 || R: 0.096 || F1: 0.163
2586 Permen_Dagri_2018_59
Case Sensitive   : P: 0.20833333333333334 || R: 0.3333333333333333 || F1: 0.25641025641025644
Case Insensitive : P: 0.208 || R: 0.333 || F1: 0.256
2587 Perpres_2015_149
Case Sensitive   : P: 0.22641509433962265 || R: 0.3333333333333333 || F1: 0.2696629213483146
Case Insensitive : P: 0.226 || R: 0.333 || F1: 0.269
2588 PP_2006_10
Case Sensitive   : P: 0.1 || R: 0.3333333333333333 || F1: 0.15384615384615383
Case Insensitive : P: 0.1 || R: 0.333 || F1: 0.154
2589 Perkot_Sorong_2013_12
Case Sensitive   : P: 0.16666666666666666 || R: 0.0989010989010989 || F1: 0.12413793103448273
Case Insensitive : P: 0.167 || R: 0.099 || F1: 0.124



####################################################

bfl 2 Shot

Case Sensitive
Precision: 0.4051090452872318
Recall: 0.13514390545199773
F1 Score: 0.2026755002046166

Case Insensitive
Precision: 0.40531906662097783
Recall: 0.13521396832420673
F1 Score: 0.2027805735900811


In [71]:
test_1('bfp', bf_phi, test_body, '1', 'results/metrics_bf.csv')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
1 Permen_KP_2013_5
Case Sensitive   : P: 0.12195121951219512 || R: 0.02252252252252252 || F1: 0.03802281368821293
Case Insensitive : P: 0.122 || R: 0.023 || F1: 0.039
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.25925925925925924 || R: 0.0707070707070707 || F1: 0.1111111111111111
Case Insensitive : P: 0.259 || R: 0.071 || F1: 0.111
3 Permen_Par_2015_14
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
4 Perpres_2019_67
Case Sensitive   : P: 0.9615384615384616 || R: 0.36231884057971014 || F1: 0.5263157894736843
Case Insensitive : P: 0.962 || R: 0.362 || F1: 0.526
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.22727272727272727 || R: 0.014326647564469915 || F1: 0.02695417789757413
Case Insensitive : P: 0.227 || R: 0.014 || F1: 0.026
6 Perkab_Tabalong_2010_09
Case Sensitive   : P: 0.3684210526315789 || R: 0.14893617021276595 |

Case Insensitive : P: 0.051 || R: 0.009 || F1: 0.015
58 Permen_Keu_2015_201
Case Sensitive   : P: 0.3888888888888889 || R: 0.1111111111111111 || F1: 0.1728395061728395
Case Insensitive : P: 0.389 || R: 0.111 || F1: 0.173
59 Permen_Hub_2012_36
Case Sensitive   : P: 0.0625 || R: 0.023255813953488372 || F1: 0.03389830508474576
Case Insensitive : P: 0.062 || R: 0.023 || F1: 0.034
60 Permen_Hut_2009_32
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
61 Peraturan_KPU_2018_11
Case Sensitive   : P: 0.2777777777777778 || R: 0.05 || F1: 0.08474576271186442
Case Insensitive : P: 0.278 || R: 0.05 || F1: 0.085
62 Permen_Tan_2017_49
Case Sensitive   : P: 0.25925925925925924 || R: 0.047619047619047616 || F1: 0.08045977011494253
Case Insensitive : P: 0.259 || R: 0.048 || F1: 0.081
63 Perkot_Sorong_2013_32
Case Sensitive   : P: 0.5 || R: 0.24271844660194175 || F1: 0.32679738562091504
Case Insensitive : P: 0.5 || R: 0.243 || F1: 0.327
64 Perkot_Bogor_2006_11
Cas

122 Permen_ESDM_2013_17
Case Sensitive   : P: 0.45454545454545453 || R: 0.07092198581560284 || F1: 0.12269938650306748
Case Insensitive : P: 0.455 || R: 0.071 || F1: 0.123
123 Perprov_Yogya_2001_8
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
124 Permen_Dikbud_2014_115
Case Sensitive   : P: 0.13114754098360656 || R: 0.016359918200409 || F1: 0.029090909090909094
Case Insensitive : P: 0.131 || R: 0.016 || F1: 0.029
125 Peraturan_BPKP_2016_23
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
126 Permen_Tan_2012_53
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
127 Perpres_2010_2
Case Sensitive   : P: 0.75 || R: 0.6666666666666666 || F1: 0.7058823529411765
Case Insensitive : P: 0.75 || R: 0.667 || F1: 0.706
128 Permen_Dikbud_2012_58
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
129 Peraturan_Basarnas_2017_17
Case Sensitiv

187 Permen_Bappenas_2017_14
Case Sensitive   : P: 0.14285714285714285 || R: 0.05128205128205128 || F1: 0.07547169811320754
Case Insensitive : P: 0.143 || R: 0.051 || F1: 0.075
188 PP_2013_94
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
189 Perprov_Jatim_2009_3
Case Sensitive   : P: 0.18309859154929578 || R: 0.05263157894736842 || F1: 0.08176100628930819
Case Insensitive : P: 0.183 || R: 0.053 || F1: 0.082
190 Permen_Perin_2014_56
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
191 Permen_Perin_2013_35
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
192 Peraturan_BNPP_2018_6
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
193 Permen_Dag_2017_16
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
194 Permen_Dagri_2014_59
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive 

250 UU_2019_17
Case Sensitive   : P: 0.4827586206896552 || R: 0.08484848484848485 || F1: 0.1443298969072165
Case Insensitive : P: 0.483 || R: 0.085 || F1: 0.145
251 Perpres_2018_115
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
252 Peraturan_LAN_2013_15
Case Sensitive   : P: 1.0 || R: 0.3333333333333333 || F1: 0.5
Case Insensitive : P: 1.0 || R: 0.333 || F1: 0.5
253 UU_1971_7
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
254 Permen_Kes_2017_32
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
255 Permen_Keu_2012_34
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
256 UU_2002_25
Case Sensitive   : P: 0.9655172413793104 || R: 0.358974358974359 || F1: 0.5233644859813085
Case Insensitive : P: 0.966 || R: 0.359 || F1: 0.523
257 Permen_Keu_2016_148
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0

...

Case Insensitive : P: 0.333 || R: 0.095 || F1: 0.148
2353 Permen_PUPR_2015_01
Case Sensitive   : P: 0.42857142857142855 || R: 0.07692307692307693 || F1: 0.13043478260869565
Case Insensitive : P: 0.429 || R: 0.077 || F1: 0.131
2354 PP_2019_28
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2355 Perkot_Depok_2003_10
Case Sensitive   : P: 1.0 || R: 0.27848101265822783 || F1: 0.43564356435643564
Case Insensitive : P: 1.0 || R: 0.278 || F1: 0.435
2356 Permen_Hub_2013_16
Case Sensitive   : P: 0.09230769230769231 || R: 0.045454545454545456 || F1: 0.060913705583756333
Case Insensitive : P: 0.092 || R: 0.045 || F1: 0.06
2357 Perpres_2009_42
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2358 Permen_Ristekdikti_2017_75
Case Sensitive   : P: 0.06944444444444445 || R: 0.012626262626262626 || F1: 0.021367521367521368
Case Insensitive : P: 0.069 || R: 0.013 || F1: 0.022
2359 Permen_Hut_2010_16
Case Sensitive   : P: 

2411 Peraturan_Bapeten_2019_3
Case Sensitive   : P: 0.9615384615384616 || R: 0.36231884057971014 || F1: 0.5263157894736843
Case Insensitive : P: 0.962 || R: 0.362 || F1: 0.526
2412 Peraturan_Polri_2018_4
Case Sensitive   : P: 0.44 || R: 0.13095238095238096 || F1: 0.2018348623853211
Case Insensitive : P: 0.44 || R: 0.131 || F1: 0.202
2413 UU_1953_7
Case Sensitive   : P: 0.08045977011494253 || R: 0.016203703703703703 || F1: 0.026974951830443156
Case Insensitive : P: 0.08 || R: 0.016 || F1: 0.027
2414 Permen_Kes_2016_1
Case Sensitive   : P: 1.0 || R: 0.19047619047619047 || F1: 0.32
Case Insensitive : P: 1.0 || R: 0.19 || F1: 0.319
2415 Perkot_Tasikmalaya_2007_8
Case Sensitive   : P: 0.5263157894736842 || R: 0.13513513513513514 || F1: 0.21505376344086022
Case Insensitive : P: 0.526 || R: 0.135 || F1: 0.215
2416 PP_1994_8
Case Sensitive   : P: 0.17647058823529413 || R: 0.058823529411764705 || F1: 0.08823529411764706
Case Insensitive : P: 0.176 || R: 0.059 || F1: 0.088
2417 Permen_Hub_2018_2

Case Insensitive : P: 0.9 || R: 0.158 || F1: 0.269
2470 Peraturan_BNPP_2012_3
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2471 Permen_KP_2016_30
Case Sensitive   : P: 1.0 || R: 0.2833333333333333 || F1: 0.4415584415584416
Case Insensitive : P: 1.0 || R: 0.283 || F1: 0.441
2472 Permen_Sos_2016_4
Case Sensitive   : P: 0.65625 || R: 0.1320754716981132 || F1: 0.2198952879581152
Case Insensitive : P: 0.656 || R: 0.132 || F1: 0.22
2473 Permen_Keu_2010_64
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2474 Perpres_2018_107
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2475 Peraturan_BKKBN_2016_481
Case Sensitive   : P: 0.09230769230769231 || R: 0.05128205128205128 || F1: 0.06593406593406594
Case Insensitive : P: 0.092 || R: 0.051 || F1: 0.066
2476 Peraturan_KY_2015_2
Case Sensitive   : P: 0.17142857142857143 || R: 0.045283018867924525 || F1: 0.07164179104477612


2526 Perprov_Riau_2013_17
Case Sensitive   : P: 0.171875 || R: 0.02857142857142857 || F1: 0.04899777282850779
Case Insensitive : P: 0.172 || R: 0.029 || F1: 0.05
2527 Permen_PPPA_2010_10
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2528 Peraturan_BSSN_2016_16
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2529 Perkab_Musi_Rawas_2005_7
Case Sensitive   : P: 1.0 || R: 0.2191780821917808 || F1: 0.3595505617977528
Case Insensitive : P: 1.0 || R: 0.219 || F1: 0.359
2530 Permen_KP_2016_28
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2531 Peraturan_Ombudsman_2012_9
Case Sensitive   : P: 0.96875 || R: 0.36904761904761907 || F1: 0.5344827586206897
Case Insensitive : P: 0.969 || R: 0.369 || F1: 0.534
2532 Perkab_Tanggamus_2012_01
Case Sensitive   : P: 0.19607843137254902 || R: 0.06134969325153374 || F1: 0.09345794392523364
Case Insensitive : P: 0.196 || R: 0.061 ||

2592 Peraturan_LAN_2016_5
Case Sensitive   : P: 0 || R: 0.0 || F1: 0
Case Insensitive : P: 0 || R: 0.0 || F1: 0
2593 Permen_Dagri_2011_11
Case Sensitive   : P: 1.0 || R: 0.13333333333333333 || F1: 0.23529411764705882
Case Insensitive : P: 1.0 || R: 0.133 || F1: 0.235
2594 Perkab_Ponorogo_2011_4
Case Sensitive   : P: 0.27906976744186046 || R: 0.08633093525179857 || F1: 0.13186813186813187
Case Insensitive : P: 0.279 || R: 0.086 || F1: 0.131
2595 Permen_ESDM_2009_08
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2596 UU_2010_8
Case Sensitive   : P: 0.10810810810810811 || R: 0.022792022792022793 || F1: 0.037647058823529415
Case Insensitive : P: 0.108 || R: 0.023 || F1: 0.038
2597 Perkab_Bantul_2008_15
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2598 Permen_Desa_2018_6
Case Sensitive   : P: 0.2692307692307692 || R: 0.04964539007092199 || F1: 0.08383233532934131
Case Insensitive : P: 0.269 || R: 0.05 ||

In [72]:
test_1('bfp', bf_phi, test_body, '2', 'results/metrics_bf.csv')

tes
0 Permen_Ristekdikti_2017_20
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
1 Permen_KP_2013_5
Case Sensitive   : P: 0.30434782608695654 || R: 0.03153153153153153 || F1: 0.057142857142857134
Case Insensitive : P: 0.304 || R: 0.032 || F1: 0.058
2 Permen_Keu_2011_249
Case Sensitive   : P: 0.23529411764705882 || R: 0.08080808080808081 || F1: 0.12030075187969926
Case Insensitive : P: 0.235 || R: 0.081 || F1: 0.12
3 Permen_Par_2015_14
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
4 Perpres_2019_67
Case Sensitive   : P: 0.9047619047619048 || R: 0.2753623188405797 || F1: 0.4222222222222222
Case Insensitive : P: 0.905 || R: 0.275 || F1: 0.422
5 Perkab_Sumenep_2012_4
Case Sensitive   : P: 0.07272727272727272 || R: 0.011461318051575931 || F1: 0.0198019801980198
Case Insensitive : P: 0.073 || R: 0.011 || F1: 0.019
6 Perkab_Tabalong_2010_09
Case Sensitive   : P: 0.09523809523809523 || R: 0.02127659574468085 

Case Insensitive : P: 0.058 || R: 0.009 || F1: 0.016
58 Permen_Keu_2015_201
Case Sensitive   : P: 0.375 || R: 0.09523809523809523 || F1: 0.1518987341772152
Case Insensitive : P: 0.375 || R: 0.095 || F1: 0.152
59 Permen_Hub_2012_36
Case Sensitive   : P: 0.03773584905660377 || R: 0.015503875968992248 || F1: 0.021978021978021976
Case Insensitive : P: 0.038 || R: 0.016 || F1: 0.023
60 Permen_Hut_2009_32
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
61 Peraturan_KPU_2018_11
Case Sensitive   : P: 0.13636363636363635 || R: 0.03 || F1: 0.04918032786885246
Case Insensitive : P: 0.136 || R: 0.03 || F1: 0.049
62 Permen_Tan_2017_49
Case Sensitive   : P: 0.0945945945945946 || R: 0.047619047619047616 || F1: 0.06334841628959276
Case Insensitive : P: 0.095 || R: 0.048 || F1: 0.064
63 Perkot_Sorong_2013_32
Case Sensitive   : P: 0.27906976744186046 || R: 0.11650485436893204 || F1: 0.1643835616438356
Case Insensitive : P: 0.279 || R: 0.117 || F1: 0.165
64 Perko

Case Insensitive : P: 0.5 || R: 0.113 || F1: 0.184
123 Perprov_Yogya_2001_8
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
124 Permen_Dikbud_2014_115
Case Sensitive   : P: 0.08333333333333333 || R: 0.010224948875255624 || F1: 0.01821493624772313
Case Insensitive : P: 0.083 || R: 0.01 || F1: 0.018
125 Peraturan_BPKP_2016_23
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
126 Permen_Tan_2012_53
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
127 Perpres_2010_2
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
128 Permen_Dikbud_2012_58
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
129 Peraturan_Basarnas_2017_17
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
130 Permen_ATRBPN_2018_16
Case Sensitive   : P: 0.46875 || R: 0.19230769230769232 |

187 Permen_Bappenas_2017_14
Case Sensitive   : P: 0.1267605633802817 || R: 0.057692307692307696 || F1: 0.07929515418502202
Case Insensitive : P: 0.127 || R: 0.058 || F1: 0.08
188 PP_2013_94
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
189 Perprov_Jatim_2009_3
Case Sensitive   : P: 0.2631578947368421 || R: 0.020242914979757085 || F1: 0.03759398496240601
Case Insensitive : P: 0.263 || R: 0.02 || F1: 0.037
190 Permen_Perin_2014_56
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
191 Permen_Perin_2013_35
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
192 Peraturan_BNPP_2018_6
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
193 Permen_Dag_2017_16
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
194 Permen_Dagri_2014_59
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : 

256 UU_2002_25
Case Sensitive   : P: 1.0 || R: 0.3076923076923077 || F1: 0.47058823529411764
Case Insensitive : P: 1.0 || R: 0.308 || F1: 0.471
257 Permen_Keu_2016_148
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
258 Perkot_Semarang_2004_14
Case Sensitive   : P: 0.09090909090909091 || R: 0.03680981595092025 || F1: 0.05240174672489083
Case Insensitive : P: 0.091 || R: 0.037 || F1: 0.053
259 Perprov_Jabar_2013_1
Case Sensitive   : P: 0.06944444444444445 || R: 0.013623978201634877 || F1: 0.02277904328018223
Case Insensitive : P: 0.069 || R: 0.014 || F1: 0.023
260 Permen_ESDM_2018_4
Case Sensitive   : P: 0.2 || R: 0.05925925925925926 || F1: 0.09142857142857143
Case Insensitive : P: 0.2 || R: 0.059 || F1: 0.091
261 PP_1985_32
Case Sensitive   : P: 0.7272727272727273 || R: 0.3333333333333333 || F1: 0.4571428571428572
Case Insensitive : P: 0.727 || R: 0.333 || F1: 0.457
262 Permen_Keu_2015_247
Case Sensitive   : P: 0.2727272727272727 || R: 0.044776

...

Case Insensitive : P: 0.095 || R: 0.054 || F1: 0.069
2391 UU_1957_53
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2392 Peraturan_BNPB_2010_15
Case Sensitive   : P: 0 || R: 0.0 || F1: 0
Case Insensitive : P: 0 || R: 0.0 || F1: 0
2393 Permen_Han_2014_56
Case Sensitive   : P: 0.35714285714285715 || R: 0.09803921568627451 || F1: 0.15384615384615385
Case Insensitive : P: 0.357 || R: 0.098 || F1: 0.154
2394 Peraturan_BPOM_2017_12
Case Sensitive   : P: 0.9166666666666666 || R: 0.4074074074074074 || F1: 0.5641025641025641
Case Insensitive : P: 0.917 || R: 0.407 || F1: 0.564
2395 Permen_ESDM_2014_25
Case Sensitive   : P: 0.25 || R: 0.07526881720430108 || F1: 0.11570247933884298
Case Insensitive : P: 0.25 || R: 0.075 || F1: 0.115
2396 Permen_Dagri_2016_63
Case Sensitive   : P: 0.9285714285714286 || R: 0.24074074074074073 || F1: 0.3823529411764706
Case Insensitive : P: 0.929 || R: 0.241 || F1: 0.383
2397 Peraturan_BMKG_2014_4
Case Sensitive   : P: 0.14

2448 Permen_Keu_2009_180
Case Sensitive   : P: 0.5 || R: 0.02702702702702703 || F1: 0.05128205128205129
Case Insensitive : P: 0.5 || R: 0.027 || F1: 0.051
2449 Peraturan_BPH_Migas_2013_10
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2450 Permen_Dikbud_2018_28
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2451 Peraturan_BKN_2018_9
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2452 Permen_Perin_2012_102
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2453 Perkab_Bengkayang_2005_2
Case Sensitive   : P: 0.23255813953488372 || R: 0.09345794392523364 || F1: 0.13333333333333333
Case Insensitive : P: 0.233 || R: 0.093 || F1: 0.133
2454 Perkab_Banyuwangi_2011_3
Case Sensitive   : P: 0.08888888888888889 || R: 0.015625 || F1: 0.026578073089700997
Case Insensitive : P: 0.089 || R: 0.016 || F1: 0.027
2455 Permen_Ristekdikti_20

Case Insensitive : P: 0.2 || R: 0.059 || F1: 0.091
2508 Permen_Hub_2018_86
Case Sensitive   : P: 0.20833333333333334 || R: 0.05847953216374269 || F1: 0.09132420091324199
Case Insensitive : P: 0.208 || R: 0.058 || F1: 0.091
2509 Permen_Sos_2017_21
Case Sensitive   : P: 0.42105263157894735 || R: 0.12121212121212122 || F1: 0.18823529411764706
Case Insensitive : P: 0.421 || R: 0.121 || F1: 0.188
2510 Permen_Desa_2018_2
Case Sensitive   : P: 0.109375 || R: 0.06862745098039216 || F1: 0.08433734939759037
Case Insensitive : P: 0.109 || R: 0.069 || F1: 0.085
2511 Permen_Sos_2017_30
Case Sensitive   : P: 0.1568627450980392 || R: 0.05442176870748299 || F1: 0.0808080808080808
Case Insensitive : P: 0.157 || R: 0.054 || F1: 0.08
2512 Permen_Agama_2018_4
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2513 PP_1977_24
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2514 Peraturan_LAN_2017_14
Case Sensitive   : P: 0.0 |

2569 Permen_Agama_2016_2
Case Sensitive   : P: 0.5263157894736842 || R: 0.01984126984126984 || F1: 0.03824091778202677
Case Insensitive : P: 0.526 || R: 0.02 || F1: 0.039
2570 Permenko_Kesra_2014_9
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2571 Peraturan_Basarnas_2016_2
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2572 Peraturan_Bapeten_2011_7
Case Sensitive   : P: 0.7666666666666667 || R: 0.23232323232323232 || F1: 0.3565891472868217
Case Insensitive : P: 0.767 || R: 0.232 || F1: 0.356
2573 Perpres_2019_2
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2574 Perkab_Poso_2010_9
Case Sensitive   : P: 1.0 || R: 0.45161290322580644 || F1: 0.6222222222222222
Case Insensitive : P: 1.0 || R: 0.452 || F1: 0.623
2575 UU_2007_5
Case Sensitive   : P: 0.1956521739130435 || R: 0.08571428571428572 || F1: 0.11920529801324505
Case Insensitive : P: 0.196 || R: 0.086 || 

2629 Peraturan_OJK_2014_37
Case Sensitive   : P: 0.5 || R: 0.13333333333333333 || F1: 0.2105263157894737
Case Insensitive : P: 0.5 || R: 0.133 || F1: 0.21
2630 Permen_Dag_2015_115
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2631 Perpres_2011_24
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2632 PP_1954_4
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2633 Perkab_Bantul_2000_45
Case Sensitive   : P: 0.9 || R: 0.14754098360655737 || F1: 0.2535211267605634
Case Insensitive : P: 0.9 || R: 0.148 || F1: 0.254
2634 Peraturan_BPS_2012_49
Case Sensitive   : P: 0.0 || R: 0.0 || F1: 0
Case Insensitive : P: 0.0 || R: 0.0 || F1: 0
2635 Permen_Dagri_2019_15
Case Sensitive   : P: 0.9545454545454546 || R: 0.20588235294117646 || F1: 0.33870967741935487
Case Insensitive : P: 0.955 || R: 0.206 || F1: 0.339
2636 UU_2002_10
Case Sensitive   : P: 0.7391304347826086 || R: 0.246